### Rights, Reuse, and Authorship
This work is copyright (c) the Regents of the University of Minnesota, 2018.  
It was written by Kelly Thompson from 2017-2018.

In [1]:
#Import all the necessary libraries:

# pymarc, for reading MARC & MARCXML files and parsing records
import pymarc
from pymarc import Record, Field
from pymarc import MARCReader

# pandas, for the data structures and methods
import pandas as pd

# tqdm is the library that produces the progress bars on the functions that take a long time to run
from tqdm import tqdm
tqdm.pandas(desc="Progress!")

# numpy is helpful in dealing with null value cells
import numpy as np

# re, regular expression library
import re

In [2]:
# Tell the script where your MARC data lives.  These files were exported from Alma as XML.  This is because
# otherwise the MARC record exceeds allowable size as binary output.
emarcfile = "elec-serials-full-holdings-items_new.xml"
marcfile = "phys-serials-full-holdings-items_new.xml"

In [3]:
# This function gets subfields x (ISSN) and w (OCN) of a given linking field (76X-78X)
def getxw(field, record, Related_ISSNs, Related_OCNs):
    for f in record.get_fields(field):
        if f.get_subfields('x'):
            for x in f.get_subfields('x'):
                Related_ISSNs.append(x)    
        if f.get_subfields('w'):
            for w in f.get_subfields('w'):
                if 'OCoLC' in w:
                    w = w.replace("(OCoLC)","")
                    Related_OCNs.append(w)
        return Related_ISSNs, Related_OCNs

In [4]:
def extract_from_records(records,df):
    
    # this function reads in a file of MARC records, reads and extracts data from the fields of interest,
    # and returns as a dataframe
    
    batch = len(records)
    for record in tqdm(records,desc="searching progress", total = batch, unit="records"):
        #strip extra values out of the 001 field to get just the MMS_ID (local unique system identifier)
        mms_id = str(record['001'])
        mms_id = mms_id.replace("=001  ","")
        #print(mms_id)
        
        OCN = ""
        Related_OCNs = []
        
        #OCN = OCLC Control Number; Look for 035$a with prefix (OCoLC)
        if record['035']:
            for f035 in record.get_fields('035'):
                if f035.get_subfields('a'):
                    for subfa in f035.get_subfields('a'):
                        if 'OCoLC' in subfa:
                            OCN = subfa.replace("(OCoLC)","")
                            #print(OCN)
                #get any old OCNs from any 035$z with prefix (OCoLC)
                if f035.get_subfields('z'):
                    for subfz in f035.get_subfields('z'):
                        if 'OCoLC' in subfz:
                            Related_OCNs.append(subfz.replace("(OCoLC)",""))
        else:
            # if there's no 035$a with (OCoLC), leave it blank
            OCN = ""
        
        #get any previous or merged OCNs from any 019 fields present
        if record['019']:
            for f019 in record.get_fields('019'):
                if record['019'].get_subfields('a'):
                    for suba in record['019'].get_subfields('a'):
                        Related_OCNs.append(suba)
        
        ISSN = ""
        Related_ISSNs = []
        
        #Look for an ISSN (International Standard Serial Number) in 022$a
        if record['022']:
            for f022 in record.get_fields('022'):
                if f022['a']:
                    for suba in f022.get_subfields('a'):
                        ISSN = suba
                        #print(ISSN)
                else:
                    ISSN = ""
                # 022$l = linking ISSN (ISSN-L)
                if f022['l']:
                    for subl in f022.get_subfields('l'):
                        Related_ISSNs.append(subl)
                # 022$m = Canceled ISSN-L
                if f022['m']:
                    for subm in f022.get_subfields('m'):
                        Related_ISSNs.append(subm)
                # 022$y = Incorrect ISSN
                if f022['y']:
                    for suby in f022.get_subfields('y'):
                        Related_ISSNs.append(suby)
                #022$z = Canceled ISSN
                if f022['z']:
                    for subz in f022.get_subfields('z'):
                        Related_ISSNs.append(subz)
        # if there aren't any 022 fields, leave it blank
        else:
            ISSN = ""

        #look for title fields in preferential order
        
        # Key title
        if record['222']:
            title = record['222']['a']
            #print(title)
        else:
            # Main Entry - Uniform Title
            if record['130']:
                title = record['130']['a']
                #print(title)
            else:
                # Uniform title
                if record['240']:
                    title = record['240']['a']
                    #print(title)
                else:
                    # First part of title statement
                    title = record['245']['a']
                    #print(title)
        
        #Main Series Entry 
        if record['760']:
            getxw('760', record, Related_ISSNs, Related_OCNs)
                        
        #Subseries Entry
        if record['762']:
            getxw('762', record, Related_ISSNs, Related_OCNs)
            
        #Supplement/Special Issue Entry
        if record['770']:
            getxw('770', record, Related_ISSNs, Related_OCNs)
                        
        #Supplement Parent Entry
        if record['772']:
            getxw('772', record, Related_ISSNs, Related_OCNs)
            
        #Host Item Entry
        if record['773']:
            getxw('773', record, Related_ISSNs, Related_OCNs)
                        
        #Constituent Unit Entry
        if record['774']:
            getxw('774', record, Related_ISSNs, Related_OCNs)
            
        #Other Edition Entry
        if record['775']:
            getxw('775', record, Related_ISSNs, Related_OCNs)
            
        #Additional Physical Form Entry
        if record['776']:
            getxw('776', record, Related_ISSNs, Related_OCNs)
            
        #Issued With Entry
        if record['777']:
            getxw('777', record, Related_ISSNs, Related_OCNs)
        
        #Preceding Entry
        if record['780']:
            getxw('780', record, Related_ISSNs, Related_OCNs)
          
        #Succeeding Entry
        if record['785']:
            getxw('785', record, Related_ISSNs, Related_OCNs)
            
        #Other Relationship Entry
        if record['787']:
            getxw('787', record, Related_ISSNs, Related_OCNs)
        
        #print(Related_ISSNs)
        #print(Related_OCNs)
        Related_ISSNs = list(set(Related_ISSNs))
        Related_OCNs = list(set(Related_OCNs))

        #print(Related_ISSNs)
        #print(Related_OCNs)
        #print()
        
        Holding_IDs = []
        barcodes = []
        enum = []
        chron = []
        descr = []

        if record['954']:
            for f954 in record.get_fields('954'):
                if f954['a']:
                    for suba in f954.get_subfields('a'):
                        Holding_IDs.append(suba)
                        
                if f954['b']:
                    for subb in f954.get_subfields('b'):
                        barcodes.append(subb)

                if f954['e']:
                    for sube in f954.get_subfields('e'):
                        enum.append(sube)

                if f954['g']:
                    for subg in f954.get_subfields('g'):
                        chron.append(subg)

                if f954['i']:
                    for subi in f954.get_subfields('i'):
                        descr.append(subi)
        
        e_holdings = []
        if record['955']:
            for f955 in record.get_fields('955'):
                for subfg in f955.get_subfields('g'):
                    e_holdings.append(subfg)
        
        
        # compile all the values you just extracted into a row to be appended onto a dataframe
        row = [mms_id, title, OCN, ISSN, Related_OCNs, Related_ISSNs, Holding_IDs, enum, chron, descr, barcodes, e_holdings]
        
        # create a mini dataframe of your row you just created
        df2 = pd.DataFrame([row], columns=headerrow)
        #print(df2)
        
        # append your new mini dataframe to the big dataframe
        df = df.append(df2,ignore_index=True)

    #Split any multi-valued OCNs or ISSNs that might have semicolons (this has only been tested when reading in a spreadsheet of values, not in reading actual MARC, since we're only taking one OCN and ISSN)
    df.OCN = df.OCN.str.split(";")
    df.ISSN = df.ISSN.str.split(";")

    return df

In [5]:
# Because the records were output as MARCXML, not binary MARC, we have to use pymarc to parse the XML into something it can
# process as MARC records.

e_records = pymarc.parse_xml_to_array(emarcfile)
p_records = pymarc.parse_xml_to_array(marcfile)

In [6]:
# Define what your header row will be for the dataframe output you are going to put your MARC data in
headerrow = ['MMS_ID', 'Title', 'OCN','ISSN','Related_OCNs','Related_ISSNs', 'Holding ID','enum','chron','descr','barcodes', 'e_holdings']
#headerrow = ['MMS_ID', 'Title', 'OCN','ISSN','Related_OCNs','Related_ISSNs']

# Create empty dataframes to put your data in.
e_df = pd.DataFrame(columns=headerrow)
print(e_df)
p_df = pd.DataFrame(columns=headerrow)
p_df

Empty DataFrame
Columns: [MMS_ID, Title, OCN, ISSN, Related_OCNs, Related_ISSNs, Holding ID, enum, chron, descr, barcodes, e_holdings]
Index: []


Empty DataFrame
Columns: [MMS_ID, Title, OCN, ISSN, Related_OCNs, Related_ISSNs, Holding ID, enum, chron, descr, barcodes, e_holdings]
Index: []

In [7]:
# Extract data from the records for electronic resources
e_df = extract_from_records(e_records, e_df)

searching progress: 100%|██████████████████████████████████████████████████| 48028/48028 [07:57<00:00, 100.62records/s]


In [8]:
# Extract data from the records for physical resources
p_df = extract_from_records(p_records, p_df)

searching progress: 100%|███████████████████████████████████████████████████| 99295/99295 [37:46<00:00, 43.81records/s]


In [9]:
# How big is our E dataset?
e_df.shape

(48028, 12)

In [10]:
# How big is our P dataset?
p_df.shape

(99295, 12)

In [12]:
# It took a long time to get that data into a format we can use, so save it as a pickle (.pkl) file so we can just instantly
# read it back into our notebook if we have to stop here and come back.

e_df.to_pickle('e_df.pkl')
p_df.to_pickle('p_df.pkl')

In [13]:
# Either run this or the commented line, depending on if you just created the e_df dataframe, or if you are starting the script in the middle.
#edf = pd.read_pickle('e_df.pkl')
edf = e_df
edf

MMS_ID                                              Title  \
0      9974125338401701                            The Banner of the Cross   
1      9974125400901701                             The Cabinet of Freedom   
2      9974125335601701                                    The Boston spy.   
3      9974125600601701  Rudolph Garrigue's Monthly Bulletin of German ...   
4      9974125417001701         Kirkelig tidende et Luthersk maanedsskrift   
5      9974125495201701  Mobile Literary Gazette: Devoted to Literature...   
6      9974125496001701  Miss Leslie's Magazine or The Home Book of Lit...   
7      9974125410201701                               Mt. Auburn memorial.   
8      9974125374801701                     Mrs. Colvin's Weekly Messenger   
9      9974125319501701  Expounder of Primitive Christianity: Devoted t...   
10     9974125315001701  Gazette of the Union Golden Rule and Odd Fello...   
11     9974125311101701       Hesperian, The, or, Western Monthly Magazine   
12     9974125334001701                     Boys' and Girls' Penny Journal   
13     9974375039001701  Reports of cases at law and in equity, argued ...   
14     9974375166601701          Report of the Attorney General of Arizona   
15     9974375156601701  Opinions of the Attorney General of the state ...   
16     9974375124101701                         Senate journal, New Mexico   
17     9974375172401701                        Arkansas reports, annotated   
18     9974375035601701                          Oklahoma reports (Online)   
19     9974375171101701  Chrostwaite's Pennsylvania municipal law reporter   
20     9974375165301701                                   Sessional papers   
21     9974141884501701                   Control Conference (ICC), Indian   
22     9974125357401701                                             Sprite   
23     9974125603501701                                     Polish eaglet.   
24     9974125456701701                                        The sunbeam   
25     9974125491801701                Musical review and choral advocate.   
26     9974125289501701                               The Centennial Eagle   
27     9974125266801701             The journal of the Franklin Institute    
28     9974125286501701                                        The citadel   
29     9974125240801701  The Quarterly of the Young Men's Christian Ass...   
...                 ...                                                ...   
47998  9968419300001701                             Strategic outsourcing.   
47999  9968623500001701                         Studies in the Renaissance   
48000  9968623930001701                  Advocate of peace through justice   
48001  9968244930001701   IEEE International Conference on Neural Networks   
48002  9968634630001701                  Niles' national register (Online)   
48003  9968212110001701                               Museum international   
48004  9968518660001701       Journal of plant nutrition and soil science.   
48005  9968159130001701                      Fette, Seifen, Anstrichmittel   
48006  9968426800001701  IRE transactions on aeronautical and navigatio...   
48007  9968274250001701         Mechanics of cohesive-frictional materials   
48008  9968439710001701  Journal of the Society of Motion Picture Engin...   
48009  9968645490001701  Revue d'histoire de la deuxième guerre mondial...   
48010  9968386210001701         International journal of vegetable science   
48011  9968318900001701                         The Edgar Allan Poe review   
48012  9968620360001701       Progress in tourism and hospitality research   
48013  9968472800001701        Agricultural and forest entomology (Online)   
48014  9968591580001701  European journal on criminal policy and resear...   
48015  9968569050001701  Software Process, International Conference on the   
48016  9968570970001701  Recent Advances in Microwave Theory and Applic...   
48017  9968469490001701  Multimedia Com

In [14]:
# Either run this or the commented line, depending on if you just created the p_df dataframe, or if you are starting the script in the middle.
#pdf = pd.read_pickle('p_df.pkl')
pdf = p_df
pdf

MMS_ID                                              Title  \
0      9913162530001701                Annual review of chronopharmacology   
1      9912286510001701  Annual report on inheritance and improvement o...   
2      9912380980001701  Station list of officers of Medical Department...   
3      9912842260001701          Regional conference series in mathematics   
4      9913436020001701                              Journal of glaciology   
5      9913837990001701        Studies in Cistercian art and architecture.   
6      9912739540001701                The Agricultural education magazine   
7      9913448360001701                                    Gothic studies.   
8      9913436980001701                                Internet @ schools.   
9      9913216420001701                                   Aquatic insects.   
10     9913415620001701      Journal of muscle research and cell motility.   
11     9913396060001701                                  Spazio e società   
12     9912841300001701                             Compositio mathematica   
13     9912758800001701                           Annali di architettura :   
14     9913176500001701  Acta crystallographica. Section A. Foundations...   
15     9912749160001701                          Social science & medicine   
16     9913383290001701  Research quarterly of the American Association...   
17     9913442920001701                                     Screen digest.   
18     9913442120001701                          Sociology of the sciences   
19     9912741930001701  Annual statistical digest (Castries, Saint Lucia)   
20     9913884430001701                     Magyar statistikai évkönyv =   
21     9913907650001701                  Vestnik Moskovskogo universiteta.   
22     9913448660001701                                  Larousse mensuel.   
23     9913300500001701                                Fieldstaff reports.   
24     9913226960001701                            Bulletin signalétique.   
25     9913219080001701                                    Årsberetning /   
26     9913220260001701   Arthropods of Florida and neighboring land areas   
27     9913168330001701  Annual report of the State Oil and Gas Supervisor   
28     9913184460001701                    Archivio per le scienze mediche   
29     9913134380001701  The Mercantile Agency reference book for the B...   
...                 ...                                                ...   
99265  9963076860001701                             Country profile. Malta   
99266  9963135770001701                Rock mechanics and rock engineering   
99267  9963097840001701                               The Social frontier.   
99268  9963095330001701  Library and reference facilities in the area o...   
99269  9962898650001701  Comparative statements of cash disbursements b...   
99270  9962886880001701  Monograph (University of California, Berkeley....   
99271  9962886180001701                    Agriculture, the third century.   
99272  9962378370001701                                  Neues Abendland ;   
99273  9961859470001701                               Statistical summary.   
99274  9965926900001701             BP statistical review of world energy.   
99275  9965934940001701                                 California design.   
99276  9973295993501701            Data sheets for ordnance type materiel.   
99277  9972960920001701  Direct and general support and depot maintenan...   
99278  9973345108901701                                Operator's manual :   
99279  9972598080001701  Direct and general support and depot maintenan...   
99280  9972960990001701           Operator's and unit maintenance manual :   
99281  9972598010001701  Operator, organizational, direct and general s...   
99282  9972960280001701  Operator's, unit, intermediate direct support,...   
99283  9973345099501701  Operator and organizational maintenance manual...   
99284  9964736970001701                

In [15]:
# Because the MARC records have ISSN and OCN data that relates to the described work AS WELL AS potentially having ISSN and
# OCN data for related works in 76X, 77X, or 78X fields, we want to get all of those potential match points into a glob so
# we can match against any of them at the same level.  

edf['OCN_cluster'] = edf.progress_apply(lambda row: list(set(row['Related_OCNs'] + [x for x in row['OCN'] if x != ""])), axis=1)
edf['ISSN_cluster'] = edf.progress_apply(lambda row: list(set(row['Related_ISSNs'] + [x for x in row['ISSN'] if x != ""])), axis=1)
edf['OCN_cluster'] = edf.progress_apply(lambda row: list(set([x for x in row['OCN_cluster'] if x != ""])), axis=1)
edf['ISSN_cluster'] = edf.progress_apply(lambda row: list(set([x for x in row['ISSN_cluster'] if x != ""])), axis=1)
edf

Progress!: 100%|██████████████████████████████████████████████████████████████| 48028/48028 [00:00<00:00, 64030.33it/s]


MMS_ID                                              Title  \
0      9974125338401701                            The Banner of the Cross   
1      9974125400901701                             The Cabinet of Freedom   
2      9974125335601701                                    The Boston spy.   
3      9974125600601701  Rudolph Garrigue's Monthly Bulletin of German ...   
4      9974125417001701         Kirkelig tidende et Luthersk maanedsskrift   
5      9974125495201701  Mobile Literary Gazette: Devoted to Literature...   
6      9974125496001701  Miss Leslie's Magazine or The Home Book of Lit...   
7      9974125410201701                               Mt. Auburn memorial.   
8      9974125374801701                     Mrs. Colvin's Weekly Messenger   
9      9974125319501701  Expounder of Primitive Christianity: Devoted t...   
10     9974125315001701  Gazette of the Union Golden Rule and Odd Fello...   
11     9974125311101701       Hesperian, The, or, Western Monthly Magazine   
12     9974125334001701                     Boys' and Girls' Penny Journal   
13     9974375039001701  Reports of cases at law and in equity, argued ...   
14     9974375166601701          Report of the Attorney General of Arizona   
15     9974375156601701  Opinions of the Attorney General of the state ...   
16     9974375124101701                         Senate journal, New Mexico   
17     9974375172401701                        Arkansas reports, annotated   
18     9974375035601701                          Oklahoma reports (Online)   
19     9974375171101701  Chrostwaite's Pennsylvania municipal law reporter   
20     9974375165301701                                   Sessional papers   
21     9974141884501701                   Control Conference (ICC), Indian   
22     9974125357401701                                             Sprite   
23     9974125603501701                                     Polish eaglet.   
24     9974125456701701                                        The sunbeam   
25     9974125491801701                Musical review and choral advocate.   
26     9974125289501701                               The Centennial Eagle   
27     9974125266801701             The journal of the Franklin Institute    
28     9974125286501701                                        The citadel   
29     9974125240801701  The Quarterly of the Young Men's Christian Ass...   
...                 ...                                                ...   
47998  9968419300001701                             Strategic outsourcing.   
47999  9968623500001701                         Studies in the Renaissance   
48000  9968623930001701                  Advocate of peace through justice   
48001  9968244930001701   IEEE International Conference on Neural Networks   
48002  9968634630001701                  Niles' national register (Online)   
48003  9968212110001701                               Museum international   
48004  9968518660001701       Journal of plant nutrition and soil science.   
48005  9968159130001701                      Fette, Seifen, Anstrichmittel   
48006  9968426800001701  IRE transactions on aeronautical and navigatio...   
48007  9968274250001701         Mechanics of cohesive-frictional materials   
48008  9968439710001701  Journal of the Society of Motion Picture Engin...   
48009  9968645490001701  Revue d'histoire de la deuxième guerre mondial...   
48010  9968386210001701         International journal of vegetable science   
48011  9968318900001701                         The Edgar Allan Poe review   
48012  9968620360001701       Progress in tourism and hospitality research   
48013  9968472800001701        Agricultural and forest entomology (Online)   
48014  9968591580001701  European journal on criminal policy and resear...   
48015  9968569050001701  Software Process, International Conference on the   
48016  9968570970001701  Recent Advances in Microwave Theory and Applic...   
48017  9968469490001701  Multimedia Com

In [16]:
pdf['OCN_cluster'] = pdf.progress_apply(lambda row: list(set(row['Related_OCNs'] + [x for x in row['OCN'] if x != ""])), axis=1)
pdf['ISSN_cluster'] = pdf.progress_apply(lambda row: list(set(row['Related_ISSNs'] + [x for x in row['ISSN'] if x != ""])), axis=1)
pdf['OCN_cluster'] = pdf.progress_apply(lambda row: list(set([x for x in row['OCN_cluster'] if x != ""])), axis=1)
pdf['ISSN_cluster'] = pdf.progress_apply(lambda row: list(set([x for x in row['ISSN_cluster'] if x != ""])), axis=1)
pdf

Progress!: 100%|██████████████████████████████████████████████████████████████| 99295/99295 [00:01<00:00, 66217.44it/s]


MMS_ID                                              Title  \
0      9913162530001701                Annual review of chronopharmacology   
1      9912286510001701  Annual report on inheritance and improvement o...   
2      9912380980001701  Station list of officers of Medical Department...   
3      9912842260001701          Regional conference series in mathematics   
4      9913436020001701                              Journal of glaciology   
5      9913837990001701        Studies in Cistercian art and architecture.   
6      9912739540001701                The Agricultural education magazine   
7      9913448360001701                                    Gothic studies.   
8      9913436980001701                                Internet @ schools.   
9      9913216420001701                                   Aquatic insects.   
10     9913415620001701      Journal of muscle research and cell motility.   
11     9913396060001701                                  Spazio e società   
12     9912841300001701                             Compositio mathematica   
13     9912758800001701                           Annali di architettura :   
14     9913176500001701  Acta crystallographica. Section A. Foundations...   
15     9912749160001701                          Social science & medicine   
16     9913383290001701  Research quarterly of the American Association...   
17     9913442920001701                                     Screen digest.   
18     9913442120001701                          Sociology of the sciences   
19     9912741930001701  Annual statistical digest (Castries, Saint Lucia)   
20     9913884430001701                     Magyar statistikai évkönyv =   
21     9913907650001701                  Vestnik Moskovskogo universiteta.   
22     9913448660001701                                  Larousse mensuel.   
23     9913300500001701                                Fieldstaff reports.   
24     9913226960001701                            Bulletin signalétique.   
25     9913219080001701                                    Årsberetning /   
26     9913220260001701   Arthropods of Florida and neighboring land areas   
27     9913168330001701  Annual report of the State Oil and Gas Supervisor   
28     9913184460001701                    Archivio per le scienze mediche   
29     9913134380001701  The Mercantile Agency reference book for the B...   
...                 ...                                                ...   
99265  9963076860001701                             Country profile. Malta   
99266  9963135770001701                Rock mechanics and rock engineering   
99267  9963097840001701                               The Social frontier.   
99268  9963095330001701  Library and reference facilities in the area o...   
99269  9962898650001701  Comparative statements of cash disbursements b...   
99270  9962886880001701  Monograph (University of California, Berkeley....   
99271  9962886180001701                    Agriculture, the third century.   
99272  9962378370001701                                  Neues Abendland ;   
99273  9961859470001701                               Statistical summary.   
99274  9965926900001701             BP statistical review of world energy.   
99275  9965934940001701                                 California design.   
99276  9973295993501701            Data sheets for ordnance type materiel.   
99277  9972960920001701  Direct and general support and depot maintenan...   
99278  9973345108901701                                Operator's manual :   
99279  9972598080001701  Direct and general support and depot maintenan...   
99280  9972960990001701           Operator's and unit maintenance manual :   
99281  9972598010001701  Operator, organizational, direct and general s...   
99282  9972960280001701  Operator's, unit, intermediate direct support,...   
99283  9973345099501701  Operator and organizational maintenance manual...   
99284  9964736970001701                

In [17]:
# We want to use some regular expressions to remove data that doesn't conform to the format we would expect for ISSNs.

import re
rmv_period = re.compile(r'^[0-9Xx]{4}\-[0-9Xx]{4}\.$')
regex = re.compile(r'^[0-9Xx]{4}\-[0-9Xx]{4}$')

In [18]:
sum(edf['ISSN_cluster'].apply(lambda x: len(x)))

52648

In [19]:
sum(pdf['ISSN_cluster'].apply(lambda x: len(x)))

75670

In [20]:
edf['ISSN_cluster'] = edf.apply(lambda row: list(set([rmv_period.sub(issn[:-1], issn) for issn in row['ISSN_cluster']])), axis=1)
edf['ISSN_cluster'] = edf.apply(lambda row: list(filter(regex.search, row['ISSN_cluster'])), axis=1)
edf

MMS_ID                                              Title  \
0      9974125338401701                            The Banner of the Cross   
1      9974125400901701                             The Cabinet of Freedom   
2      9974125335601701                                    The Boston spy.   
3      9974125600601701  Rudolph Garrigue's Monthly Bulletin of German ...   
4      9974125417001701         Kirkelig tidende et Luthersk maanedsskrift   
5      9974125495201701  Mobile Literary Gazette: Devoted to Literature...   
6      9974125496001701  Miss Leslie's Magazine or The Home Book of Lit...   
7      9974125410201701                               Mt. Auburn memorial.   
8      9974125374801701                     Mrs. Colvin's Weekly Messenger   
9      9974125319501701  Expounder of Primitive Christianity: Devoted t...   
10     9974125315001701  Gazette of the Union Golden Rule and Odd Fello...   
11     9974125311101701       Hesperian, The, or, Western Monthly Magazine   
12     9974125334001701                     Boys' and Girls' Penny Journal   
13     9974375039001701  Reports of cases at law and in equity, argued ...   
14     9974375166601701          Report of the Attorney General of Arizona   
15     9974375156601701  Opinions of the Attorney General of the state ...   
16     9974375124101701                         Senate journal, New Mexico   
17     9974375172401701                        Arkansas reports, annotated   
18     9974375035601701                          Oklahoma reports (Online)   
19     9974375171101701  Chrostwaite's Pennsylvania municipal law reporter   
20     9974375165301701                                   Sessional papers   
21     9974141884501701                   Control Conference (ICC), Indian   
22     9974125357401701                                             Sprite   
23     9974125603501701                                     Polish eaglet.   
24     9974125456701701                                        The sunbeam   
25     9974125491801701                Musical review and choral advocate.   
26     9974125289501701                               The Centennial Eagle   
27     9974125266801701             The journal of the Franklin Institute    
28     9974125286501701                                        The citadel   
29     9974125240801701  The Quarterly of the Young Men's Christian Ass...   
...                 ...                                                ...   
47998  9968419300001701                             Strategic outsourcing.   
47999  9968623500001701                         Studies in the Renaissance   
48000  9968623930001701                  Advocate of peace through justice   
48001  9968244930001701   IEEE International Conference on Neural Networks   
48002  9968634630001701                  Niles' national register (Online)   
48003  9968212110001701                               Museum international   
48004  9968518660001701       Journal of plant nutrition and soil science.   
48005  9968159130001701                      Fette, Seifen, Anstrichmittel   
48006  9968426800001701  IRE transactions on aeronautical and navigatio...   
48007  9968274250001701         Mechanics of cohesive-frictional materials   
48008  9968439710001701  Journal of the Society of Motion Picture Engin...   
48009  9968645490001701  Revue d'histoire de la deuxième guerre mondial...   
48010  9968386210001701         International journal of vegetable science   
48011  9968318900001701                         The Edgar Allan Poe review   
48012  9968620360001701       Progress in tourism and hospitality research   
48013  9968472800001701        Agricultural and forest entomology (Online)   
48014  9968591580001701  European journal on criminal policy and resear...   
48015  9968569050001701  Software Process, International Conference on the   
48016  9968570970001701  Recent Advances in Microwave Theory and Applic...   
48017  9968469490001701  Multimedia Com

In [21]:
print(sum(edf['ISSN_cluster'].apply(lambda x: len(x))))
print(sum(edf['OCN_cluster'].apply(lambda x: len(x))))

52637
42129


In [22]:
pdf['ISSN_cluster'] = pdf.apply(lambda row: list(set([rmv_period.sub(issn[:-1], issn) for issn in row['ISSN_cluster']])), axis=1)
pdf['ISSN_cluster'] = pdf.apply(lambda row: list(filter(regex.search, row['ISSN_cluster'])), axis=1)
pdf

MMS_ID                                              Title  \
0      9913162530001701                Annual review of chronopharmacology   
1      9912286510001701  Annual report on inheritance and improvement o...   
2      9912380980001701  Station list of officers of Medical Department...   
3      9912842260001701          Regional conference series in mathematics   
4      9913436020001701                              Journal of glaciology   
5      9913837990001701        Studies in Cistercian art and architecture.   
6      9912739540001701                The Agricultural education magazine   
7      9913448360001701                                    Gothic studies.   
8      9913436980001701                                Internet @ schools.   
9      9913216420001701                                   Aquatic insects.   
10     9913415620001701      Journal of muscle research and cell motility.   
11     9913396060001701                                  Spazio e società   
12     9912841300001701                             Compositio mathematica   
13     9912758800001701                           Annali di architettura :   
14     9913176500001701  Acta crystallographica. Section A. Foundations...   
15     9912749160001701                          Social science & medicine   
16     9913383290001701  Research quarterly of the American Association...   
17     9913442920001701                                     Screen digest.   
18     9913442120001701                          Sociology of the sciences   
19     9912741930001701  Annual statistical digest (Castries, Saint Lucia)   
20     9913884430001701                     Magyar statistikai évkönyv =   
21     9913907650001701                  Vestnik Moskovskogo universiteta.   
22     9913448660001701                                  Larousse mensuel.   
23     9913300500001701                                Fieldstaff reports.   
24     9913226960001701                            Bulletin signalétique.   
25     9913219080001701                                    Årsberetning /   
26     9913220260001701   Arthropods of Florida and neighboring land areas   
27     9913168330001701  Annual report of the State Oil and Gas Supervisor   
28     9913184460001701                    Archivio per le scienze mediche   
29     9913134380001701  The Mercantile Agency reference book for the B...   
...                 ...                                                ...   
99265  9963076860001701                             Country profile. Malta   
99266  9963135770001701                Rock mechanics and rock engineering   
99267  9963097840001701                               The Social frontier.   
99268  9963095330001701  Library and reference facilities in the area o...   
99269  9962898650001701  Comparative statements of cash disbursements b...   
99270  9962886880001701  Monograph (University of California, Berkeley....   
99271  9962886180001701                    Agriculture, the third century.   
99272  9962378370001701                                  Neues Abendland ;   
99273  9961859470001701                               Statistical summary.   
99274  9965926900001701             BP statistical review of world energy.   
99275  9965934940001701                                 California design.   
99276  9973295993501701            Data sheets for ordnance type materiel.   
99277  9972960920001701  Direct and general support and depot maintenan...   
99278  9973345108901701                                Operator's manual :   
99279  9972598080001701  Direct and general support and depot maintenan...   
99280  9972960990001701           Operator's and unit maintenance manual :   
99281  9972598010001701  Operator, organizational, direct and general s...   
99282  9972960280001701  Operator's, unit, intermediate direct support,...   
99283  9973345099501701  Operator and organizational maintenance manual...   
99284  9964736970001701                

In [23]:
print(sum(pdf['ISSN_cluster'].apply(lambda x: len(x))))
print(sum(pdf['OCN_cluster'].apply(lambda x: len(x))))

75446
159692


In [24]:
# We also want to remove any OCN-like data that might be in an ISSN field
lcno = re.compile(r'.*\(DLC\).*')

edf['ISSN_cluster'] = edf.apply(lambda row: list(set([i for i in row['ISSN_cluster'] if not lcno.search(i)])), axis=1)
edf['OCN_cluster'] = edf.apply(lambda row: list(set([i for i in row['OCN_cluster'] if not lcno.search(i)])), axis=1)

In [25]:
lcno = re.compile(r'.*\(DLC\).*')

pdf['ISSN_cluster'] = pdf.apply(lambda row: list(set([i for i in row['ISSN_cluster'] if not lcno.search(i)])), axis=1)
pdf['OCN_cluster'] = pdf.apply(lambda row: list(set([i for i in row['OCN_cluster'] if not lcno.search(i)])), axis=1)

In [26]:
# Clean up any extra prefixes in the OCN data that would lead to false negatives in matching
edf['OCN_cluster'] = edf.apply(lambda row: list(set([a.replace("ocm","").replace("OCM","").replace("ocn","").replace("OCN","").strip() for a in row['OCN_cluster']])), axis = 1)

In [27]:
pdf['OCN_cluster'] = pdf.apply(lambda row: list(set([a.replace("ocm","").replace("OCM","").replace("ocn","").replace("OCN","").strip() for a in row['OCN_cluster']])), axis = 1)

In [28]:
print(sum(edf['OCN_cluster'].apply(lambda x: len(x))))

42129


In [29]:
print(sum(pdf['OCN_cluster'].apply(lambda x: len(x))))

159634


In [30]:
# Moving forward, we really only need a subset of the data we've amassed, so select the columns we're going to work with now.

edf2 = edf[['MMS_ID','Title','OCN','ISSN','OCN_cluster','ISSN_cluster','e_holdings']]
#edf2 = edf[['MMS_ID','Title','OCN_cluster','ISSN_cluster']]
edf2

MMS_ID                                              Title  \
0      9974125338401701                            The Banner of the Cross   
1      9974125400901701                             The Cabinet of Freedom   
2      9974125335601701                                    The Boston spy.   
3      9974125600601701  Rudolph Garrigue's Monthly Bulletin of German ...   
4      9974125417001701         Kirkelig tidende et Luthersk maanedsskrift   
5      9974125495201701  Mobile Literary Gazette: Devoted to Literature...   
6      9974125496001701  Miss Leslie's Magazine or The Home Book of Lit...   
7      9974125410201701                               Mt. Auburn memorial.   
8      9974125374801701                     Mrs. Colvin's Weekly Messenger   
9      9974125319501701  Expounder of Primitive Christianity: Devoted t...   
10     9974125315001701  Gazette of the Union Golden Rule and Odd Fello...   
11     9974125311101701       Hesperian, The, or, Western Monthly Magazine   
12     9974125334001701                     Boys' and Girls' Penny Journal   
13     9974375039001701  Reports of cases at law and in equity, argued ...   
14     9974375166601701          Report of the Attorney General of Arizona   
15     9974375156601701  Opinions of the Attorney General of the state ...   
16     9974375124101701                         Senate journal, New Mexico   
17     9974375172401701                        Arkansas reports, annotated   
18     9974375035601701                          Oklahoma reports (Online)   
19     9974375171101701  Chrostwaite's Pennsylvania municipal law reporter   
20     9974375165301701                                   Sessional papers   
21     9974141884501701                   Control Conference (ICC), Indian   
22     9974125357401701                                             Sprite   
23     9974125603501701                                     Polish eaglet.   
24     9974125456701701                                        The sunbeam   
25     9974125491801701                Musical review and choral advocate.   
26     9974125289501701                               The Centennial Eagle   
27     9974125266801701             The journal of the Franklin Institute    
28     9974125286501701                                        The citadel   
29     9974125240801701  The Quarterly of the Young Men's Christian Ass...   
...                 ...                                                ...   
47998  9968419300001701                             Strategic outsourcing.   
47999  9968623500001701                         Studies in the Renaissance   
48000  9968623930001701                  Advocate of peace through justice   
48001  9968244930001701   IEEE International Conference on Neural Networks   
48002  9968634630001701                  Niles' national register (Online)   
48003  9968212110001701                               Museum international   
48004  9968518660001701       Journal of plant nutrition and soil science.   
48005  9968159130001701                      Fette, Seifen, Anstrichmittel   
48006  9968426800001701  IRE transactions on aeronautical and navigatio...   
48007  9968274250001701         Mechanics of cohesive-frictional materials   
48008  9968439710001701  Journal of the Society of Motion Picture Engin...   
48009  9968645490001701  Revue d'histoire de la deuxième guerre mondial...   
48010  9968386210001701         International journal of vegetable science   
48011  9968318900001701                         The Edgar Allan Poe review   
48012  9968620360001701       Progress in tourism and hospitality research   
48013  9968472800001701        Agricultural and forest entomology (Online)   
48014  9968591580001701  European journal on criminal policy and resear...   
48015  9968569050001701  Software Process, International Conference on the   
48016  9968570970001701  Recent Advances in Microwave Theory and Applic...   
48017  9968469490001701  Multimedia Com

In [31]:
edf2.to_pickle('edf2-20180516.pkl')

In [32]:
pdf2 = pdf[['MMS_ID','Title','OCN','ISSN','OCN_cluster','ISSN_cluster','enum','chron','descr']]
#pdf2 = pdf[['MMS_ID','Title','OCN_cluster','ISSN_cluster']]
pdf2

MMS_ID                                              Title  \
0      9913162530001701                Annual review of chronopharmacology   
1      9912286510001701  Annual report on inheritance and improvement o...   
2      9912380980001701  Station list of officers of Medical Department...   
3      9912842260001701          Regional conference series in mathematics   
4      9913436020001701                              Journal of glaciology   
5      9913837990001701        Studies in Cistercian art and architecture.   
6      9912739540001701                The Agricultural education magazine   
7      9913448360001701                                    Gothic studies.   
8      9913436980001701                                Internet @ schools.   
9      9913216420001701                                   Aquatic insects.   
10     9913415620001701      Journal of muscle research and cell motility.   
11     9913396060001701                                  Spazio e società   
12     9912841300001701                             Compositio mathematica   
13     9912758800001701                           Annali di architettura :   
14     9913176500001701  Acta crystallographica. Section A. Foundations...   
15     9912749160001701                          Social science & medicine   
16     9913383290001701  Research quarterly of the American Association...   
17     9913442920001701                                     Screen digest.   
18     9913442120001701                          Sociology of the sciences   
19     9912741930001701  Annual statistical digest (Castries, Saint Lucia)   
20     9913884430001701                     Magyar statistikai évkönyv =   
21     9913907650001701                  Vestnik Moskovskogo universiteta.   
22     9913448660001701                                  Larousse mensuel.   
23     9913300500001701                                Fieldstaff reports.   
24     9913226960001701                            Bulletin signalétique.   
25     9913219080001701                                    Årsberetning /   
26     9913220260001701   Arthropods of Florida and neighboring land areas   
27     9913168330001701  Annual report of the State Oil and Gas Supervisor   
28     9913184460001701                    Archivio per le scienze mediche   
29     9913134380001701  The Mercantile Agency reference book for the B...   
...                 ...                                                ...   
99265  9963076860001701                             Country profile. Malta   
99266  9963135770001701                Rock mechanics and rock engineering   
99267  9963097840001701                               The Social frontier.   
99268  9963095330001701  Library and reference facilities in the area o...   
99269  9962898650001701  Comparative statements of cash disbursements b...   
99270  9962886880001701  Monograph (University of California, Berkeley....   
99271  9962886180001701                    Agriculture, the third century.   
99272  9962378370001701                                  Neues Abendland ;   
99273  9961859470001701                               Statistical summary.   
99274  9965926900001701             BP statistical review of world energy.   
99275  9965934940001701                                 California design.   
99276  9973295993501701            Data sheets for ordnance type materiel.   
99277  9972960920001701  Direct and general support and depot maintenan...   
99278  9973345108901701                                Operator's manual :   
99279  9972598080001701  Direct and general support and depot maintenan...   
99280  9972960990001701           Operator's and unit maintenance manual :   
99281  9972598010001701  Operator, organizational, direct and general s...   
99282  9972960280001701  Operator's, unit, intermediate direct support,...   
99283  9973345099501701  Operator and organizational maintenance manual...   
99284  9964736970001701                

In [33]:
pdf2.to_pickle('pdf-20180516.pkl')

In [ ]:
pdf2 = pd.read_pickle('pdf_test.pkl')

In [ ]:
#edf2['ISSN_cluster'].apply(pd.Series)

In [ ]:
edf2 = pd.read_pickle('edf_test.pkl')
edf2

In [34]:
# We're going to combine our P and E dataframes into one for the clustering, but we want to be able to easily separate them
# back out again.  Initiate and fill a new column for this purpose.

edf2['p_or_e'] = 'e'
edf2

C:\Users\kjthomps\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.


MMS_ID                                              Title  \
0      9974125338401701                            The Banner of the Cross   
1      9974125400901701                             The Cabinet of Freedom   
2      9974125335601701                                    The Boston spy.   
3      9974125600601701  Rudolph Garrigue's Monthly Bulletin of German ...   
4      9974125417001701         Kirkelig tidende et Luthersk maanedsskrift   
5      9974125495201701  Mobile Literary Gazette: Devoted to Literature...   
6      9974125496001701  Miss Leslie's Magazine or The Home Book of Lit...   
7      9974125410201701                               Mt. Auburn memorial.   
8      9974125374801701                     Mrs. Colvin's Weekly Messenger   
9      9974125319501701  Expounder of Primitive Christianity: Devoted t...   
10     9974125315001701  Gazette of the Union Golden Rule and Odd Fello...   
11     9974125311101701       Hesperian, The, or, Western Monthly Magazine   
12     9974125334001701                     Boys' and Girls' Penny Journal   
13     9974375039001701  Reports of cases at law and in equity, argued ...   
14     9974375166601701          Report of the Attorney General of Arizona   
15     9974375156601701  Opinions of the Attorney General of the state ...   
16     9974375124101701                         Senate journal, New Mexico   
17     9974375172401701                        Arkansas reports, annotated   
18     9974375035601701                          Oklahoma reports (Online)   
19     9974375171101701  Chrostwaite's Pennsylvania municipal law reporter   
20     9974375165301701                                   Sessional papers   
21     9974141884501701                   Control Conference (ICC), Indian   
22     9974125357401701                                             Sprite   
23     9974125603501701                                     Polish eaglet.   
24     9974125456701701                                        The sunbeam   
25     9974125491801701                Musical review and choral advocate.   
26     9974125289501701                               The Centennial Eagle   
27     9974125266801701             The journal of the Franklin Institute    
28     9974125286501701                                        The citadel   
29     9974125240801701  The Quarterly of the Young Men's Christian Ass...   
...                 ...                                                ...   
47998  9968419300001701                             Strategic outsourcing.   
47999  9968623500001701                         Studies in the Renaissance   
48000  9968623930001701                  Advocate of peace through justice   
48001  9968244930001701   IEEE International Conference on Neural Networks   
48002  9968634630001701                  Niles' national register (Online)   
48003  9968212110001701                               Museum international   
48004  9968518660001701       Journal of plant nutrition and soil science.   
48005  9968159130001701                      Fette, Seifen, Anstrichmittel   
48006  9968426800001701  IRE transactions on aeronautical and navigatio...   
48007  9968274250001701         Mechanics of cohesive-frictional materials   
48008  9968439710001701  Journal of the Society of Motion Picture Engin...   
48009  9968645490001701  Revue d'histoire de la deuxième guerre mondial...   
48010  9968386210001701         International journal of vegetable science   
48011  9968318900001701                         The Edgar Allan Poe review   
48012  9968620360001701       Progress in tourism and hospitality research   
48013  9968472800001701        Agricultural and forest entomology (Online)   
48014  9968591580001701  European journal on criminal policy and resear...   
48015  9968569050001701  Software Process, International Conference on the   
48016  9968570970001701  Recent Advances in Microwave Theory and Applic...   
48017  9968469490001701  Multimedia Com

In [35]:
pdf2['p_or_e'] = 'p'
pdf2

C:\Users\kjthomps\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


MMS_ID                                              Title  \
0      9913162530001701                Annual review of chronopharmacology   
1      9912286510001701  Annual report on inheritance and improvement o...   
2      9912380980001701  Station list of officers of Medical Department...   
3      9912842260001701          Regional conference series in mathematics   
4      9913436020001701                              Journal of glaciology   
5      9913837990001701        Studies in Cistercian art and architecture.   
6      9912739540001701                The Agricultural education magazine   
7      9913448360001701                                    Gothic studies.   
8      9913436980001701                                Internet @ schools.   
9      9913216420001701                                   Aquatic insects.   
10     9913415620001701      Journal of muscle research and cell motility.   
11     9913396060001701                                  Spazio e società   
12     9912841300001701                             Compositio mathematica   
13     9912758800001701                           Annali di architettura :   
14     9913176500001701  Acta crystallographica. Section A. Foundations...   
15     9912749160001701                          Social science & medicine   
16     9913383290001701  Research quarterly of the American Association...   
17     9913442920001701                                     Screen digest.   
18     9913442120001701                          Sociology of the sciences   
19     9912741930001701  Annual statistical digest (Castries, Saint Lucia)   
20     9913884430001701                     Magyar statistikai évkönyv =   
21     9913907650001701                  Vestnik Moskovskogo universiteta.   
22     9913448660001701                                  Larousse mensuel.   
23     9913300500001701                                Fieldstaff reports.   
24     9913226960001701                            Bulletin signalétique.   
25     9913219080001701                                    Årsberetning /   
26     9913220260001701   Arthropods of Florida and neighboring land areas   
27     9913168330001701  Annual report of the State Oil and Gas Supervisor   
28     9913184460001701                    Archivio per le scienze mediche   
29     9913134380001701  The Mercantile Agency reference book for the B...   
...                 ...                                                ...   
99265  9963076860001701                             Country profile. Malta   
99266  9963135770001701                Rock mechanics and rock engineering   
99267  9963097840001701                               The Social frontier.   
99268  9963095330001701  Library and reference facilities in the area o...   
99269  9962898650001701  Comparative statements of cash disbursements b...   
99270  9962886880001701  Monograph (University of California, Berkeley....   
99271  9962886180001701                    Agriculture, the third century.   
99272  9962378370001701                                  Neues Abendland ;   
99273  9961859470001701                               Statistical summary.   
99274  9965926900001701             BP statistical review of world energy.   
99275  9965934940001701                                 California design.   
99276  9973295993501701            Data sheets for ordnance type materiel.   
99277  9972960920001701  Direct and general support and depot maintenan...   
99278  9973345108901701                                Operator's manual :   
99279  9972598080001701  Direct and general support and depot maintenan...   
99280  9972960990001701           Operator's and unit maintenance manual :   
99281  9972598010001701  Operator, organizational, direct and general s...   
99282  9972960280001701  Operator's, unit, intermediate direct support,...   
99283  9973345099501701  Operator and organizational maintenance manual...   
99284  9964736970001701                

In [36]:
# Combine the P and E dataframes (stack vertically).

df = pd.concat([edf2,pdf2], ignore_index=True)
df

ISSN                       ISSN_cluster            MMS_ID  \
0                []                                 []  9974125338401701   
1                []                                 []  9974125400901701   
2                []                                 []  9974125335601701   
3                []                                 []  9974125600601701   
4                []                                 []  9974125417001701   
5                []                                 []  9974125495201701   
6                []                                 []  9974125496001701   
7                []                                 []  9974125410201701   
8                []                                 []  9974125374801701   
9                []                                 []  9974125319501701   
10               []                                 []  9974125315001701   
11               []                                 []  9974125311101701   
12               []                                 []  9974125334001701   
13               []                        [0092-9581]  9974375039001701   
14               []                                 []  9974375166601701   
15               []                                 []  9974375156601701   
16               []                                 []  9974375124101701   
17               []                                 []  9974375172401701   
18               []                                 []  9974375035601701   
19               []                                 []  9974375171101701   
20               []                                 []  9974375165301701   
21               []                                 []  9974141884501701   
22      [1181-0157]                        [1181-0157]  9974125357401701   
23      [0732-1007]                        [0732-1007]  9974125603501701   
24               []                                 []  9974125456701701   
25               []                                 []  9974125491801701   
26               []                                 []  9974125289501701   
27               []                                 []  9974125266801701   
28               []                                 []  9974125286501701   
29               []                                 []  9974125240801701   
...             ...                                ...               ...   
147293  [0269-8137]  [0269-7238, 0266-9730, 0269-8137]  9963076860001701   
147294  [0723-2632]  [1434-453X, 0035-7448, 0723-2632]  9963135770001701   
147295           []                                 []  9963097840001701   
147296  [0191-2798]                        [0191-2798]  9963095330001701   
147297           []                                 []  9962898650001701   
147298           []                                 []  9962886880001701   
147299           []                                 []  9962886180001701   
147300           []                                 []  9962378370001701   
147301           []                                 []  9961859470001701   
147302  [0263-9815]             [1467-5692, 0263-9815]  9965926900001701   
147303  [0068-5542]                        [0068-5542]  9965934940001701   
147304           []                                 []  9973295993501701   
147305           []                                 []  9972960920001701   
147306           []                                 []  9973345108901701   
147307           []                                 []  9972598080001701   
147308           []                                 []  9972960990001701   
147309           []                                 []  9972598010001701   
147310           []                                 []  9972960280001701   
147311           []                                 []  9973345099501701   
147312  [0009-4617]                        [0009-4617]  9964736970001701   
147313  [0001-5962]                        [0001-5962]  9964613

In [37]:
def melt_group_ids ( df, identifier_column, identifier_name, group_name ):
    
    # This function takes a column of multi-valued cells in a dataframe, explodes them out into single-valued cells still 
    # linked to their row ID.  This data is then merged with a database-style join with the input dataframe

    melted_ids = pd.concat([pd.DataFrame(v, index=np.repeat(k,len(v)))
                              for k,v in df[identifier_column].to_dict().items()])
    melted_ids = melted_ids.rename(columns={0:identifier_name})
    print('melted')
    print(melted_ids.columns)

    df2 = pd.DataFrame()
    df2 = pd.merge(df,melted_ids,how="inner",left_index=True,right_index=True)
    df2 = df2.reset_index()
    df2 = df2.rename(columns={"index":"record_index"})
    print('merged')
    print(df2.columns)

    df3 = pd.DataFrame()
    df3 = df2.groupby([identifier_name]).ngroup()
    print('grouped')

    groups = df3.to_frame()
    groups.rename(columns={0: group_name + '_group_id' },inplace=True)
    print(groups.columns)
    
    eg = pd.merge(df2[['record_index']],groups,left_index=True,right_index=True, how="inner")
    
    print(eg.columns)
    
    df6 = pd.DataFrame()
    df6 = eg.groupby(['record_index']).agg(lambda x: list(set(x))).reset_index()
    print('re-grouped')
    print(df6.columns)
    
    while df6[group_name + '_group_id'].str.len().max() > 1:
        for each in tqdm(df6[group_name + '_group_id'],desc="reducing progress", unit="records"):
            if len(each) > 1:
                #print(each)
                val = each[0]
                for x in each[1:]:
                    #print(x)
                    eg[group_name + '_group_id'][eg[group_name + '_group_id'] == x] = val
                    eg.drop_duplicates(inplace=True)
        df6 = pd.DataFrame()
        df6 = eg.groupby(['record_index']).agg(lambda x: list(set(x))).reset_index()
    eg = eg.sort_values([group_name + '_group_id'])
    
    print('merging back into df')
    eg1 = pd.merge(df,eg,how='left',left_index=True,right_on='record_index')
    eg1.set_index('record_index',inplace=True)
    
    matches = eg1[eg1[group_name + '_group_id'].notnull()]
    group_ids = sorted(list(set(matches[group_name + '_group_id'])))
    group_list = list(range(0,len(group_ids)))
    group_dict = dict(zip(group_ids,group_list))
    
    matches[group_name + '_group_id'].replace(group_dict, inplace=True)
    
    no_matches = eg1[eg1[group_name + '_group_id'].isnull()]
    no_matches[group_name + '_group_id'] = list(range(len(group_ids),len(group_ids)+len(no_matches)))
    output = pd.concat([matches,no_matches])
    output.sort_values(group_name + '_group_id',inplace=True)
    
    return output

In [38]:
df_issns = melt_group_ids ( df, 'ISSN_cluster', 'ISSN_y', 'ISSN' )
df_issns

melted
Index(['ISSN_y'], dtype='object')
merged
Index(['record_index', 'ISSN', 'ISSN_cluster', 'MMS_ID', 'OCN', 'OCN_cluster',
       'Title', 'chron', 'descr', 'e_holdings', 'enum', 'p_or_e', 'ISSN_y'],
      dtype='object')
grouped
Index(['ISSN_group_id'], dtype='object')
Index(['record_index', 'ISSN_group_id'], dtype='object')
re-grouped
Index(['record_index', 'ISSN_group_id'], dtype='object')


reducing progress: 100%|███████████████████████████████████████████████| 76176/76176 [00:00<00:00, 1624410.50records/s]


merging back into df


C:\Users\kjthomps\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\generic.py:4619: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._update_inplace(new_data)
C:\Users\kjthomps\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


ISSN                                  ISSN_cluster  \
record_index                                                              
127770        [0000-0787]             [0000-0469, 0000-0787, 0000-0019]   
97726         [0000-0469]             [0000-0469, 0000-0787, 0000-0019]   
8069          [2150-4008]             [0094-257X, 0000-0019, 2150-4008]   
56385         [0000-0019]  [0000-0469, 0000-0019, 0094-257X, 2150-4008]   
76458         [0000-0175]             [0000-0175, 0000-2100, 1068-0500]   
126287        [0000-2100]                        [0000-0175, 0000-2100]   
28487         [0000-2100]                        [0000-0175, 0000-2100]   
88734         [0000-0094]             [0000-0175, 0000-0507, 0000-0094]   
74362         [0000-0043]             [0000-0094, 0000-0043, 0000-0175]   
100477        [0000-0183]                                   [0000-0183]   
52244         [0065-6968]                                   [0065-6968]   
126136                 []                        [0065-6968, 0000-0191]   
111547        [0000-0191]                                   [0000-0191]   
131131                 []                                   [0000-0213]   
128263        [0000-0213]                                   [0000-0213]   
73127         [0000-0302]                                   [0000-0302]   
134646        [0000-0345]                                   [0000-0345]   
129280        [0000-0361]                                   [0000-0361]   
93918         [0000-0388]                                   [0000-0388]   
73535         [0000-0418]                                   [0000-0418]   
78445         [0000-0426]                                   [0000-0426]   
84148         [0000-0434]                        [0270-1359, 0000-0434]   
120124        [0000-0450]             [0142-0208, 0162-878X, 0000-0450]   
88687         [0000-0523]                                   [0000-0523]   
79438         [0000-054X]                        [0000-0248, 0000-054X]   
50377         [0362-8930]             [0000-0566, 0362-8930, 0000-0035]   
84489         [0000-0973]                        [0000-0590, 0000-0973]   
81783         [0000-0590]                        [0000-0590, 0000-0973]   
83770                  []                                   [0000-0973]   
118259        [0000-0604]                                   [0000-0604]   
...                   ...                                           ...   
147265                 []                                            []   
147268                 []                                            []   
147270                 []                                            []   
147271                 []                                            []   
147273                 []                                            []   
147277                 []                                            []   
147278                 []                                            []   
147283                 []                                            []   
147285                 []                                            []   
147286                 []                                            []   
147289                 []                                            []   
147292                 []                                            []   
147295                 []                                            []   
147297                 []                                            []   
147298                 []                                            []   
147299                 []                                            []   
147300                 []                                            []   
147301                 []                                            []   
147304                 []                                            []   
147305                 []                                            []   
147306                 []                     

In [39]:
df_issns.sort_index()

ISSN                       ISSN_cluster  \
record_index                                                   
0                      []                                 []   
1                      []                                 []   
2                      []                                 []   
3                      []                                 []   
4                      []                                 []   
5                      []                                 []   
6                      []                                 []   
7                      []                                 []   
8                      []                                 []   
9                      []                                 []   
10                     []                                 []   
11                     []                                 []   
12                     []                                 []   
13                     []                        [0092-9581]   
14                     []                                 []   
15                     []                                 []   
16                     []                                 []   
17                     []                                 []   
18                     []                                 []   
19                     []                                 []   
20                     []                                 []   
21                     []                                 []   
22            [1181-0157]                        [1181-0157]   
23            [0732-1007]                        [0732-1007]   
24                     []                                 []   
25                     []                                 []   
26                     []                                 []   
27                     []                                 []   
28                     []                                 []   
29                     []                                 []   
...                   ...                                ...   
147293        [0269-8137]  [0269-7238, 0266-9730, 0269-8137]   
147294        [0723-2632]  [1434-453X, 0035-7448, 0723-2632]   
147295                 []                                 []   
147296        [0191-2798]                        [0191-2798]   
147297                 []                                 []   
147298                 []                                 []   
147299                 []                                 []   
147300                 []                                 []   
147301                 []                                 []   
147302        [0263-9815]             [1467-5692, 0263-9815]   
147303        [0068-5542]                        [0068-5542]   
147304                 []                                 []   
147305                 []                                 []   
147306                 []                                 []   
147307                 []                                 []   
147308                 []                                 []   
147309                 []                                 []   
147310                 []                                 []   
147311                 []                                 []   
147312        [0009-4617]                        [0009-4617]   
147313        [0001-5962]                        [0001-5962]   
147314                 []                                 []   
147315                 []                                 []   
147316        [1554-8554]             [0093-7576, 1554-8554]   
147317        [0739-456X]             [0739-456X, 0004-5675]   
147318        [1011-9493]             [1738-2297, 1011-9493]   
147319        [0377-7103]                        [0377-7103]   
147320                 []                                 []   
147321                 []                                 []   
147322        [0011-3700]                        [001

In [40]:
df_issns.to_pickle('edf_issns_grouped.pkl')
df_issns.to_csv('edf_issns_grouped.txt',sep='\t')

In [48]:
df_ocns = melt_group_ids ( df_issns, 'OCN_cluster', 'OCN_y', 'OCN' )
df_ocns

melted
Index(['OCN_y'], dtype='object')
merged
Index(['record_index', 'ISSN', 'ISSN_cluster', 'MMS_ID', 'OCN', 'OCN_cluster',
       'Title', 'chron', 'descr', 'e_holdings', 'enum', 'p_or_e',
       'ISSN_group_id', 'OCN_y'],
      dtype='object')
grouped
Index(['OCN_group_id'], dtype='object')
Index(['record_index', 'OCN_group_id'], dtype='object')
re-grouped
Index(['record_index', 'OCN_group_id'], dtype='object')


reducing progress: 100%|█████████████████████████████████████████████| 129513/129513 [00:00<00:00, 1381285.82records/s]


merging back into df


C:\Users\kjthomps\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\generic.py:4619: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._update_inplace(new_data)
C:\Users\kjthomps\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


ISSN                                  ISSN_cluster  \
record_index                                                              
115308                 []                                            []   
76019         [0348-1158]                                   [0348-1158]   
134425                 []                                            []   
146648                 []                                            []   
132674                 []                                            []   
118158        [0070-8208]                                   [0070-8208]   
111714        [0020-6024]                        [0303-6936, 0020-6024]   
119749        [0303-6936]             [0303-6936, 0020-6024, 0262-6667]   
128004        [0262-6667]                        [0303-6936, 0262-6667]   
143817                 []                                            []   
90685                  []                                   [0014-2433]   
146297                 []                                   [0081-4873]   
107558                 []                                   [0078-0170]   
145097                 []                                   [0003-9489]   
100151        [1224-7685]                        [0368-7732, 1224-7685]   
141538        [0003-9489]                        [0368-7732, 0003-9489]   
117117        [1476-0835]                        [0007-1129, 1476-0835]   
57638                  []                                            []   
113790        [0001-6357]                        [0365-530X, 0001-6357]   
131243                 []                                            []   
80883         [0547-0013]                                   [0547-0013]   
54801         [0486-3720]                        [1473-5784, 0486-3720]   
100896        [1473-5784]                        [1473-5784, 0486-3720]   
66650         [0035-869X]                        [0035-869X, 1356-1863]   
40737         [2051-2066]  [1474-0591, 0950-4737, 0035-869X, 2051-2066]   
26114         [0950-4737]                        [0950-4737, 1474-0591]   
140057                 []                                   [0035-869X]   
28493         [1474-0591]             [0950-4737, 1474-0591, 1356-1863]   
132234                 []                                   [0505-401X]   
99382         [1470-1995]                        [0011-0875, 1470-1995]   
...                   ...                                           ...   
47821                  []                                            []   
47822                  []                                            []   
47834                  []                                            []   
47836                  []                                            []   
47879                  []                                            []   
47880                  []                                            []   
47881                  []                                            []   
47885                  []                                            []   
47886                  []                                            []   
47909                  []                                            []   
47910                  []                                            []   
47911                  []                                            []   
47952                  []                                            []   
47953                  []                                            []   
47954                  []                                            []   
47955                  []                                            []   
47956                  []                                            []   
47957                  []                                            []   
47975                  []                                            []   
47976                  []                                            []   
47977                  []                     

In [49]:
df = df_ocns

In [50]:
df['ISSN_group_id']= df['ISSN_group_id'].apply(lambda x: [str(int(x)) + 'i'])
df

ISSN                                  ISSN_cluster  \
record_index                                                              
115308                 []                                            []   
76019         [0348-1158]                                   [0348-1158]   
134425                 []                                            []   
146648                 []                                            []   
132674                 []                                            []   
118158        [0070-8208]                                   [0070-8208]   
111714        [0020-6024]                        [0303-6936, 0020-6024]   
119749        [0303-6936]             [0303-6936, 0020-6024, 0262-6667]   
128004        [0262-6667]                        [0303-6936, 0262-6667]   
143817                 []                                            []   
90685                  []                                   [0014-2433]   
146297                 []                                   [0081-4873]   
107558                 []                                   [0078-0170]   
145097                 []                                   [0003-9489]   
100151        [1224-7685]                        [0368-7732, 1224-7685]   
141538        [0003-9489]                        [0368-7732, 0003-9489]   
117117        [1476-0835]                        [0007-1129, 1476-0835]   
57638                  []                                            []   
113790        [0001-6357]                        [0365-530X, 0001-6357]   
131243                 []                                            []   
80883         [0547-0013]                                   [0547-0013]   
54801         [0486-3720]                        [1473-5784, 0486-3720]   
100896        [1473-5784]                        [1473-5784, 0486-3720]   
66650         [0035-869X]                        [0035-869X, 1356-1863]   
40737         [2051-2066]  [1474-0591, 0950-4737, 0035-869X, 2051-2066]   
26114         [0950-4737]                        [0950-4737, 1474-0591]   
140057                 []                                   [0035-869X]   
28493         [1474-0591]             [0950-4737, 1474-0591, 1356-1863]   
132234                 []                                   [0505-401X]   
99382         [1470-1995]                        [0011-0875, 1470-1995]   
...                   ...                                           ...   
47821                  []                                            []   
47822                  []                                            []   
47834                  []                                            []   
47836                  []                                            []   
47879                  []                                            []   
47880                  []                                            []   
47881                  []                                            []   
47885                  []                                            []   
47886                  []                                            []   
47909                  []                                            []   
47910                  []                                            []   
47911                  []                                            []   
47952                  []                                            []   
47953                  []                                            []   
47954                  []                                            []   
47955                  []                                            []   
47956                  []                                            []   
47957                  []                                            []   
47975                  []                                            []   
47976                  []                                            []   
47977                  []                     

In [51]:
df['OCN_group_id']= df['OCN_group_id'].apply(lambda x: [str(int(x)) + 'o'])
df

ISSN                                  ISSN_cluster  \
record_index                                                              
115308                 []                                            []   
76019         [0348-1158]                                   [0348-1158]   
134425                 []                                            []   
146648                 []                                            []   
132674                 []                                            []   
118158        [0070-8208]                                   [0070-8208]   
111714        [0020-6024]                        [0303-6936, 0020-6024]   
119749        [0303-6936]             [0303-6936, 0020-6024, 0262-6667]   
128004        [0262-6667]                        [0303-6936, 0262-6667]   
143817                 []                                            []   
90685                  []                                   [0014-2433]   
146297                 []                                   [0081-4873]   
107558                 []                                   [0078-0170]   
145097                 []                                   [0003-9489]   
100151        [1224-7685]                        [0368-7732, 1224-7685]   
141538        [0003-9489]                        [0368-7732, 0003-9489]   
117117        [1476-0835]                        [0007-1129, 1476-0835]   
57638                  []                                            []   
113790        [0001-6357]                        [0365-530X, 0001-6357]   
131243                 []                                            []   
80883         [0547-0013]                                   [0547-0013]   
54801         [0486-3720]                        [1473-5784, 0486-3720]   
100896        [1473-5784]                        [1473-5784, 0486-3720]   
66650         [0035-869X]                        [0035-869X, 1356-1863]   
40737         [2051-2066]  [1474-0591, 0950-4737, 0035-869X, 2051-2066]   
26114         [0950-4737]                        [0950-4737, 1474-0591]   
140057                 []                                   [0035-869X]   
28493         [1474-0591]             [0950-4737, 1474-0591, 1356-1863]   
132234                 []                                   [0505-401X]   
99382         [1470-1995]                        [0011-0875, 1470-1995]   
...                   ...                                           ...   
47821                  []                                            []   
47822                  []                                            []   
47834                  []                                            []   
47836                  []                                            []   
47879                  []                                            []   
47880                  []                                            []   
47881                  []                                            []   
47885                  []                                            []   
47886                  []                                            []   
47909                  []                                            []   
47910                  []                                            []   
47911                  []                                            []   
47952                  []                                            []   
47953                  []                                            []   
47954                  []                                            []   
47955                  []                                            []   
47956                  []                                            []   
47957                  []                                            []   
47975                  []                                            []   
47976                  []                                            []   
47977                  []                     

In [52]:
df['both_groups'] = df['ISSN_group_id'] + df['OCN_group_id']
df

ISSN                                  ISSN_cluster  \
record_index                                                              
115308                 []                                            []   
76019         [0348-1158]                                   [0348-1158]   
134425                 []                                            []   
146648                 []                                            []   
132674                 []                                            []   
118158        [0070-8208]                                   [0070-8208]   
111714        [0020-6024]                        [0303-6936, 0020-6024]   
119749        [0303-6936]             [0303-6936, 0020-6024, 0262-6667]   
128004        [0262-6667]                        [0303-6936, 0262-6667]   
143817                 []                                            []   
90685                  []                                   [0014-2433]   
146297                 []                                   [0081-4873]   
107558                 []                                   [0078-0170]   
145097                 []                                   [0003-9489]   
100151        [1224-7685]                        [0368-7732, 1224-7685]   
141538        [0003-9489]                        [0368-7732, 0003-9489]   
117117        [1476-0835]                        [0007-1129, 1476-0835]   
57638                  []                                            []   
113790        [0001-6357]                        [0365-530X, 0001-6357]   
131243                 []                                            []   
80883         [0547-0013]                                   [0547-0013]   
54801         [0486-3720]                        [1473-5784, 0486-3720]   
100896        [1473-5784]                        [1473-5784, 0486-3720]   
66650         [0035-869X]                        [0035-869X, 1356-1863]   
40737         [2051-2066]  [1474-0591, 0950-4737, 0035-869X, 2051-2066]   
26114         [0950-4737]                        [0950-4737, 1474-0591]   
140057                 []                                   [0035-869X]   
28493         [1474-0591]             [0950-4737, 1474-0591, 1356-1863]   
132234                 []                                   [0505-401X]   
99382         [1470-1995]                        [0011-0875, 1470-1995]   
...                   ...                                           ...   
47821                  []                                            []   
47822                  []                                            []   
47834                  []                                            []   
47836                  []                                            []   
47879                  []                                            []   
47880                  []                                            []   
47881                  []                                            []   
47885                  []                                            []   
47886                  []                                            []   
47909                  []                                            []   
47910                  []                                            []   
47911                  []                                            []   
47952                  []                                            []   
47953                  []                                            []   
47954                  []                                            []   
47955                  []                                            []   
47956                  []                                            []   
47957                  []                                            []   
47975                  []                                            []   
47976                  []                                            []   
47977                  []                     

In [ ]:
def both_group_ids ( df, identifier_column, identifier_name, group_name ):

    melted_ids = pd.concat([pd.DataFrame(v, index=np.repeat(k,len(v)))
                              for k,v in df[identifier_column].to_dict().items()])
    melted_ids = melted_ids.rename(columns={0:identifier_name})
    print('melted')
    print(melted_ids.columns)

    df2 = pd.DataFrame()
    df2 = pd.merge(df,melted_ids,how="inner",left_index=True,right_index=True)
    df2 = df2.reset_index()
    df2 = df2.rename(columns={"index":"record_index"})
    print('merged')
    print(df2.columns)

    df3 = pd.DataFrame()
    df3 = df2.groupby([identifier_name]).ngroup()
    print('grouped')

    groups = df3.to_frame()
    groups.rename(columns={0: group_name + '_group_id' },inplace=True)
    print(groups.columns)
    
    eg = pd.merge(df2[['record_index']],groups,left_index=True,right_index=True, how="inner")
    
    print(eg.columns)
    
    df6 = pd.DataFrame()
    df6 = eg.groupby(['record_index']).agg(lambda x: list(set(x))).reset_index()
    print('re-grouped')
    print(df6.columns)
    
    while df6[group_name + '_group_id'].str.len().max() > 1:
        for each in tqdm(df6[group_name + '_group_id'],desc="reducing progress", unit="records"):
            if len(each) > 1:
                #print(each)
                val = each[0]
                for x in each[1:]:
                    #print(x)
                    eg[group_name + '_group_id'][eg[group_name + '_group_id'] == x] = val
                    eg.drop_duplicates(inplace=True)
        df6 = pd.DataFrame()
        df6 = eg.groupby(['record_index']).agg(lambda x: list(set(x))).reset_index()
    eg = eg.sort_values([group_name + '_group_id'])
    
    print('merging back into df')
    eg1 = pd.merge(df,eg,how='left',left_index=True,right_on='record_index')
    eg1.set_index('record_index',inplace=True)
    
    '''
    matches = eg1[eg1[group_name + '_group_id'].notnull()]
    group_ids = sorted(list(set(matches[group_name + '_group_id'])))
    group_list = list(range(0,len(group_ids)))
    group_dict = dict(zip(group_ids,group_list))
    
    matches[group_name + '_group_id'].replace(group_dict, inplace=True)
    
    no_matches = eg1[eg1[group_name + '_group_id'].isnull()]
    no_matches[group_name + '_group_id'] = list(range(len(group_ids),len(group_ids)+len(no_matches)))
    output = pd.concat([matches,no_matches])
    output.sort_values(group_name + '_group_id',inplace=True)
    '''
    
    return eg1

In [ ]:
pe_df = both_group_ids ( df, 'both_groups', 'matches', 'matches' )
pe_df


In [ ]:
pe_df.sort_values('matches_group_id')

In [ ]:
group_ids = sorted(list(set(pe_df['matches_group_id'])))
group_list = list(range(0,len(group_ids)))
group_dict = dict(zip(group_ids,group_list))

In [ ]:
len(group_dict)

In [ ]:
pe_df['matches_group_id'].replace(group_dict, inplace=True)
pe_df

In [ ]:
pe_df.sort_index()

In [ ]:
pe_df.sort_values('matches_group_id', inplace=True)

In [ ]:
pe_df.to_pickle('pe_df_20180702.pkl')
pe_df.to_csv('pe_df_20180702.txt', sep='\t')

In [14]:
pe_df = pd.read_pickle('pe_df_20180702.pkl')
pe_df

ISSN                                  ISSN_cluster  \
record_index                                                              
127770        [0000-0787]             [0000-0787, 0000-0469, 0000-0019]   
8069          [2150-4008]             [2150-4008, 0094-257X, 0000-0019]   
97726         [0000-0469]             [0000-0787, 0000-0469, 0000-0019]   
56385         [0000-0019]  [0000-0469, 2150-4008, 0094-257X, 0000-0019]   
115308                 []                                            []   
108628                 []                                            []   
20942                  []                                            []   
55290         [0741-7233]                                   [0741-7233]   
108631                 []                                            []   
39905                  []                                   [2080-8097]   
108637                 []                                            []   
58118                  []                                            []   
108646                 []                                            []   
95797                  []                                            []   
41184         [2411-1406]                        [2411-1406, 2072-6414]   
35540         [2055-5520]                                   [2055-5520]   
108649                 []                                            []   
8866                   []                                   [2059-5131]   
108650                 []                                            []   
95578                  []                                            []   
80716                  []                                            []   
103257                 []                                            []   
56888                  []                                            []   
108660                 []                                            []   
125136        [0713-3936]                                   [0713-3936]   
18777         [1929-7084]                        [0713-3936, 1929-7084]   
108674                 []                                            []   
142132        [0557-3912]                                   [0557-3912]   
108675                 []                                            []   
108677                 []                                            []   
...                   ...                                           ...   
108584                 []                                            []   
51997                  []                                   [0164-0968]   
3634                   []                                            []   
108590                 []                                            []   
105652                 []                                            []   
108593                 []                                            []   
127516                 []                                            []   
121344                 []                                            []   
110631                 []                                            []   
108600                 []                                            []   
35291                  []                                            []   
139884        [0131-6095]                                   [0131-6095]   
32182                  []                                   [0131-6095]   
97302                  []                                            []   
108601                 []                                            []   
79929                  []                                            []   
2359          [0893-7184]                                   [0893-7184]   
108605                 []                                            []   
62336         [0737-4194]                                   [0737-4194]   
43741                  []                                            []   
12151         [2470-7597]                     

In [4]:
p_loc_df = pd.read_csv('p-ser-loc-data.txt',sep='\t',dtype=str)
p_loc_df

001              954$a            954$b      954$c  \
0      9932238790001701  23390775640001701  31953000323080J         29   
1      9932238790001701  23390774920001701  319530006617072         72   
2      9932238790001701  23390774770001701  31953000894461X         78   
3      9936469410001701  23409123020001701  31951000218977I          6   
4      9936469410001701  23409122350001701  31951D009489771         48   
5      9936469410001701  23409122270001701  31951P00447179L         52   
6      9941315740001701  23429574750001701  31951P01067390X      30-31   
7      9943394650001701  23438778910001701  31951P006077050         62   
8      9943394650001701  23438778690001701  31951P00716900U      89-90   
9      9947676880001701  23649522530001701  31951P01207515P    270-277   
10     9947676880001701  23456221650001701  31951P01013353H    230-241   
11     9945271420001701  23446297170001701  31951P00997046B         45   
12     9945271420001701  23446297050001701  31951P006910240         38   
13     9945271420001701  23446296990001701  31951000736402W         27   
14     9945271420001701  23446296400001701  31951P00852295A         42   
15     9945271420001701  23446295510001701  31953000432404B         35   
16     9945271420001701  23446295440001701  319530006328380         37   
17     9944549220001701  23443215470001701  31951P00032408J      50-51   
18     9943544430001701  23439348130001701  31951P002735266         24   
19     9941332650001701  23429716710001701  31951P00531616I      71-73   
20     9941326320001701  23429633850001701   35905004893565         26   
21     9937560120001701  23414003900001701  31953000768678D         28   
22     9948562090001701  23459953390001701  31951D01690506R       1999   
23     9942530920001701  23434834010001701  31951000191182F          7   
24     9939989520001701  23424118420001701  31953000207763Q         59   
25     9937328660001701  23412837100001701  31951P002179517        317   
26     9937328660001701  23412836900001701  31951P00702090T        333   
27     9945094780001701  23445495190001701  31951P00016956G         34   
28     9945094780001701  23445495100001701  31951P00105915Y         40   
29     9946779030001701  23452441500001701  319510007363953      17-18   
...                 ...                ...              ...        ...   
26249  9947037570001701  23662115400001701          X793765        102   
26250  9952533200001701  23475875120001701  31951P00370244O          7   
26251  9948562090001701  23459956360001701  31951D01161033K       1992   
26252  9948562090001701  23459955320001701  31951D012774117       1987   
26253  9947271240001701  23454618470001701  31951D003846313       1964   
26254  9947271240001701  23454617750001701  31951P01219751X       1951   
26255  9947271240001701  23454617630001701  31951P01219755P  1953/1956   
26256  9950856800001701  23469238630001701  31951D03571156Q        4-5   
26257  9965893580001701  23533885420001701  319530007944282        340   
26258  9954102240001701  23482982230001701  31951P006178860        239   
26259  9953799700001701  23481737590001701  31953000623743C         76   
26260  9953499650001701  23624865160001701  31951SI10139943         54   
26261  9951705040001701  23472508950001701  31953000924397F        107   
26262  9951705040001701  23472508880001701  31953000930261I        107   
26263  9951705040001701  23472508520001701  31953000709258U        102   
26264  9951705040001701  23472507560001701  31953000728635J        103   
26265  9951705040001701  23472505270001701   35905011638458        109   
26266  9951705040001701  23472505200001701   35905008593716        103   
26267  9951705040001701  23472492690001701  31951P00459745Y        103   
26268  9951705040001701  23472492670001701  31951P007528385        104   
26269  9951705040001701  23472492510001701  31951P007550019        104   
26270  9951705040001701  23472492310001701  31951P00737826Z        105   
26271  9951705040001701 

In [5]:
p_loc_df.columns

Index(['001', '954$a', '954$b', '954$c', '954$d', '954$e', '954$f', '954$g'], dtype='object')

In [6]:
p_loc_df.rename(columns={'001':'MMS ID', '954$a':'Item PID', '954$b':'Barcode', 
                         '954$c':'Enum_item', '954$d':'Chron_item', '954$e':'Descr_item', 
                         '954$f':'Permanent Library', '954$g':'Permanent Location'},inplace=True)
p_loc_df

MMS ID           Item PID          Barcode  Enum_item  \
0      9932238790001701  23390775640001701  31953000323080J         29   
1      9932238790001701  23390774920001701  319530006617072         72   
2      9932238790001701  23390774770001701  31953000894461X         78   
3      9936469410001701  23409123020001701  31951000218977I          6   
4      9936469410001701  23409122350001701  31951D009489771         48   
5      9936469410001701  23409122270001701  31951P00447179L         52   
6      9941315740001701  23429574750001701  31951P01067390X      30-31   
7      9943394650001701  23438778910001701  31951P006077050         62   
8      9943394650001701  23438778690001701  31951P00716900U      89-90   
9      9947676880001701  23649522530001701  31951P01207515P    270-277   
10     9947676880001701  23456221650001701  31951P01013353H    230-241   
11     9945271420001701  23446297170001701  31951P00997046B         45   
12     9945271420001701  23446297050001701  31951P006910240         38   
13     9945271420001701  23446296990001701  31951000736402W         27   
14     9945271420001701  23446296400001701  31951P00852295A         42   
15     9945271420001701  23446295510001701  31953000432404B         35   
16     9945271420001701  23446295440001701  319530006328380         37   
17     9944549220001701  23443215470001701  31951P00032408J      50-51   
18     9943544430001701  23439348130001701  31951P002735266         24   
19     9941332650001701  23429716710001701  31951P00531616I      71-73   
20     9941326320001701  23429633850001701   35905004893565         26   
21     9937560120001701  23414003900001701  31953000768678D         28   
22     9948562090001701  23459953390001701  31951D01690506R       1999   
23     9942530920001701  23434834010001701  31951000191182F          7   
24     9939989520001701  23424118420001701  31953000207763Q         59   
25     9937328660001701  23412837100001701  31951P002179517        317   
26     9937328660001701  23412836900001701  31951P00702090T        333   
27     9945094780001701  23445495190001701  31951P00016956G         34   
28     9945094780001701  23445495100001701  31951P00105915Y         40   
29     9946779030001701  23452441500001701  319510007363953      17-18   
...                 ...                ...              ...        ...   
26249  9947037570001701  23662115400001701          X793765        102   
26250  9952533200001701  23475875120001701  31951P00370244O          7   
26251  9948562090001701  23459956360001701  31951D01161033K       1992   
26252  9948562090001701  23459955320001701  31951D012774117       1987   
26253  9947271240001701  23454618470001701  31951D003846313       1964   
26254  9947271240001701  23454617750001701  31951P01219751X       1951   
26255  9947271240001701  23454617630001701  31951P01219755P  1953/1956   
26256  9950856800001701  23469238630001701  31951D03571156Q        4-5   
26257  9965893580001701  23533885420001701  319530007944282        340   
26258  9954102240001701  23482982230001701  31951P006178860        239   
26259  9953799700001701  23481737590001701  31953000623743C         76   
26260  9953499650001701  23624865160001701  31951SI10139943         54   
26261  9951705040001701  23472508950001701  31953000924397F        107   
26262  9951705040001701  23472508880001701  31953000930261I        107   
26263  9951705040001701  23472508520001701  31953000709258U        102   
26264  9951705040001701  23472507560001701  31953000728635J        103   
26265  9951705040001701  23472505270001701   35905011638458        109   
26266  9951705040001701  23472505200001701   35905008593716        103   
26267  9951705040001701  23472492690001701  31951P00459745Y        103   
26268  9951705040001701  23472492670001701  31951P007528385        104   
26269  9951705040001701  23472492510001701  31951P007550019        104   
26270  9951705040001701  23472492310001701  31951P00737826Z        105   
26271  99517050400017

In [86]:
df_items = pd.merge(pe_df,p_loc_df,how='left',left_on='MMS_ID',right_on='MMS ID')
df_items

ISSN                                  ISSN_cluster  \
0       [0000-0787]             [0000-0787, 0000-0469, 0000-0019]   
1       [2150-4008]             [2150-4008, 0094-257X, 0000-0019]   
2       [0000-0469]             [0000-0787, 0000-0469, 0000-0019]   
3       [0000-0019]  [0000-0469, 2150-4008, 0094-257X, 0000-0019]   
4                []                                            []   
5                []                                            []   
6                []                                            []   
7       [0741-7233]                                   [0741-7233]   
8                []                                            []   
9                []                                   [2080-8097]   
10               []                                            []   
11               []                                            []   
12               []                                            []   
13               []                                            []   
14      [2411-1406]                        [2411-1406, 2072-6414]   
15      [2055-5520]                                   [2055-5520]   
16               []                                            []   
17               []                                   [2059-5131]   
18               []                                            []   
19               []                                            []   
20               []                                            []   
21               []                                            []   
22               []                                            []   
23               []                                            []   
24      [0713-3936]                                   [0713-3936]   
25      [1929-7084]                        [0713-3936, 1929-7084]   
26               []                                            []   
27      [0557-3912]                                   [0557-3912]   
28               []                                            []   
29               []                                            []   
...             ...                                           ...   
173262           []                                            []   
173263           []                                   [0164-0968]   
173264           []                                            []   
173265           []                                            []   
173266           []                                            []   
173267           []                                            []   
173268           []                                            []   
173269           []                                            []   
173270           []                                            []   
173271           []                                            []   
173272           []                                            []   
173273  [0131-6095]                                   [0131-6095]   
173274           []                                   [0131-6095]   
173275           []                                            []   
173276           []                                            []   
173277           []                                            []   
173278  [0893-7184]                                   [0893-7184]   
173279           []                                            []   
173280  [0737-4194]                                   [0737-4194]   
173281           []                                            []   
173282  [2470-7597]                        [2470-7597, 2470-7589]   
173283           []                                            []   
173284  [2470-7708]                        [2470-766X, 2470-7708]   
173285           []                                            []   
173286           []                                            []   
173287           []                                            []   
173288  [0098

In [16]:
df_items[df_items['Barcode'].notnull()]

ISSN                       ISSN_cluster            MMS_ID  \
5602    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5603    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5604    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5605    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5606    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5607    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5608    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5609    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5610    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5611    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5612    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5613    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5614    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5615    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5616    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5617    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5618    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5619    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5620    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5621    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5622    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5623    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5624    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5625    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5626    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5627    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5628    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5629    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5630    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
5631    [0952-8385]  [0959-5341, 0952-8385, 0035-9238]  9961000350001701   
...             ...                                ...               ...   
171484  [0037-6752]                        [0037-6752]  9923267410001701   
171485  [0037-6752]                        [0037-6752]  9923267410001701   
171486  [0037-6752]                        [0037-6752]  9923267410001701   
171487  [0037-6752]                        [0037-6752]  9923267410001701   
171488  [0037-6752]                        [0037-6752]  9923267410001701   
171489  [0037-6752]                        [0037-6752]  9923267410001701   
172549  [0066-6637]                        [0066-6637]  9957111480001701   
172550  [0066-6637]                        [0066-6637]  9957111480001701   
172551  [0066-6637]                        [0066-6637]  9957111480001701   
172552  [0066-6637]                        [0066-6637]  9957111480001701   
172553  [0066-6637]                        [0066-6637]  9957111480001701   
172554  [0066-6637]                        [0066-6637]  9957111480001701   
172555  [0066-6637]                        [0066-6637]  9957111480001701   
172556  [0066-6637]                        [0066-6637]  9957111480001701   
172557  [0066-6637]                        [0066-6637]  9957111480001701   
172558  [0066-6637]                        [0066-6637]  9957111480001701   
172559  [0066-6637]                        [0066-6637]  9957111480001701   
172560  [0066-6637]                        [0066-6637]  9957111480001701   
172561  [0066-6637]                        [0066-6637]  9957111480001701   
172562  [0066-6637]                        [0066-6637]  9957111480001701   
172563  [0066-6637]                        [0066-6637]  9957111

In [10]:
pcad0 = pd.read_csv('PCAD-collection-IDs-to-title-info-0.csv',sep='\t',dtype=str)
pcad0

Electronic Collection Id  \
0             61535209430001701   
1             61535209430001701   
2             61535209430001701   
3             61535209430001701   
4             61535209430001701   
5             61535209430001701   
6             61535209430001701   
7             61535209430001701   
8             61535209430001701   
9             61535209430001701   
10            61535209430001701   
11            61535209430001701   
12            61535209430001701   
13            61535209430001701   
14            61535209430001701   
15            61535209430001701   
16            61535209430001701   
17            61535209430001701   
18            61535209430001701   
19            61535209430001701   
20            61535209430001701   
21            61535209430001701   
22            61535209430001701   
23            61535209430001701   
24            61535209430001701   
25            61535209430001701   
26            61535209430001701   
27            61535209430001701   
28            61535209430001701   
29            61535209430001701   
...                         ...   
399970        61646192490001701   
399971        61646192490001701   
399972        61646192490001701   
399973        61646192490001701   
399974        61646192490001701   
399975        61646192490001701   
399976        61646192490001701   
399977        61646192490001701   
399978        61646192490001701   
399979        61646192490001701   
399980        61646192490001701   
399981        61646192490001701   
399982        61646192490001701   
399983        61646192490001701   
399984        61646192490001701   
399985        61646192490001701   
399986        61646192490001701   
399987        61646192490001701   
399988        61646192490001701   
399989        61646192490001701   
399990        61646192490001701   
399991        61646192490001701   
399992        61646192490001701   
399993        61646192490001701   
399994        61646192490001701   
399995        61646192490001701   
399996        61646192490001701   
399997        61646192490001701   
399998        61646192490001701   
399999        61646192490001701   

                                              Public Name            MMS Id  \
0                  American Medical Association Backfiles  9966629010001701   
1                  American Medical Association Backfiles  9966757510001701   
2                  American Medical Association Backfiles  9966759170001701   
3                  American Medical Association Backfiles  9966774590001701   
4                  American Medical Association Backfiles  9966774910001701   
5                  American Medical Association Backfiles  9966787540001701   
6                  American Medical Association Backfiles  9966943130001701   
7                  American Medical Association Backfiles  9966943140001701   
8                  American Medical Association Backfiles  9966943150001701   
9                  American Medical Association Backfiles  9966943160001701   
10                 American Medical Association Backfiles  9966943170001701   
11                 American Medical Association Backfiles  9966943180001701   
12                 American Medical Association Backfiles  9966943190001701   
13                 American Medical Association Backfiles  9966956590001701   
14                 American Medical Association Backfiles  9967320470001701   
15                 American Medical Association Backfiles  9967329290001701   
16                 American Medical Association Backfiles  9967759390001701   
17                 American Medical Association Backfiles  9967826480001701   
18                 American Medical Association Backfiles  9968411380001701   
19                 American Medical Association Backfiles  9968426080001701   
20                 American Medical Association Backfiles  9968426100001701   
21                 American Medical Association Backfiles  9968437560001701   
22                 

In [11]:
pcad1 = pd.read_csv('PCAD-collection-IDs-to-title-info-1.csv',sep='\t',dtype=str)
pcad1

Electronic Collection Id  \
0             61646192490001701   
1             61646192490001701   
2             61646192490001701   
3             61646192490001701   
4             61646192490001701   
5             61646192490001701   
6             61646192490001701   
7             61646192490001701   
8             61646192490001701   
9             61646192490001701   
10            61646192490001701   
11            61646192490001701   
12            61646192490001701   
13            61646192490001701   
14            61646192490001701   
15            61646192490001701   
16            61646192490001701   
17            61646192490001701   
18            61646192490001701   
19            61646192490001701   
20            61646192490001701   
21            61646192490001701   
22            61646192490001701   
23            61646192490001701   
24            61646192490001701   
25            61646192490001701   
26            61646192490001701   
27            61646192490001701   
28            61646192490001701   
29            61646192490001701   
...                         ...   
243994        61704432090001701   
243995        61704432090001701   
243996        61704432090001701   
243997        61704432090001701   
243998        61704432090001701   
243999        61704432090001701   
244000        61704432090001701   
244001        61704432090001701   
244002        61704432090001701   
244003        61704432090001701   
244004        61704432090001701   
244005        61704432090001701   
244006        61704432090001701   
244007        61704432090001701   
244008        61704432090001701   
244009        61704432090001701   
244010        61710975640001701   
244011        61710975640001701   
244012        61710975640001701   
244013        61711008050001701   
244014        61711008050001701   
244015        61711453530001701   
244016        61711453530001701   
244017        61711453530001701   
244018        61711453530001701   
244019        61711453530001701   
244020        61711453530001701   
244021        61711453530001701   
244022        61711453530001701   
244023        61711453530001701   

                                              Public Name            MMS Id  \
0       EBSCOhost American Antiquarian Society Histori...  9974125301101701   
1       EBSCOhost American Antiquarian Society Histori...  9974125301201701   
2       EBSCOhost American Antiquarian Society Histori...  9974125301301701   
3       EBSCOhost American Antiquarian Society Histori...  9974125301401701   
4       EBSCOhost American Antiquarian Society Histori...  9974125301501701   
5       EBSCOhost American Antiquarian Society Histori...  9974125301601701   
6       EBSCOhost American Antiquarian Society Histori...  9974125301701701   
7       EBSCOhost American Antiquarian Society Histori...  9974125301801701   
8       EBSCOhost American Antiquarian Society Histori...  9974125301901701   
9       EBSCOhost American Antiquarian Society Histori...  9974125301901701   
10      EBSCOhost American Antiquarian Society Histori...  9974125302001701   
11      EBSCOhost American Antiquarian Society Histori...  9974125302101701   
12      EBSCOhost American Antiquarian Society Histori...  9974125302201701   
13      EBSCOhost American Antiquarian Society Histori...  9974125302301701   
14      EBSCOhost American Antiquarian Society Histori...  9974125302401701   
15      EBSCOhost American Antiquarian Society Histori...  9974125302501701   
16      EBSCOhost American Antiquarian Society Histori...  9974125302601701   
17      EBSCOhost American Antiquarian Society Histori...  9974125302701701   
18      EBSCOhost American Antiquarian Society Histori...  9974125302801701   
19      EBSCOhost American Antiquarian Society Histori...  9974125302901701   
20      EBSCOhost American Antiquarian Society Histori...  9974125303001701   
21      EBSCOhost American Antiquarian Society Histori...  9974125303101701   
22      EBSCOhost A

In [85]:
pcad = pd.concat([pcad0,pcad1],ignore_index=True)
pcad

Electronic Collection Id  \
0             61535209430001701   
1             61535209430001701   
2             61535209430001701   
3             61535209430001701   
4             61535209430001701   
5             61535209430001701   
6             61535209430001701   
7             61535209430001701   
8             61535209430001701   
9             61535209430001701   
10            61535209430001701   
11            61535209430001701   
12            61535209430001701   
13            61535209430001701   
14            61535209430001701   
15            61535209430001701   
16            61535209430001701   
17            61535209430001701   
18            61535209430001701   
19            61535209430001701   
20            61535209430001701   
21            61535209430001701   
22            61535209430001701   
23            61535209430001701   
24            61535209430001701   
25            61535209430001701   
26            61535209430001701   
27            61535209430001701   
28            61535209430001701   
29            61535209430001701   
...                         ...   
643994        61704432090001701   
643995        61704432090001701   
643996        61704432090001701   
643997        61704432090001701   
643998        61704432090001701   
643999        61704432090001701   
644000        61704432090001701   
644001        61704432090001701   
644002        61704432090001701   
644003        61704432090001701   
644004        61704432090001701   
644005        61704432090001701   
644006        61704432090001701   
644007        61704432090001701   
644008        61704432090001701   
644009        61704432090001701   
644010        61710975640001701   
644011        61710975640001701   
644012        61710975640001701   
644013        61711008050001701   
644014        61711008050001701   
644015        61711453530001701   
644016        61711453530001701   
644017        61711453530001701   
644018        61711453530001701   
644019        61711453530001701   
644020        61711453530001701   
644021        61711453530001701   
644022        61711453530001701   
644023        61711453530001701   

                                              Public Name            MMS Id  \
0                  American Medical Association Backfiles  9966629010001701   
1                  American Medical Association Backfiles  9966757510001701   
2                  American Medical Association Backfiles  9966759170001701   
3                  American Medical Association Backfiles  9966774590001701   
4                  American Medical Association Backfiles  9966774910001701   
5                  American Medical Association Backfiles  9966787540001701   
6                  American Medical Association Backfiles  9966943130001701   
7                  American Medical Association Backfiles  9966943140001701   
8                  American Medical Association Backfiles  9966943150001701   
9                  American Medical Association Backfiles  9966943160001701   
10                 American Medical Association Backfiles  9966943170001701   
11                 American Medical Association Backfiles  9966943180001701   
12                 American Medical Association Backfiles  9966943190001701   
13                 American Medical Association Backfiles  9966956590001701   
14                 American Medical Association Backfiles  9967320470001701   
15                 American Medical Association Backfiles  9967329290001701   
16                 American Medical Association Backfiles  9967759390001701   
17                 American Medical Association Backfiles  9967826480001701   
18                 American Medical Association Backfiles  9968411380001701   
19                 American Medical Association Backfiles  9968426080001701   
20                 American Medical Association Backfiles  9968426100001701   
21                 American Medical Association Backfiles  9968437560001701   
22                 

In [87]:
pcad.drop_duplicates(inplace=True)
pcad

Electronic Collection Id  \
0             61535209430001701   
1             61535209430001701   
2             61535209430001701   
3             61535209430001701   
4             61535209430001701   
5             61535209430001701   
6             61535209430001701   
7             61535209430001701   
8             61535209430001701   
9             61535209430001701   
10            61535209430001701   
11            61535209430001701   
12            61535209430001701   
13            61535209430001701   
14            61535209430001701   
15            61535209430001701   
16            61535209430001701   
17            61535209430001701   
18            61535209430001701   
19            61535209430001701   
20            61535209430001701   
21            61535209430001701   
22            61535209430001701   
23            61535209430001701   
24            61535209430001701   
25            61535209430001701   
26            61535209430001701   
27            61535209430001701   
28            61535209430001701   
29            61535209430001701   
...                         ...   
643994        61704432090001701   
643995        61704432090001701   
643996        61704432090001701   
643997        61704432090001701   
643998        61704432090001701   
643999        61704432090001701   
644000        61704432090001701   
644001        61704432090001701   
644002        61704432090001701   
644003        61704432090001701   
644004        61704432090001701   
644005        61704432090001701   
644006        61704432090001701   
644007        61704432090001701   
644008        61704432090001701   
644009        61704432090001701   
644010        61710975640001701   
644011        61710975640001701   
644012        61710975640001701   
644013        61711008050001701   
644014        61711008050001701   
644015        61711453530001701   
644016        61711453530001701   
644017        61711453530001701   
644018        61711453530001701   
644019        61711453530001701   
644020        61711453530001701   
644021        61711453530001701   
644022        61711453530001701   
644023        61711453530001701   

                                              Public Name            MMS Id  \
0                  American Medical Association Backfiles  9966629010001701   
1                  American Medical Association Backfiles  9966757510001701   
2                  American Medical Association Backfiles  9966759170001701   
3                  American Medical Association Backfiles  9966774590001701   
4                  American Medical Association Backfiles  9966774910001701   
5                  American Medical Association Backfiles  9966787540001701   
6                  American Medical Association Backfiles  9966943130001701   
7                  American Medical Association Backfiles  9966943140001701   
8                  American Medical Association Backfiles  9966943150001701   
9                  American Medical Association Backfiles  9966943160001701   
10                 American Medical Association Backfiles  9966943170001701   
11                 American Medical Association Backfiles  9966943180001701   
12                 American Medical Association Backfiles  9966943190001701   
13                 American Medical Association Backfiles  9966956590001701   
14                 American Medical Association Backfiles  9967320470001701   
15                 American Medical Association Backfiles  9967329290001701   
16                 American Medical Association Backfiles  9967759390001701   
17                 American Medical Association Backfiles  9967826480001701   
18                 American Medical Association Backfiles  9968411380001701   
19                 American Medical Association Backfiles  9968426080001701   
20                 American Medical Association Backfiles  9968426100001701   
21                 American Medical Association Backfiles  9968437560001701   
22                 

In [88]:
df_items.index.names = ['record_index']
df_items.reset_index(inplace=True)
df_items

record_index         ISSN  \
0                  0  [0000-0787]   
1                  1  [2150-4008]   
2                  2  [0000-0469]   
3                  3  [0000-0019]   
4                  4           []   
5                  5           []   
6                  6           []   
7                  7  [0741-7233]   
8                  8           []   
9                  9           []   
10                10           []   
11                11           []   
12                12           []   
13                13           []   
14                14  [2411-1406]   
15                15  [2055-5520]   
16                16           []   
17                17           []   
18                18           []   
19                19           []   
20                20           []   
21                21           []   
22                22           []   
23                23           []   
24                24  [0713-3936]   
25                25  [1929-7084]   
26                26           []   
27                27  [0557-3912]   
28                28           []   
29                29           []   
...              ...          ...   
173262        173262           []   
173263        173263           []   
173264        173264           []   
173265        173265           []   
173266        173266           []   
173267        173267           []   
173268        173268           []   
173269        173269           []   
173270        173270           []   
173271        173271           []   
173272        173272           []   
173273        173273  [0131-6095]   
173274        173274           []   
173275        173275           []   
173276        173276           []   
173277        173277           []   
173278        173278  [0893-7184]   
173279        173279           []   
173280        173280  [0737-4194]   
173281        173281           []   
173282        173282  [2470-7597]   
173283        173283           []   
173284        173284  [2470-7708]   
173285        173285           []   
173286        173286           []   
173287        173287           []   
173288        173288  [0098-6143]   
173289        173289  [0007-7011]   
173290        173290           []   
173291        173291  [0078-0170]   

                                        ISSN_cluster            MMS_ID  \
0                  [0000-0787, 0000-0469, 0000-0019]  9937257820001701   
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
2                  [0000-0787, 0000-0469, 0000-0019]  9913446020001701   
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
4                                                 []  9940052290001701   
5                                                 []  9915732180001701   
6                                                 []  9967355600001701   
7                                        [0741-7233]  9959067250001701   
8                                                 []  9915654130001701   
9                                        [2080-8097]  9966896580001701   
10                                                []  9915303430001701   
11                                                []  9944643300001701   
12                                                []  9914906750001701   
13                                                []  9960994670001701   
14                            [2411-1406, 2072-6414]  9974071460801701   
15                                       [2055-5520]  9974080735401701   
16                                                []  9914678130001701   
17                                       [2059-5131]  9974744300301701   
18                                                []  9914603730001701   
19                                                []  9948999710001701   
20                                                []  9957169080001701   
21                                                []  9951631900001701   
22         

In [23]:
pcad_ynm = pd.read_excel('PCAD_collections_20180701.xlsx',dtype=str)
pcad_ynm.rename(columns={'Collection ID':'Electronic Collection Id'},inplace=True)
pcad_ynm

Electronic Collection Id  PCAD?
0          61695747580001701    Yes
1          61695748140001701  Maybe
2          61696658410001701    Yes
3          61696708350001701  Maybe
4          61697548150001701  Maybe
5          61697733150001701  Maybe
6          61697850880001701  Maybe
7          61697871840001701    Yes
8          61697929180001701    Yes
9          61697948260001701    Yes
10         61697958290001701    Yes
11         61698590920001701    Yes
12         61698780560001701    Yes
13         61699652780001701    Yes
14         61704077470001701  Maybe
15         61704432090001701  Maybe
16         61710975640001701    Yes
17         61711008050001701    Yes
18         61711453530001701  Maybe
19         61692585340001701  Maybe
20         61669277840001701  Maybe
21         61666178570001701  Maybe
22         61623345220001701  Maybe
23         61680396060001701  Maybe
24         61535216540001701  Maybe
25         61662684670001701  Maybe
26         61624402740001701  Maybe
27         61669131230001701  Maybe
28         61535215030001701  Maybe
29         61535216470001701  Maybe
..                       ...    ...
624        61535210260001701  Maybe
625        61535211320001701  Maybe
626        61712098260001701    Yes
627        61712264880001701    Yes
628        61647985620001701  Maybe
629        61647985400001701  Maybe
630        61696698250001701  Maybe
631        61695869100001701  Maybe
632        61695881460001701  Maybe
633        61695881300001701  Maybe
634        61695881240001701  Maybe
635        61695868770001701  Maybe
636        61712327330001701    Yes
637        61712327210001701    Yes
638        61712327310001701    Yes
639        61712625980001701    Yes
640        61712327270001701    Yes
641        61712327250001701    Yes
642        61712327230001701    Yes
643        61662868970001701  Maybe
644        61704070540001701  Maybe
645        61697367970001701    Yes
646        61637917640001701  Maybe
647        61712806570001701  Maybe
648        61535212260001701  Maybe
649        61549770730001701  Maybe
650        61561919610001701  Maybe
651        61647790170001701  Maybe
652        61651058670001701  Maybe
653        61692663030001701    Yes

[654 rows x 2 columns]

In [89]:
pcad = pd.merge(pcad,pcad_ynm,how='inner',left_on='Electronic Collection Id',right_on='Electronic Collection Id')
pcad

Electronic Collection Id  \
0             61535209430001701   
1             61535209430001701   
2             61535209430001701   
3             61535209430001701   
4             61535209430001701   
5             61535209430001701   
6             61535209430001701   
7             61535209430001701   
8             61535209430001701   
9             61535209430001701   
10            61535209430001701   
11            61535209430001701   
12            61535209430001701   
13            61535209430001701   
14            61535209430001701   
15            61535209430001701   
16            61535209430001701   
17            61535209430001701   
18            61535209430001701   
19            61535209430001701   
20            61535209430001701   
21            61535209430001701   
22            61535209430001701   
23            61535209430001701   
24            61535209430001701   
25            61535209430001701   
26            61535209430001701   
27            61535209430001701   
28            61535209430001701   
29            61535209430001701   
...                         ...   
643994        61704432090001701   
643995        61704432090001701   
643996        61704432090001701   
643997        61704432090001701   
643998        61704432090001701   
643999        61704432090001701   
644000        61704432090001701   
644001        61704432090001701   
644002        61704432090001701   
644003        61704432090001701   
644004        61704432090001701   
644005        61704432090001701   
644006        61704432090001701   
644007        61704432090001701   
644008        61704432090001701   
644009        61704432090001701   
644010        61710975640001701   
644011        61710975640001701   
644012        61710975640001701   
644013        61711008050001701   
644014        61711008050001701   
644015        61711453530001701   
644016        61711453530001701   
644017        61711453530001701   
644018        61711453530001701   
644019        61711453530001701   
644020        61711453530001701   
644021        61711453530001701   
644022        61711453530001701   
644023        61711453530001701   

                                              Public Name            MMS Id  \
0                  American Medical Association Backfiles  9966629010001701   
1                  American Medical Association Backfiles  9966757510001701   
2                  American Medical Association Backfiles  9966759170001701   
3                  American Medical Association Backfiles  9966774590001701   
4                  American Medical Association Backfiles  9966774910001701   
5                  American Medical Association Backfiles  9966787540001701   
6                  American Medical Association Backfiles  9966943130001701   
7                  American Medical Association Backfiles  9966943140001701   
8                  American Medical Association Backfiles  9966943150001701   
9                  American Medical Association Backfiles  9966943160001701   
10                 American Medical Association Backfiles  9966943170001701   
11                 American Medical Association Backfiles  9966943180001701   
12                 American Medical Association Backfiles  9966943190001701   
13                 American Medical Association Backfiles  9966956590001701   
14                 American Medical Association Backfiles  9967320470001701   
15                 American Medical Association Backfiles  9967329290001701   
16                 American Medical Association Backfiles  9967759390001701   
17                 American Medical Association Backfiles  9967826480001701   
18                 American Medical Association Backfiles  9968411380001701   
19                 American Medical Association Backfiles  9968426080001701   
20                 American Medical Association Backfiles  9968426100001701   
21                 American Medical Association Backfiles  9968437560001701   
22                 

In [90]:
df_pcad = pd.merge(df_items, pcad, how='left', left_on='MMS_ID',right_on='MMS Id',suffixes=['_bib','_portfolio'])
df_pcad

record_index     ISSN_bib  \
0                  0  [0000-0787]   
1                  1  [2150-4008]   
2                  2  [0000-0469]   
3                  3  [0000-0019]   
4                  4           []   
5                  5           []   
6                  6           []   
7                  7  [0741-7233]   
8                  8           []   
9                  9           []   
10                 9           []   
11                10           []   
12                11           []   
13                12           []   
14                13           []   
15                14  [2411-1406]   
16                15  [2055-5520]   
17                15  [2055-5520]   
18                15  [2055-5520]   
19                16           []   
20                17           []   
21                17           []   
22                17           []   
23                18           []   
24                19           []   
25                20           []   
26                21           []   
27                22           []   
28                23           []   
29                24  [0713-3936]   
...              ...          ...   
209912        173263           []   
209913        173264           []   
209914        173264           []   
209915        173265           []   
209916        173266           []   
209917        173267           []   
209918        173268           []   
209919        173269           []   
209920        173270           []   
209921        173271           []   
209922        173272           []   
209923        173273  [0131-6095]   
209924        173274           []   
209925        173275           []   
209926        173276           []   
209927        173277           []   
209928        173278  [0893-7184]   
209929        173279           []   
209930        173280  [0737-4194]   
209931        173281           []   
209932        173282  [2470-7597]   
209933        173283           []   
209934        173284  [2470-7708]   
209935        173285           []   
209936        173286           []   
209937        173287           []   
209938        173288  [0098-6143]   
209939        173289  [0007-7011]   
209940        173290           []   
209941        173291  [0078-0170]   

                                        ISSN_cluster            MMS_ID  \
0                  [0000-0787, 0000-0469, 0000-0019]  9937257820001701   
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
2                  [0000-0787, 0000-0469, 0000-0019]  9913446020001701   
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
4                                                 []  9940052290001701   
5                                                 []  9915732180001701   
6                                                 []  9967355600001701   
7                                        [0741-7233]  9959067250001701   
8                                                 []  9915654130001701   
9                                        [2080-8097]  9966896580001701   
10                                       [2080-8097]  9966896580001701   
11                                                []  9915303430001701   
12                                                []  9944643300001701   
13                                                []  9914906750001701   
14                                                []  9960994670001701   
15                            [2411-1406, 2072-6414]  9974071460801701   
16                                       [2055-5520]  9974080735401701   
17                                       [2055-5520]  9974080735401701   
18                                       [2055-5520]  9974080735401701   
19                                                []  9914678130001701   
20                                       [2059-5131]  9974744300301701   
21                                       [2059-5131]  9974744300301701   
22         

In [84]:
df_pcad.columns

Index(['ISSN_bib', 'ISSN_cluster', 'MMS_ID', 'OCN', 'OCN_cluster', 'Title_bib',
       'chron', 'descr', 'e_holdings', 'enum', 'p_or_e', 'ISSN_group_id',
       'OCN_group_id', 'both_groups', 'matches_group_id', 'MMS ID', 'Item PID',
       'Barcode', 'Enum_item', 'Chron_item', 'Descr_item', 'Permanent Library',
       'Permanent Location', 'Electronic Collection Id', 'Public Name',
       'MMS Id', 'Title_portfolio', 'Begin Publication Date',
       'End Publication Date', 'ISSN_portfolio',
       'Coverage Information Combined', 'Coverage Statement', 'Portfolio Id',
       'Lifecycle', 'Embargo Operator', 'Embargo Months', 'Embargo Years',
       'Status (Active)', 'PCAD?', 'ISSN_to_match'],
      dtype='object')

In [91]:
df_pcad['ISSN_to_match'] = df_pcad['ISSN_bib'].apply(lambda x: str(x[0]))
df_pcad

record_index     ISSN_bib  \
0                  0  [0000-0787]   
1                  1  [2150-4008]   
2                  2  [0000-0469]   
3                  3  [0000-0019]   
4                  4           []   
5                  5           []   
6                  6           []   
7                  7  [0741-7233]   
8                  8           []   
9                  9           []   
10                 9           []   
11                10           []   
12                11           []   
13                12           []   
14                13           []   
15                14  [2411-1406]   
16                15  [2055-5520]   
17                15  [2055-5520]   
18                15  [2055-5520]   
19                16           []   
20                17           []   
21                17           []   
22                17           []   
23                18           []   
24                19           []   
25                20           []   
26                21           []   
27                22           []   
28                23           []   
29                24  [0713-3936]   
...              ...          ...   
209912        173263           []   
209913        173264           []   
209914        173264           []   
209915        173265           []   
209916        173266           []   
209917        173267           []   
209918        173268           []   
209919        173269           []   
209920        173270           []   
209921        173271           []   
209922        173272           []   
209923        173273  [0131-6095]   
209924        173274           []   
209925        173275           []   
209926        173276           []   
209927        173277           []   
209928        173278  [0893-7184]   
209929        173279           []   
209930        173280  [0737-4194]   
209931        173281           []   
209932        173282  [2470-7597]   
209933        173283           []   
209934        173284  [2470-7708]   
209935        173285           []   
209936        173286           []   
209937        173287           []   
209938        173288  [0098-6143]   
209939        173289  [0007-7011]   
209940        173290           []   
209941        173291  [0078-0170]   

                                        ISSN_cluster            MMS_ID  \
0                  [0000-0787, 0000-0469, 0000-0019]  9937257820001701   
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
2                  [0000-0787, 0000-0469, 0000-0019]  9913446020001701   
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
4                                                 []  9940052290001701   
5                                                 []  9915732180001701   
6                                                 []  9967355600001701   
7                                        [0741-7233]  9959067250001701   
8                                                 []  9915654130001701   
9                                        [2080-8097]  9966896580001701   
10                                       [2080-8097]  9966896580001701   
11                                                []  9915303430001701   
12                                                []  9944643300001701   
13                                                []  9914906750001701   
14                                                []  9960994670001701   
15                            [2411-1406, 2072-6414]  9974071460801701   
16                                       [2055-5520]  9974080735401701   
17                                       [2055-5520]  9974080735401701   
18                                       [2055-5520]  9974080735401701   
19                                                []  9914678130001701   
20                                       [2059-5131]  9974744300301701   
21                                       [2059-5131]  9974744300301701   
22         

In [64]:
btaa = pd.read_excel('BTAA-SPR.xlsx')
btaa

ISSN Number                                    Title 1 (Print)  \
0      0001-0782                         Communications of the ACM.   
1      0001-1541                                     AIChE journal.   
2      0001-2092                                      AORN journal.   
3      0001-2815                                   Tissue antigens.   
4      0001-2998                      Seminars in nuclear medicine.   
5      0001-4346      Mathematical notes = Matematicheskie zametki.   
6      0001-4370                                        Oceanology.   
7      0001-4575                  Accident analysis and prevention.   
8      0001-4842                     Accounts of chemical research.   
9      0001-4966  The Journal of the Acoustical Society of America.   
10     0001-5180                                    Acta anatomica.   
11     0001-5342  Acta biotheoretica : ediderunt Directores Fund...   
12     0001-5652                                    Human heredity.   
13     0001-5717            Di zhi xue bao = Acta geologica Sinica.   
14     0001-5903                                  Acta informatica.   
15     0001-5962                                  Acta mathematica.   
16     0001-5970                                    Acta mechanica.   
17     0001-6160                                 Acta metallurgica.   
18     0001-6268                              Acta neurochirurgica.   
19     0001-6314                     Acta neurologica Scandinavica.   
20     0001-6322                             Acta neuropathologica.   
21     0001-6349     Acta obstetricia et gynecologica scandinavica.   
22     0001-639X                 Acta ophthalmologica Scandinavica.   
23     0001-6683               Acta pharmacologica et toxicologica.   
24     0001-6772                    Acta physiologica Scandinavica.   
25     0001-690X                    Acta psychiatrica Scandinavica.   
26     0001-6969                   Acta scientiarum mathematicarum.   
27     0001-6993                                  Acta sociologica.   
28     0001-8244                                 Behavior genetics.   
29     0001-8392                  Administrative science quarterly.   
...          ...                                                ...   
9624   2329-7131                                 The French review.   
9625   2331-219X                                    Special papers.   
9626   2332-4252                            Operative neurosurgery.   
9627   2372-5664  Middle west review : an interdisciplinary jour...   
9628   2375-6314          Aerospace medicine and human performance.   
9629   2377-5726                                       Proceedings.   
9630   2399-8083                          Environment and planning.   
9631   2399-8091                          Environment and planning.   
9632   2405-4984                              Journal of Japonisme.   
9633   2451-828X  Chinese as a second language : Journal of the ...   
9634   2451-8298  Chinese as a second language : Journal of the ...   
9635   2468-1458                 Agriculture and natural resources.   
9636   2476-1397                   Journal of global south studies.   
9637   3900-7303                            Forum modernes Theater.   
9638   8750-1317                                     The Oregonian.   
9639   8755-1187  ASAE standards : standards, engineering practi...   
9640   8755-1225                The Journal of pharmacy technology.   
9641   8755-2930  Earthquake spectra : the professional journal ...   
9642   8755-9668     Advances in free radical biology and medicine.   
9643   8756-0437                     Seminars in surgical oncology.   
9644   8756-0879                Journal of plastic film & sheeting.   
9645   8756-5641                     Developmental neuropsychology.   
9646   8756-6222          Journal of law, economics & organization.   
9647   8756-6583                    Holocaust and genocide studies.   
9648   8756-7016             

In [65]:
btaa_cols = list(btaa.columns)
btaa_cols

['ISSN Number',
 'Title 1 (Print)',
 'Publisher (Print)',
 'Title 2 (Print)',
 'Publisher (Print).1',
 'Title 3 (Print)',
 'Publisher (Print).2',
 '(more bib records?)',
 'Match?',
 'SPR Holdings',
 'SPR Missing']

In [66]:
btaa_cols_edit = []
for x in btaa_cols:
    btaa_cols_edit.append(str(x) + '_BTAA-SPR')
btaa_cols_edit

['ISSN Number_BTAA-SPR',
 'Title 1 (Print)_BTAA-SPR',
 'Publisher (Print)_BTAA-SPR',
 'Title 2 (Print)_BTAA-SPR',
 'Publisher (Print).1_BTAA-SPR',
 'Title 3 (Print)_BTAA-SPR',
 'Publisher (Print).2_BTAA-SPR',
 '(more bib records?)_BTAA-SPR',
 'Match?_BTAA-SPR',
 'SPR Holdings_BTAA-SPR',
 'SPR Missing_BTAA-SPR']

In [67]:
btaa_dict = dict(zip(btaa_cols, btaa_cols_edit))
btaa_dict

{'(more bib records?)': '(more bib records?)_BTAA-SPR',
 'ISSN Number': 'ISSN Number_BTAA-SPR',
 'Match?': 'Match?_BTAA-SPR',
 'Publisher (Print)': 'Publisher (Print)_BTAA-SPR',
 'Publisher (Print).1': 'Publisher (Print).1_BTAA-SPR',
 'Publisher (Print).2': 'Publisher (Print).2_BTAA-SPR',
 'SPR Holdings': 'SPR Holdings_BTAA-SPR',
 'SPR Missing': 'SPR Missing_BTAA-SPR',
 'Title 1 (Print)': 'Title 1 (Print)_BTAA-SPR',
 'Title 2 (Print)': 'Title 2 (Print)_BTAA-SPR',
 'Title 3 (Print)': 'Title 3 (Print)_BTAA-SPR'}

In [68]:
btaa.rename(index=str, columns = btaa_dict, inplace=True)
btaa

ISSN Number_BTAA-SPR                           Title 1 (Print)_BTAA-SPR  \
0               0001-0782                         Communications of the ACM.   
1               0001-1541                                     AIChE journal.   
2               0001-2092                                      AORN journal.   
3               0001-2815                                   Tissue antigens.   
4               0001-2998                      Seminars in nuclear medicine.   
5               0001-4346      Mathematical notes = Matematicheskie zametki.   
6               0001-4370                                        Oceanology.   
7               0001-4575                  Accident analysis and prevention.   
8               0001-4842                     Accounts of chemical research.   
9               0001-4966  The Journal of the Acoustical Society of America.   
10              0001-5180                                    Acta anatomica.   
11              0001-5342  Acta biotheoretica : ediderunt Directores Fund...   
12              0001-5652                                    Human heredity.   
13              0001-5717            Di zhi xue bao = Acta geologica Sinica.   
14              0001-5903                                  Acta informatica.   
15              0001-5962                                  Acta mathematica.   
16              0001-5970                                    Acta mechanica.   
17              0001-6160                                 Acta metallurgica.   
18              0001-6268                              Acta neurochirurgica.   
19              0001-6314                     Acta neurologica Scandinavica.   
20              0001-6322                             Acta neuropathologica.   
21              0001-6349     Acta obstetricia et gynecologica scandinavica.   
22              0001-639X                 Acta ophthalmologica Scandinavica.   
23              0001-6683               Acta pharmacologica et toxicologica.   
24              0001-6772                    Acta physiologica Scandinavica.   
25              0001-690X                    Acta psychiatrica Scandinavica.   
26              0001-6969                   Acta scientiarum mathematicarum.   
27              0001-6993                                  Acta sociologica.   
28              0001-8244                                 Behavior genetics.   
29              0001-8392                  Administrative science quarterly.   
...                   ...                                                ...   
9624            2329-7131                                 The French review.   
9625            2331-219X                                    Special papers.   
9626            2332-4252                            Operative neurosurgery.   
9627            2372-5664  Middle west review : an interdisciplinary jour...   
9628            2375-6314          Aerospace medicine and human performance.   
9629            2377-5726                                       Proceedings.   
9630            2399-8083                          Environment and planning.   
9631            2399-8091                          Environment and planning.   
9632            2405-4984                              Journal of Japonisme.   
9633            2451-828X  Chinese as a second language : Journal of the ...   
9634            2451-8298  Chinese as a second language : Journal of the ...   
9635            2468-1458                 Agriculture and natural resources.   
9636            2476-1397                   Journal of global south studies.   
9637            3900-7303                            Forum modernes Theater.   
9638            8750-1317                                     The Oregonian.   
9639            8755-1187  ASAE standards : standards, engineering practi...   
9640            8755-1225                The Journal of pharmacy technology.   
9641            8755-2930  Earthquake spectra : the professional journal ...   
9642 

In [92]:
df_pcad_btaa = pd.merge(df_pcad,btaa,how='left',left_on='ISSN_to_match',right_on='ISSN Number_BTAA-SPR')
df_pcad_btaa

record_index     ISSN_bib  \
0                  0  [0000-0787]   
1                  1  [2150-4008]   
2                  2  [0000-0469]   
3                  3  [0000-0019]   
4                  4           []   
5                  5           []   
6                  6           []   
7                  7  [0741-7233]   
8                  8           []   
9                  9           []   
10                 9           []   
11                10           []   
12                11           []   
13                12           []   
14                13           []   
15                14  [2411-1406]   
16                15  [2055-5520]   
17                15  [2055-5520]   
18                15  [2055-5520]   
19                16           []   
20                17           []   
21                17           []   
22                17           []   
23                18           []   
24                19           []   
25                20           []   
26                21           []   
27                22           []   
28                23           []   
29                24  [0713-3936]   
...              ...          ...   
209912        173263           []   
209913        173264           []   
209914        173264           []   
209915        173265           []   
209916        173266           []   
209917        173267           []   
209918        173268           []   
209919        173269           []   
209920        173270           []   
209921        173271           []   
209922        173272           []   
209923        173273  [0131-6095]   
209924        173274           []   
209925        173275           []   
209926        173276           []   
209927        173277           []   
209928        173278  [0893-7184]   
209929        173279           []   
209930        173280  [0737-4194]   
209931        173281           []   
209932        173282  [2470-7597]   
209933        173283           []   
209934        173284  [2470-7708]   
209935        173285           []   
209936        173286           []   
209937        173287           []   
209938        173288  [0098-6143]   
209939        173289  [0007-7011]   
209940        173290           []   
209941        173291  [0078-0170]   

                                        ISSN_cluster            MMS_ID  \
0                  [0000-0787, 0000-0469, 0000-0019]  9937257820001701   
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
2                  [0000-0787, 0000-0469, 0000-0019]  9913446020001701   
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
4                                                 []  9940052290001701   
5                                                 []  9915732180001701   
6                                                 []  9967355600001701   
7                                        [0741-7233]  9959067250001701   
8                                                 []  9915654130001701   
9                                        [2080-8097]  9966896580001701   
10                                       [2080-8097]  9966896580001701   
11                                                []  9915303430001701   
12                                                []  9944643300001701   
13                                                []  9914906750001701   
14                                                []  9960994670001701   
15                            [2411-1406, 2072-6414]  9974071460801701   
16                                       [2055-5520]  9974080735401701   
17                                       [2055-5520]  9974080735401701   
18                                       [2055-5520]  9974080735401701   
19                                                []  9914678130001701   
20                                       [2059-5131]  9974744300301701   
21                                       [2059-5131]  9974744300301701   
22         

In [71]:
portico = pd.read_excel('Portico.xlsx',sheet_name='Comparison to Portico')
portico

Library Input Row ISSN Number  \
0                     1   0000-0019   
1                     2   0000-2100   
2                     3   0001-0196   
3                     4   0001-026X   
4                     5   0001-0782   
5                     6   0001-1452   
6                     7   0001-1541   
7                     8   0001-2092   
8                     9   0001-2351   
9                    10   0001-253X   
10                   11   0001-2815   
11                   12   0001-2890   
12                   13   0001-2998   
13                   14   0001-3072   
14                   15   0001-3455   
15                   16   0001-4001   
16                   17   0001-4273   
17                   18   0001-4346   
18                   19   0001-4370   
19                   20   0001-4575   
20                   21   0001-4788   
21                   22   0001-4826   
22                   23   0001-4842   
23                   24   0001-4966   
24                   25   0001-5172   
25                   26   0001-5180   
26                   27   0001-5199   
27                   28   0001-5342   
28                   29   0001-5547   
29                   30   0001-5652   
...                 ...         ...   
9624               9625   8750-7587   
9625               9626   8755-1039   
9626               9627   8755-1187   
9627               9628   8755-1209   
9628               9629   8755-1225   
9629               9630   8755-2930   
9630               9631   8755-3996   
9631               9632   8755-4615   
9632               9633   8755-6863   
9633               9634   8755-7223   
9634               9635   8755-9668   
9635               9636   8756-0437   
9636               9637   8756-0879   
9637               9638   8756-2324   
9638               9639   8756-3282   
9639               9640   8756-3894   
9640               9641   8756-5641   
9641               9642   8756-6222   
9642               9643   8756-6583   
9643               9644   8756-6621   
9644               9645   8756-663X   
9645               9646   8756-7016   
9646               9647   8756-7547   
9647               9648   8756-7555   
9648               9649   8756-758X   
9649               9650   8756-7938   
9650               9651   8756-8225   
9651               9652   8756-9264   
9652               9653   8756-971X   
9653               9654   8756-9728   

                                   Title 1 (Electronic)  \
0                                The Publishers weekly.   
1                       Ulrich's periodicals directory.   
2     Bulletin of the American Museum of Natural His...   
3     AAUP bulletin : quarterly publication of the A...   
4     Communications of the Association for Computin...   
5                                          AIAA journal   
6                                         AIChE journal   
7                                         AORN journal.   
8                             Transactions of the ASAE.   
9                                     Aslib proceedings   
10                                     Tissue antigens.   
11                              AV communication review   
12                        Seminars in nuclear medicine.   
13                                              Abacus.   
14                            Abstracts in anthropology   
15                                           Chirurgie.   
16                       Academy of Management journal.   
17    Mathematical notes of the Academy of Sciences ...   
18                                           Oceanology   
19                    Accident analysis and prevention.   
20                    Accounting and business research.   
21                                The accounting review   
22                        Accounts of chemical research   
23    The Journal of the Acoustical Society of America.   
24                  Acta anaesthesiologica Scandinavica   
25                                      Acta anatomic

In [72]:
portico['Linking ISSN list'] = portico['Linking ISSN'].apply(lambda x: str(x).split('|'))
portico

Library Input Row ISSN Number  \
0                     1   0000-0019   
1                     2   0000-2100   
2                     3   0001-0196   
3                     4   0001-026X   
4                     5   0001-0782   
5                     6   0001-1452   
6                     7   0001-1541   
7                     8   0001-2092   
8                     9   0001-2351   
9                    10   0001-253X   
10                   11   0001-2815   
11                   12   0001-2890   
12                   13   0001-2998   
13                   14   0001-3072   
14                   15   0001-3455   
15                   16   0001-4001   
16                   17   0001-4273   
17                   18   0001-4346   
18                   19   0001-4370   
19                   20   0001-4575   
20                   21   0001-4788   
21                   22   0001-4826   
22                   23   0001-4842   
23                   24   0001-4966   
24                   25   0001-5172   
25                   26   0001-5180   
26                   27   0001-5199   
27                   28   0001-5342   
28                   29   0001-5547   
29                   30   0001-5652   
...                 ...         ...   
9624               9625   8750-7587   
9625               9626   8755-1039   
9626               9627   8755-1187   
9627               9628   8755-1209   
9628               9629   8755-1225   
9629               9630   8755-2930   
9630               9631   8755-3996   
9631               9632   8755-4615   
9632               9633   8755-6863   
9633               9634   8755-7223   
9634               9635   8755-9668   
9635               9636   8756-0437   
9636               9637   8756-0879   
9637               9638   8756-2324   
9638               9639   8756-3282   
9639               9640   8756-3894   
9640               9641   8756-5641   
9641               9642   8756-6222   
9642               9643   8756-6583   
9643               9644   8756-6621   
9644               9645   8756-663X   
9645               9646   8756-7016   
9646               9647   8756-7547   
9647               9648   8756-7555   
9648               9649   8756-758X   
9649               9650   8756-7938   
9650               9651   8756-8225   
9651               9652   8756-9264   
9652               9653   8756-971X   
9653               9654   8756-9728   

                                   Title 1 (Electronic)  \
0                                The Publishers weekly.   
1                       Ulrich's periodicals directory.   
2     Bulletin of the American Museum of Natural His...   
3     AAUP bulletin : quarterly publication of the A...   
4     Communications of the Association for Computin...   
5                                          AIAA journal   
6                                         AIChE journal   
7                                         AORN journal.   
8                             Transactions of the ASAE.   
9                                     Aslib proceedings   
10                                     Tissue antigens.   
11                              AV communication review   
12                        Seminars in nuclear medicine.   
13                                              Abacus.   
14                            Abstracts in anthropology   
15                                           Chirurgie.   
16                       Academy of Management journal.   
17    Mathematical notes of the Academy of Sciences ...   
18                                           Oceanology   
19                    Accident analysis and prevention.   
20                    Accounting and business research.   
21                                The accounting review   
22                        Accounts of chemical research   
23    The Journal of the Acoustical Society of America.   
24                  Acta anaesthesiologica Scandinavica   
25                                      Acta anatomic

In [73]:
melted_ids = pd.concat([pd.DataFrame(v, index=np.repeat(k,len(v))) for k,v in portico['Linking ISSN list'].to_dict().items()])
melted_ids = melted_ids.rename(columns={0:'Linking ISSN split'})
melted_ids = melted_ids[melted_ids['Linking ISSN split'] != '']
melted_ids

Linking ISSN split
0             0000-0019
1             0000-2100
2             0003-0090
3             0001-026X
4             0001-0782
5             0001-1452
6             0001-1541
7             0001-2092
8             0001-2351
9            0001-253X 
9             2050-3806
10           0001-2815 
10            2059-2302
11           0001-2890 
11           0148-5806 
11            1042-1629
12            0001-2998
13            0001-3072
14            0001-3455
15            0001-4001
16            0001-4273
17            0001-4346
18            0001-4370
19            0001-4575
20            0001-4788
21            0001-4826
22            0001-4842
23            0001-4966
24            0001-5172
25            0001-5180
...                 ...
9630          1558-1888
9631          1873-2011
9632          1099-0496
9633          8755-7223
9634          1878-075X
9635          1098-2388
9636          1530-8014
9637         0005-8580 
9637         0748-612X 
9637         1089-7089 
9637          8756-2324
9638          1873-2763
9639          1559-7075
9640          1532-6942
9641          1465-7341
9642          1476-7937
9643          1520-6424
9644          1520-6432
9645          8756-7016
9646          1940-5286
9647          1930-8299
9648          1460-2695
9649          1520-6033
9650          1540-4730
9651         0736-6108 
9651         0892-1059 
9651         1045-3873 
9651          8756-9264
9652          8756-971X
9653          1938-9507

[10809 rows x 1 columns]

In [74]:
portico_gran = pd.DataFrame()
portico_gran = pd.merge(portico,melted_ids,how="left",left_index=True,right_index=True)
portico_gran

Library Input Row ISSN Number  \
0                     1   0000-0019   
1                     2   0000-2100   
2                     3   0001-0196   
3                     4   0001-026X   
4                     5   0001-0782   
5                     6   0001-1452   
6                     7   0001-1541   
7                     8   0001-2092   
8                     9   0001-2351   
9                    10   0001-253X   
9                    10   0001-253X   
10                   11   0001-2815   
10                   11   0001-2815   
11                   12   0001-2890   
11                   12   0001-2890   
11                   12   0001-2890   
12                   13   0001-2998   
13                   14   0001-3072   
14                   15   0001-3455   
15                   16   0001-4001   
16                   17   0001-4273   
17                   18   0001-4346   
18                   19   0001-4370   
19                   20   0001-4575   
20                   21   0001-4788   
21                   22   0001-4826   
22                   23   0001-4842   
23                   24   0001-4966   
24                   25   0001-5172   
25                   26   0001-5180   
...                 ...         ...   
9630               9631   8755-3996   
9631               9632   8755-4615   
9632               9633   8755-6863   
9633               9634   8755-7223   
9634               9635   8755-9668   
9635               9636   8756-0437   
9636               9637   8756-0879   
9637               9638   8756-2324   
9637               9638   8756-2324   
9637               9638   8756-2324   
9637               9638   8756-2324   
9638               9639   8756-3282   
9639               9640   8756-3894   
9640               9641   8756-5641   
9641               9642   8756-6222   
9642               9643   8756-6583   
9643               9644   8756-6621   
9644               9645   8756-663X   
9645               9646   8756-7016   
9646               9647   8756-7547   
9647               9648   8756-7555   
9648               9649   8756-758X   
9649               9650   8756-7938   
9650               9651   8756-8225   
9651               9652   8756-9264   
9651               9652   8756-9264   
9651               9652   8756-9264   
9651               9652   8756-9264   
9652               9653   8756-971X   
9653               9654   8756-9728   

                                   Title 1 (Electronic)  \
0                                The Publishers weekly.   
1                       Ulrich's periodicals directory.   
2     Bulletin of the American Museum of Natural His...   
3     AAUP bulletin : quarterly publication of the A...   
4     Communications of the Association for Computin...   
5                                          AIAA journal   
6                                         AIChE journal   
7                                         AORN journal.   
8                             Transactions of the ASAE.   
9                                     Aslib proceedings   
9                                     Aslib proceedings   
10                                     Tissue antigens.   
10                                     Tissue antigens.   
11                              AV communication review   
11                              AV communication review   
11                              AV communication review   
12                        Seminars in nuclear medicine.   
13                                              Abacus.   
14                            Abstracts in anthropology   
15                                           Chirurgie.   
16                       Academy of Management journal.   
17    Mathematical notes of the Academy of Sciences ...   
18                                           Oceanology   
19                    Accident analysis and prevention.   
20                    Accounting and business research.   
21                                The accounting revi

In [75]:
portico_cols = list(portico_gran.columns)
portico_cols

['Library Input Row',
 'ISSN Number',
 'Title 1 (Electronic)',
 'Publisher 1 (Electronic)',
 'Linking ISSN',
 'Portico Match',
 'Preservation Service',
 'Portico Title',
 'Portico ISSN',
 'PCA',
 'Status',
 'Earliest Year Preserved',
 'Earliest Volume Preserved',
 'Latest Year Preserved',
 'Latest Volume Preserved',
 'Num Preserved Articles',
 'Num Preserved Issues',
 'Num Preserved Volumes',
 'URL to Journal in Audit Interface',
 'Portico Content Provider',
 'Portico Title ID',
 'Notes',
 'Linking ISSN list',
 'Linking ISSN split']

In [76]:
portico_cols_edit = []
for x in portico_cols:
    portico_cols_edit.append(str(x) + '_PORTICO')
portico_cols_edit

['Library Input Row_PORTICO',
 'ISSN Number_PORTICO',
 'Title 1 (Electronic)_PORTICO',
 'Publisher 1 (Electronic)_PORTICO',
 'Linking ISSN_PORTICO',
 'Portico Match_PORTICO',
 'Preservation Service_PORTICO',
 'Portico Title_PORTICO',
 'Portico ISSN_PORTICO',
 'PCA_PORTICO',
 'Status_PORTICO',
 'Earliest Year Preserved_PORTICO',
 'Earliest Volume Preserved_PORTICO',
 'Latest Year Preserved_PORTICO',
 'Latest Volume Preserved_PORTICO',
 'Num Preserved Articles_PORTICO',
 'Num Preserved Issues_PORTICO',
 'Num Preserved Volumes_PORTICO',
 'URL to Journal in Audit Interface_PORTICO',
 'Portico Content Provider_PORTICO',
 'Portico Title ID_PORTICO',
 'Notes_PORTICO',
 'Linking ISSN list_PORTICO',
 'Linking ISSN split_PORTICO']

In [77]:
portico_dict = dict(zip(portico_cols, portico_cols_edit))
portico_dict

{'Earliest Volume Preserved': 'Earliest Volume Preserved_PORTICO',
 'Earliest Year Preserved': 'Earliest Year Preserved_PORTICO',
 'ISSN Number': 'ISSN Number_PORTICO',
 'Latest Volume Preserved': 'Latest Volume Preserved_PORTICO',
 'Latest Year Preserved': 'Latest Year Preserved_PORTICO',
 'Library Input Row': 'Library Input Row_PORTICO',
 'Linking ISSN': 'Linking ISSN_PORTICO',
 'Linking ISSN list': 'Linking ISSN list_PORTICO',
 'Linking ISSN split': 'Linking ISSN split_PORTICO',
 'Notes': 'Notes_PORTICO',
 'Num Preserved Articles': 'Num Preserved Articles_PORTICO',
 'Num Preserved Issues': 'Num Preserved Issues_PORTICO',
 'Num Preserved Volumes': 'Num Preserved Volumes_PORTICO',
 'PCA': 'PCA_PORTICO',
 'Portico Content Provider': 'Portico Content Provider_PORTICO',
 'Portico ISSN': 'Portico ISSN_PORTICO',
 'Portico Match': 'Portico Match_PORTICO',
 'Portico Title': 'Portico Title_PORTICO',
 'Portico Title ID': 'Portico Title ID_PORTICO',
 'Preservation Service': 'Preservation Servic

In [78]:
portico_gran.rename(index=str, columns = portico_dict, inplace=True)
portico_gran

Library Input Row_PORTICO ISSN Number_PORTICO  \
0                             1           0000-0019   
1                             2           0000-2100   
2                             3           0001-0196   
3                             4           0001-026X   
4                             5           0001-0782   
5                             6           0001-1452   
6                             7           0001-1541   
7                             8           0001-2092   
8                             9           0001-2351   
9                            10           0001-253X   
9                            10           0001-253X   
10                           11           0001-2815   
10                           11           0001-2815   
11                           12           0001-2890   
11                           12           0001-2890   
11                           12           0001-2890   
12                           13           0001-2998   
13                           14           0001-3072   
14                           15           0001-3455   
15                           16           0001-4001   
16                           17           0001-4273   
17                           18           0001-4346   
18                           19           0001-4370   
19                           20           0001-4575   
20                           21           0001-4788   
21                           22           0001-4826   
22                           23           0001-4842   
23                           24           0001-4966   
24                           25           0001-5172   
25                           26           0001-5180   
...                         ...                 ...   
9630                       9631           8755-3996   
9631                       9632           8755-4615   
9632                       9633           8755-6863   
9633                       9634           8755-7223   
9634                       9635           8755-9668   
9635                       9636           8756-0437   
9636                       9637           8756-0879   
9637                       9638           8756-2324   
9637                       9638           8756-2324   
9637                       9638           8756-2324   
9637                       9638           8756-2324   
9638                       9639           8756-3282   
9639                       9640           8756-3894   
9640                       9641           8756-5641   
9641                       9642           8756-6222   
9642                       9643           8756-6583   
9643                       9644           8756-6621   
9644                       9645           8756-663X   
9645                       9646           8756-7016   
9646                       9647           8756-7547   
9647                       9648           8756-7555   
9648                       9649           8756-758X   
9649                       9650           8756-7938   
9650                       9651           8756-8225   
9651                       9652           8756-9264   
9651                       9652           8756-9264   
9651                       9652           8756-9264   
9651                       9652           8756-9264   
9652                       9653           8756-971X   
9653                       9654           8756-9728   

                           Title 1 (Electronic)_PORTICO  \
0                                The Publishers weekly.   
1                       Ulrich's periodicals directory.   
2     Bulletin of the American Museum of Natural His...   
3     AAUP bulletin : quarterly publication of the A...   
4     Communications of the Association for Computin...   
5                                          AIAA journal   
6                                         AIChE journal   
7                                         AORN journal.   
8                             Transactions of the ASAE.   
9    

In [93]:
df_pcad_btaa_portico = pd.merge(df_pcad_btaa,portico_gran,how='left',left_on='ISSN_to_match',right_on='Linking ISSN split_PORTICO')
df_pcad_btaa_portico

record_index     ISSN_bib  \
0                  0  [0000-0787]   
1                  1  [2150-4008]   
2                  2  [0000-0469]   
3                  3  [0000-0019]   
4                  4           []   
5                  5           []   
6                  6           []   
7                  7  [0741-7233]   
8                  8           []   
9                  9           []   
10                 9           []   
11                10           []   
12                11           []   
13                12           []   
14                13           []   
15                14  [2411-1406]   
16                15  [2055-5520]   
17                15  [2055-5520]   
18                15  [2055-5520]   
19                16           []   
20                17           []   
21                17           []   
22                17           []   
23                18           []   
24                19           []   
25                20           []   
26                21           []   
27                22           []   
28                23           []   
29                24  [0713-3936]   
...              ...          ...   
211673        173263           []   
211674        173264           []   
211675        173264           []   
211676        173265           []   
211677        173266           []   
211678        173267           []   
211679        173268           []   
211680        173269           []   
211681        173270           []   
211682        173271           []   
211683        173272           []   
211684        173273  [0131-6095]   
211685        173274           []   
211686        173275           []   
211687        173276           []   
211688        173277           []   
211689        173278  [0893-7184]   
211690        173279           []   
211691        173280  [0737-4194]   
211692        173281           []   
211693        173282  [2470-7597]   
211694        173283           []   
211695        173284  [2470-7708]   
211696        173285           []   
211697        173286           []   
211698        173287           []   
211699        173288  [0098-6143]   
211700        173289  [0007-7011]   
211701        173290           []   
211702        173291  [0078-0170]   

                                        ISSN_cluster            MMS_ID  \
0                  [0000-0787, 0000-0469, 0000-0019]  9937257820001701   
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
2                  [0000-0787, 0000-0469, 0000-0019]  9913446020001701   
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
4                                                 []  9940052290001701   
5                                                 []  9915732180001701   
6                                                 []  9967355600001701   
7                                        [0741-7233]  9959067250001701   
8                                                 []  9915654130001701   
9                                        [2080-8097]  9966896580001701   
10                                       [2080-8097]  9966896580001701   
11                                                []  9915303430001701   
12                                                []  9944643300001701   
13                                                []  9914906750001701   
14                                                []  9960994670001701   
15                            [2411-1406, 2072-6414]  9974071460801701   
16                                       [2055-5520]  9974080735401701   
17                                       [2055-5520]  9974080735401701   
18                                       [2055-5520]  9974080735401701   
19                                                []  9914678130001701   
20                                       [2059-5131]  9974744300301701   
21                                       [2059-5131]  9974744300301701   
22         

In [81]:
df_pcad_btaa_portico[df_pcad_btaa_portico['Linking ISSN split_PORTICO'].notnull()]

ISSN_bib                                       ISSN_cluster  \
3       [0000-0019]       [0000-0469, 2150-4008, 0094-257X, 0000-0019]   
29      [0713-3936]                                        [0713-3936]   
85      [0148-9267]                             [1531-5169, 0148-9267]   
86      [0148-9267]                             [1531-5169, 0148-9267]   
165     [0133-3720]                                        [0133-3720]   
297     [0303-4569]                                        [0303-4569]   
321     [0009-4633]                                        [0009-4633]   
343     [0091-0260]                                        [0091-0260]   
416     [1063-0279]                                        [1063-0279]   
508     [0737-8831]                                        [0737-8831]   
539     [0007-7712]                                        [0007-7712]   
540     [0007-7712]                                        [0007-7712]   
541     [0007-7712]                                        [0007-7712]   
587     [0954-7762]                  [0269-7289, 0029-6589, 0954-7762]   
616     [0263-6484]                             [1099-0844, 0263-6484]   
656     [0340-1022]  [0340-1022, 0340-7022, 2364-8961, 0071-7894, 1...   
716     [0091-7370]                             [0095-8905, 0091-7370]   
797     [0268-005X]                                        [0268-005X]   
839     [2321-0230]                             [2321-7472, 2321-0230]   
840     [2321-0230]                             [2321-7472, 2321-0230]   
985     [0030-0071]                                        [0030-0071]   
1278    [0013-5984]                                        [0013-5984]   
1564    [0264-1615]                             [0140-2773, 0264-1615]   
1594    [0003-4436]                             [1281-7082, 0003-4436]   
1657    [0262-8104]                             [1756-3488, 0262-8104]   
1661    [0094-7776]                                        [0094-7776]   
1788    [0161-8628]                             [0145-2541, 0161-8628]   
1790    [0161-8628]                             [0145-2541, 0161-8628]   
1839    [1356-336X]                  [1356-336X, 0140-7708, 1741-2749]   
1971    [0141-0423]                             [0141-0423, 1467-9817]   
...             ...                                                ...   
211180  [0737-0016]                             [1532-7655, 0737-0016]   
211190  [0044-2992]                                        [0044-2992]   
211263  [0737-1209]                                        [0737-1209]   
211288  [0942-9352]       [0323-4479, 0044-3336, 0942-9352, 0724-410X]   
211314  [0730-8566]                  [0730-8566, 1939-6228, 0743-9016]   
211315  [0362-1340]       [1558-1160, 1523-2867, 0362-1340, 2332-1865]   
211316  [0362-1340]       [1558-1160, 1523-2867, 0362-1340, 2332-1865]   
211317  [0362-1340]       [1558-1160, 1523-2867, 0362-1340, 2332-1865]   
211318  [0743-9016]                             [0730-8566, 0743-9016]   
211319  [1939-6228]                  [0730-8566, 1939-6228, 2161-2919]   
211322  [0743-9016]                             [0730-8566, 0743-9016]   
211324  [1939-6228]                  [0730-8566, 1939-6228, 1523-2867]   
211339  [1044-8314]                  [1044-8314, 0892-9904, 1082-6742]   
211340  [1082-6742]                             [1044-8314, 1082-6742]   
211367  [0040-5809]                                        [0040-5809]   
211373  [0091-5521]                                        [0091-5521]   
211400  [0884-0040]       [0737-1292, 1551-6970, 1536-0709, 0884-0040]   
211401  [0884-0040]       [0737-1292, 1551-6970, 1536-0709, 0884-0040]   
211402  [1551-6970]                  [0884-0040, 1551-6970, 1554-6306]   
211413  [1069-3971]                             [0094-3673, 1069-3971]   
211498  [0891-5245]                                        [0891-5245]   
211528  [0277-593X]                                        [0277-593X]   
211529  [0277-5

In [94]:
df_pcad_btaa_portico.to_pickle('df_pcad_repos.pkl')
df_pcad_btaa_portico.to_csv('df_pcad_repos.txt', sep='\t')

In [95]:
df_pcad_btaa_portico.columns

Index(['record_index', 'ISSN_bib', 'ISSN_cluster', 'MMS_ID', 'OCN',
       'OCN_cluster', 'Title_bib', 'chron', 'descr', 'e_holdings', 'enum',
       'p_or_e', 'ISSN_group_id', 'OCN_group_id', 'both_groups',
       'matches_group_id', 'MMS ID', 'Item PID', 'Barcode', 'Enum_item',
       'Chron_item', 'Descr_item', 'Permanent Library', 'Permanent Location',
       'Electronic Collection Id', 'Public Name', 'MMS Id', 'Title_portfolio',
       'Begin Publication Date', 'End Publication Date', 'ISSN_portfolio',
       'Coverage Information Combined', 'Coverage Statement', 'Portfolio Id',
       'Lifecycle', 'Embargo Operator', 'Embargo Months', 'Embargo Years',
       'Status (Active)', 'PCAD?', 'ISSN_to_match', 'ISSN Number_BTAA-SPR',
       'Title 1 (Print)_BTAA-SPR', 'Publisher (Print)_BTAA-SPR',
       'Title 2 (Print)_BTAA-SPR', 'Publisher (Print).1_BTAA-SPR',
       'Title 3 (Print)_BTAA-SPR', 'Publisher (Print).2_BTAA-SPR',
       '(more bib records?)_BTAA-SPR', 'Match?_BTAA-SPR',
 

In [96]:
find_only_p_or_e = df_pcad_btaa_portico[['record_index','matches_group_id','p_or_e','MMS_ID','Title_bib']]
find_only_p_or_e

record_index  matches_group_id p_or_e            MMS_ID  \
0                  0                 0      p  9937257820001701   
1                  1                 0      e  9967008940001701   
2                  2                 0      p  9913446020001701   
3                  3                 0      p  9934112930001701   
4                  4                 1      p  9940052290001701   
5                  5                 2      p  9915732180001701   
6                  6                 3      e  9967355600001701   
7                  7                 4      p  9959067250001701   
8                  8                 5      p  9915654130001701   
9                  9                 6      e  9966896580001701   
10                 9                 6      e  9966896580001701   
11                10                 7      p  9915303430001701   
12                11                 8      p  9944643300001701   
13                12                 9      p  9914906750001701   
14                13                10      p  9960994670001701   
15                14                11      e  9974071460801701   
16                15                12      e  9974080735401701   
17                15                12      e  9974080735401701   
18                15                12      e  9974080735401701   
19                16                13      p  9914678130001701   
20                17                14      e  9974744300301701   
21                17                14      e  9974744300301701   
22                17                14      e  9974744300301701   
23                18                15      p  9914603730001701   
24                19                15      p  9948999710001701   
25                20                16      p  9957169080001701   
26                21                17      p  9951631900001701   
27                22                18      p  9960998770001701   
28                23                19      p  9916590420001701   
29                24                20      p  9953497050001701   
...              ...               ...    ...               ...   
211673        173263            109830      p  9944644430001701   
211674        173264            109831      e  9968486320001701   
211675        173264            109831      e  9968486320001701   
211676        173265            109832      p  9925696030001701   
211677        173266            109833      p  9929890960001701   
211678        173267            109834      p  9925281110001701   
211679        173268            109835      p  9935443960001701   
211680        173269            109836      p  9929747170001701   
211681        173270            109837      p  9931084540001701   
211682        173271            109838      p  9924654070001701   
211683        173272            109839      e  9966823740001701   
211684        173273            109840      p  9921474770001701   
211685        173274            109840      e  9973979206001701   
211686        173275            109841      p  9953147090001701   
211687        173276            109842      p  9924592130001701   
211688        173277            109843      p  9943461660001701   
211689        173278            109844      e  9967766920001701   
211690        173279            109845      p  9924363170001701   
211691        173280            109846      p  9917126270001701   
211692        173281            109847      e  9974757221901701   
211693        173282            109847      e  9975423099501701   
211694        173283            109848      p  9927800620001701   
211695        173284            109849      e  9975423098901701   
211696        173285            109849      e  9974757221001701   
211697        173286            109850      p  9927781200001701   
211698        173287            109851      e  9967343540001701   
211699        173288            109852      p  9951438410001701   
211700        173289            109853      p  99351177

In [98]:
find_only_p_or_e = find_only_p_or_e.groupby(['matches_group_id']).agg(lambda x: list(set(x))).reset_index()
find_only_p_or_e

matches_group_id                                       record_index  \
0                      0                                       [0, 1, 2, 3]   
1                      1                                                [4]   
2                      2                                                [5]   
3                      3                                                [6]   
4                      4                                                [7]   
5                      5                                                [8]   
6                      6                                                [9]   
7                      7                                               [10]   
8                      8                                               [11]   
9                      9                                               [12]   
10                    10                                               [13]   
11                    11                                               [14]   
12                    12                                               [15]   
13                    13                                               [16]   
14                    14                                               [17]   
15                    15                                           [18, 19]   
16                    16                                               [20]   
17                    17                                               [21]   
18                    18                                               [22]   
19                    19                                               [23]   
20                    20                                           [24, 25]   
21                    21                                               [26]   
22                    22                                               [27]   
23                    23                                               [28]   
24                    24                                               [29]   
25                    25                                               [30]   
26                    26                                           [32, 31]   
27                    27                                               [33]   
28                    28                                               [34]   
29                    29                                               [35]   
...                  ...                                                ...   
109825            109825                                           [173243]   
109826            109826  [173248, 173249, 173250, 173251, 173252, 17325...   
109827            109827                                           [173257]   
109828            109828                   [173258, 173259, 173260, 173261]   
109829            109829                                           [173262]   
109830            109830                                           [173263]   
109831            109831                                           [173264]   
109832            109832                                           [173265]   
109833            109833                                           [173266]   
109834            109834                                           [173267]   
109835            109835                                           [173268]   
109836            109836                                           [173269]   
109837            109837                                           [173270]   
109838            109838                                           [173271]   
109839            109839                                           [173272]   
109840            109840                                   [173273, 173274]   
109841            109841                                           [173275]   
109842            109842                                           [173276]   
109843            109843                                  

In [99]:
find_only_p_or_e['pore'] = find_only_p_or_e['p_or_e'].apply(lambda x: ' '.join(x))
find_only_p_or_e

matches_group_id                                       record_index  \
0                      0                                       [0, 1, 2, 3]   
1                      1                                                [4]   
2                      2                                                [5]   
3                      3                                                [6]   
4                      4                                                [7]   
5                      5                                                [8]   
6                      6                                                [9]   
7                      7                                               [10]   
8                      8                                               [11]   
9                      9                                               [12]   
10                    10                                               [13]   
11                    11                                               [14]   
12                    12                                               [15]   
13                    13                                               [16]   
14                    14                                               [17]   
15                    15                                           [18, 19]   
16                    16                                               [20]   
17                    17                                               [21]   
18                    18                                               [22]   
19                    19                                               [23]   
20                    20                                           [24, 25]   
21                    21                                               [26]   
22                    22                                               [27]   
23                    23                                               [28]   
24                    24                                               [29]   
25                    25                                               [30]   
26                    26                                           [32, 31]   
27                    27                                               [33]   
28                    28                                               [34]   
29                    29                                               [35]   
...                  ...                                                ...   
109825            109825                                           [173243]   
109826            109826  [173248, 173249, 173250, 173251, 173252, 17325...   
109827            109827                                           [173257]   
109828            109828                   [173258, 173259, 173260, 173261]   
109829            109829                                           [173262]   
109830            109830                                           [173263]   
109831            109831                                           [173264]   
109832            109832                                           [173265]   
109833            109833                                           [173266]   
109834            109834                                           [173267]   
109835            109835                                           [173268]   
109836            109836                                           [173269]   
109837            109837                                           [173270]   
109838            109838                                           [173271]   
109839            109839                                           [173272]   
109840            109840                                   [173273, 173274]   
109841            109841                                           [173275]   
109842            109842                                           [173276]   
109843            109843                                  

In [100]:
find_only_p_or_e['pore'].value_counts()

p      68621
e      33344
p e     7890
Name: pore, dtype: int64

In [101]:
only_p = find_only_p_or_e[find_only_p_or_e['pore'] == 'p']
only_p

matches_group_id      record_index p_or_e  \
1                      1               [4]    [p]   
2                      2               [5]    [p]   
4                      4               [7]    [p]   
5                      5               [8]    [p]   
7                      7              [10]    [p]   
8                      8              [11]    [p]   
9                      9              [12]    [p]   
10                    10              [13]    [p]   
13                    13              [16]    [p]   
15                    15          [18, 19]    [p]   
16                    16              [20]    [p]   
17                    17              [21]    [p]   
18                    18              [22]    [p]   
19                    19              [23]    [p]   
21                    21              [26]    [p]   
22                    22              [27]    [p]   
23                    23              [28]    [p]   
24                    24              [29]    [p]   
25                    25              [30]    [p]   
27                    27              [33]    [p]   
28                    28              [34]    [p]   
29                    29              [35]    [p]   
30                    30              [36]    [p]   
31                    31              [37]    [p]   
32                    32          [38, 39]    [p]   
33                    33              [40]    [p]   
34                    34              [41]    [p]   
35                    35              [42]    [p]   
36                    36              [43]    [p]   
37                    37              [44]    [p]   
...                  ...               ...    ...   
109809            109809          [173226]    [p]   
109813            109813          [173230]    [p]   
109815            109815          [173232]    [p]   
109816            109816          [173233]    [p]   
109817            109817          [173234]    [p]   
109818            109818          [173235]    [p]   
109819            109819          [173236]    [p]   
109820            109820          [173237]    [p]   
109821            109821          [173238]    [p]   
109823            109823          [173240]    [p]   
109827            109827          [173257]    [p]   
109829            109829          [173262]    [p]   
109830            109830          [173263]    [p]   
109832            109832          [173265]    [p]   
109833            109833          [173266]    [p]   
109834            109834          [173267]    [p]   
109835            109835          [173268]    [p]   
109836            109836          [173269]    [p]   
109837            109837          [173270]    [p]   
109838            109838          [173271]    [p]   
109841            109841          [173275]    [p]   
109842            109842          [173276]    [p]   
109843            109843          [173277]    [p]   
109845            109845          [173279]    [p]   
109846            109846          [173280]    [p]   
109848            109848          [173283]    [p]   
109850            109850          [173286]    [p]   
109852            109852          [173288]    [p]   
109853            109853          [173289]    [p]   
109854            109854  [173290, 173291]    [p]   

                                      MMS_ID  \
1                         [9940052290001701]   
2                         [9915732180001701]   
4                         [9959067250001701]   
5                         [9915654130001701]   
7                         [9915303430001701]   
8                         [9944643300001701]   
9                         [9914906750001701]   
10                        [9960994670001701]   
13                        [9914678130001701]   
15      [9914603730001701, 9948999710001701]   
16                        [9957169080001701]   
17                        [9951631900001701]   
18                        [9960998770001701]   
19                        [9916590420001701]   
2

In [103]:
only_p_groups = list(only_p['matches_group_id'])
only_p_groups

[1,
 2,
 4,
 5,
 7,
 8,
 9,
 10,
 13,
 15,
 16,
 17,
 18,
 19,
 21,
 22,
 23,
 24,
 25,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 57,
 60,
 61,
 62,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 73,
 74,
 75,
 76,
 77,
 79,
 80,
 81,
 82,
 84,
 85,
 86,
 87,
 88,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 103,
 105,
 106,
 107,
 108,
 109,
 111,
 112,
 113,
 115,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 128,
 129,
 130,
 132,
 133,
 134,
 135,
 136,
 137,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 174,
 175,
 176,
 177,
 178,
 179,
 181,
 182,
 183,
 184,
 185,
 186,
 187,
 189,
 190,
 191,
 192,
 193,
 194,
 196,
 197,
 198,
 199,
 202,
 204,
 205,
 208,
 209,
 211,
 213,
 214,
 216,
 217,
 219,
 220,
 221,

In [104]:
only_e = find_only_p_or_e[find_only_p_or_e['pore'] == 'e']
only_e

matches_group_id                      record_index p_or_e  \
3                      3                               [6]    [e]   
6                      6                               [9]    [e]   
11                    11                              [14]    [e]   
12                    12                              [15]    [e]   
14                    14                              [17]    [e]   
26                    26                          [32, 31]    [e]   
47                    47                              [56]    [e]   
58                    58                              [67]    [e]   
59                    59                              [68]    [e]   
72                    72                              [82]    [e]   
78                    78                              [92]    [e]   
83                    83                              [97]    [e]   
89                    89                             [105]    [e]   
102                  102                             [120]    [e]   
104                  104                             [122]    [e]   
110                  110                             [129]    [e]   
114                  114                             [133]    [e]   
116                  116                        [136, 137]    [e]   
131                  131                        [160, 161]    [e]   
138                  138                             [169]    [e]   
149                  149                             [180]    [e]   
157                  157                             [189]    [e]   
158                  158                             [190]    [e]   
173                  173                             [211]    [e]   
180                  180                             [218]    [e]   
188                  188                             [226]    [e]   
195                  195                             [233]    [e]   
200                  200                             [238]    [e]   
201                  201                             [239]    [e]   
203                  203                             [241]    [e]   
...                  ...                               ...    ...   
109744            109744                          [173146]    [e]   
109746            109746                          [173148]    [e]   
109747            109747                          [173149]    [e]   
109749            109749                          [173151]    [e]   
109752            109752                          [173154]    [e]   
109756            109756                          [173158]    [e]   
109758            109758                          [173160]    [e]   
109761            109761                          [173163]    [e]   
109763            109763                          [173165]    [e]   
109770            109770                          [173175]    [e]   
109784            109784                          [173191]    [e]   
109785            109785                          [173192]    [e]   
109795            109795                          [173203]    [e]   
109799            109799                          [173208]    [e]   
109804            109804                          [173220]    [e]   
109808            109808                          [173225]    [e]   
109810            109810                          [173227]    [e]   
109811            109811                          [173228]    [e]   
109812            109812                          [173229]    [e]   
109814            109814                          [173231]    [e]   
109822            109822                          [173239]    [e]   
109824            109824                  [173241, 173242]    [e]   
109825            109825                          [173243]    [e]   
109828            109828  [173258, 173259, 173260, 173261]    [e]   
109831            109831                          [173264]    [e]   
109839            109839                          [173272]    [e]   
109844

In [106]:
only_e_groups = list(only_e['matches_group_id'])
only_e_groups

[3,
 6,
 11,
 12,
 14,
 26,
 47,
 58,
 59,
 72,
 78,
 83,
 89,
 102,
 104,
 110,
 114,
 116,
 131,
 138,
 149,
 157,
 158,
 173,
 180,
 188,
 195,
 200,
 201,
 203,
 206,
 207,
 210,
 212,
 215,
 218,
 234,
 235,
 239,
 247,
 253,
 262,
 267,
 271,
 272,
 274,
 277,
 284,
 288,
 296,
 302,
 310,
 315,
 317,
 319,
 325,
 328,
 329,
 331,
 332,
 334,
 336,
 338,
 342,
 343,
 344,
 352,
 364,
 373,
 375,
 391,
 395,
 409,
 418,
 441,
 445,
 448,
 451,
 456,
 458,
 466,
 469,
 470,
 475,
 476,
 477,
 486,
 488,
 505,
 508,
 510,
 515,
 517,
 524,
 526,
 533,
 534,
 537,
 541,
 542,
 544,
 553,
 555,
 557,
 563,
 566,
 569,
 572,
 574,
 576,
 578,
 581,
 583,
 585,
 587,
 589,
 591,
 593,
 595,
 598,
 599,
 600,
 602,
 605,
 608,
 615,
 616,
 617,
 619,
 623,
 625,
 627,
 628,
 629,
 632,
 634,
 636,
 638,
 640,
 642,
 644,
 646,
 647,
 649,
 651,
 655,
 658,
 659,
 661,
 663,
 664,
 666,
 670,
 672,
 675,
 707,
 720,
 768,
 843,
 852,
 869,
 871,
 936,
 1009,
 1022,
 1026,
 1030,
 1031,
 1

In [107]:
p_and_e = find_only_p_or_e[find_only_p_or_e['pore'] == 'p e']
p_and_e

matches_group_id                                       record_index  \
0                      0                                       [0, 1, 2, 3]   
20                    20                                           [24, 25]   
63                    63                                           [72, 73]   
127                  127                                    [152, 153, 151]   
232                  232                                         [273, 274]   
243                  243                                    [291, 292, 293]   
260                  260                          [313, 314, 315, 316, 317]   
313                  313                          [377, 378, 379, 380, 381]   
378                  378                                         [456, 457]   
400                  400                                         [488, 487]   
436                  436           [528, 529, 530, 531, 532, 533, 534, 535]   
454                  454                                         [553, 554]   
472                  472                                    [584, 585, 586]   
521                  521                                    [640, 641, 639]   
565                  565                          [704, 705, 706, 707, 703]   
575                  575                                         [717, 718]   
603                  603                                         [758, 759]   
662                  662                                         [838, 839]   
709                  709                                    [897, 898, 899]   
861                  861         [1184, 1178, 1179, 1180, 1181, 1182, 1183]   
898                  898                                 [1226, 1227, 1228]   
1093                1093                     [1456, 1457, 1458, 1459, 1460]   
1109                1109                     [1484, 1485, 1486, 1487, 1488]   
1151                1151                                       [1544, 1545]   
1152                1152                           [1546, 1547, 1548, 1549]   
1200                1200                                       [1603, 1604]   
1226                1226                                 [1632, 1633, 1631]   
1248                1248                     [1657, 1658, 1659, 1660, 1661]   
1280                1280                                 [1701, 1702, 1703]   
1287                1287                                       [1712, 1711]   
...                  ...                                                ...   
109305            109305  [172547, 172548, 172549, 172550, 172551, 17255...   
109330            109330   [172601, 172602, 172603, 172604, 172605, 172606]   
109333            109333                                   [172609, 172610]   
109345            109345   [172622, 172623, 172624, 172625, 172626, 172627]   
109360            109360                                   [172644, 172645]   
109368            109368                           [172656, 172654, 172655]   
109393            109393                           [172689, 172690, 172691]   
109403            109403                                   [172702, 172703]   
109445            109445                   [172752, 172753, 172750, 172751]   
109480            109480                                   [172803, 172804]   
109506            109506                                   [172833, 172834]   
109513            109513                                   [172841, 172842]   
109516            109516                                   [172845, 172846]   
109526            109526                           [172856, 172857, 172858]   
109574            109574                                   [172912, 172911]   
109591            109591                           [172931, 172932, 172933]   
109611            109611  [172960, 172961, 172962, 172963, 172964, 17295...   
109621            109621  [172976, 172977, 172978, 172979, 172980, 17298...   
109637            109637                                  

In [109]:
pe_groups = list(p_and_e['matches_group_id'])
pe_groups

[0,
 20,
 63,
 127,
 232,
 243,
 260,
 313,
 378,
 400,
 436,
 454,
 472,
 521,
 565,
 575,
 603,
 662,
 709,
 861,
 898,
 1093,
 1109,
 1151,
 1152,
 1200,
 1226,
 1248,
 1280,
 1287,
 1301,
 1374,
 1428,
 1431,
 1442,
 1459,
 1494,
 1528,
 1551,
 1562,
 1625,
 1627,
 1652,
 1705,
 1731,
 1734,
 1762,
 1784,
 1786,
 1807,
 1825,
 2037,
 2055,
 2073,
 2093,
 2100,
 2102,
 2109,
 2118,
 2121,
 2128,
 2143,
 2174,
 2188,
 2207,
 2209,
 2251,
 2265,
 2297,
 2302,
 2340,
 2346,
 2354,
 2380,
 2490,
 2492,
 2538,
 2546,
 2547,
 2556,
 2582,
 2599,
 2611,
 2624,
 2626,
 2631,
 2634,
 2636,
 2641,
 2642,
 2650,
 2652,
 2656,
 2665,
 2675,
 2678,
 2721,
 2727,
 2732,
 2767,
 2769,
 2775,
 2784,
 2801,
 2808,
 2844,
 2879,
 2885,
 2895,
 2922,
 2975,
 3037,
 3149,
 3189,
 3447,
 3544,
 3596,
 3695,
 3719,
 3865,
 3996,
 4022,
 4068,
 4134,
 4161,
 4253,
 4301,
 4319,
 4358,
 4377,
 4399,
 4463,
 4570,
 4722,
 4976,
 5014,
 5016,
 5202,
 5209,
 5214,
 5252,
 5360,
 5407,
 5422,
 5424,
 5530,
 55

In [112]:
p_only_data = df_pcad_btaa_portico[df_pcad_btaa_portico['matches_group_id'].isin(only_p_groups)]
p_only_data

record_index     ISSN_bib ISSN_cluster            MMS_ID          OCN  \
4                  4           []           []  9940052290001701    [5513931]   
5                  5           []           []  9915732180001701   [56968858]   
7                  7  [0741-7233]  [0741-7233]  9959067250001701    [9374421]   
8                  8           []           []  9915654130001701   [36865188]   
11                10           []           []  9915303430001701   [28031616]   
12                11           []           []  9944643300001701    [9375722]   
13                12           []           []  9914906750001701  [233933474]   
14                13           []           []  9960994670001701    [9375807]   
19                16           []           []  9914678130001701   [50361294]   
23                18           []           []  9914603730001701   [32525735]   
24                19           []           []  9948999710001701   [34916326]   
25                20           []           []  9957169080001701    [9376134]   
26                21           []           []  9951631900001701    [9376481]   
27                22           []           []  9960998770001701    [9378065]   
28                23           []           []  9916590420001701   [39990101]   
31                26           []           []  9917618120001701   [25986218]   
32                27  [0557-3912]  [0557-3912]  9943936920001701   [64163673]   
33                28           []           []  9917508900001701   [26386028]   
34                29           []           []  9917519240001701   [64218270]   
35                30           []           []  9917394900001701   [24263405]   
38                33           []           []  9917079380001701  [191255423]   
39                34           []           []  9917076360001701   [15862595]   
40                35           []           []  9916707190001701   [64229266]   
41                36  [0738-0348]  [0738-0348]  9960996990001701    [9381379]   
42                37           []           []  9918127920001701   [70676914]   
43                38           []           []  9917905780001701    [1553840]   
44                39           []  [0009-0891]  9933054090001701   [10691263]   
45                40  [0882-0457]  [0882-0457]  9959131440001701    [9384247]   
46                41  [0132-0637]  [0132-0637]  9941445080001701    [2149476]   
47                42           []           []  9920623000001701   [14903284]   
...              ...          ...          ...               ...          ...   
211633        173230           []           []  9921293660001701   [51821054]   
211635        173232           []           []  9924030700001701    [9586982]   
211636        173233           []           []  9958736530001701    [9364918]   
211637        173234           []           []  9925207030001701    [1759126]   
211638        173235           []           []  9944019910001701   [18649690]   
211639        173236           []           []  9924385920001701  [148989502]   
211640        173237           []           []  9924551950001701   [17964020]   
211641        173238           []           []  9960795500001701   [56521382]   
211643        173240           []           []  9924552750001701   [64239180]   
211667        173257  [0012-2440]  [0012-2440]  9933249370001701     [936752]   
211672        173262           []           []  9924608680001701   [64239125]   
211673        173263           []  [0164-0968]  9944644430001701    [9367672]   
211676        173265           []           []  9925696030001701    [1779619]   
211677        173266           []           []  9929890960001701   [11924484]   
211678        173267           []           []  9925281110001701  [466646049]   
211679        173268           []           []  9935443960001701    [1542198]   
211680        173269           []           []  9929747170001701    [9370267]   
211681        173270           []      

In [113]:
p_only_data.to_pickle('p_only.pkl')
p_only_data.to_csv('p_only.txt',sep='\t',index=False)

In [115]:
e_only_data = df_pcad_btaa_portico[df_pcad_btaa_portico['matches_group_id'].isin(only_e_groups)]
e_only_data

record_index     ISSN_bib                       ISSN_cluster  \
6                  6           []                                 []   
9                  9           []                        [2080-8097]   
10                 9           []                        [2080-8097]   
15                14  [2411-1406]             [2411-1406, 2072-6414]   
16                15  [2055-5520]                        [2055-5520]   
17                15  [2055-5520]                        [2055-5520]   
18                15  [2055-5520]                        [2055-5520]   
20                17           []                        [2059-5131]   
21                17           []                        [2059-5131]   
22                17           []                        [2059-5131]   
36                31  [2470-802X]             [2470-8011, 2470-802X]   
37                32           []                                 []   
61                56           []                                 []   
72                67  [2405-8521]                        [2405-8521]   
73                68  [2352-7110]                        [2352-7110]   
74                68  [2352-7110]                        [2352-7110]   
95                82  [2470-959X]             [2470-9581, 2470-959X]   
105               92  [0745-7219]                        [0745-7219]   
110               97  [0737-5379]                        [0737-5379]   
118              105           []                                 []   
133              120  [2451-8654]                        [2451-8654]   
135              122           []                                 []   
142              129  [0737-4410]             [0146-8847, 0737-4410]   
146              133  [2471-0970]             [2471-0962, 2471-0970]   
149              136  [2471-1144]             [2471-1144, 2471-1136]   
150              137           []                                 []   
173              160           []                                 []   
174              161  [2471-1756]             [2471-1748, 2471-1756]   
182              169           []                                 []   
183              169           []                                 []   
...              ...          ...                                ...   
211590        173192           []                        [2470-5470]   
211601        173203  [2405-4690]                        [2405-4690]   
211607        173208           []                                 []   
211608        173208           []                                 []   
211620        173220  [2057-1518]             [2057-150X, 2057-1518]   
211621        173220  [2057-1518]             [2057-150X, 2057-1518]   
211622        173220  [2057-1518]             [2057-150X, 2057-1518]   
211627        173225  [0131-1441]                        [0131-1441]   
211628        173225  [0131-1441]                        [0131-1441]   
211630        173227  [2470-6566]                        [2470-6566]   
211631        173228           []                                 []   
211632        173229           []                                 []   
211634        173231  [2470-6663]             [2470-6663, 2470-6655]   
211642        173239  [2470-6981]                        [2470-6981]   
211644        173241           []                                 []   
211645        173242  [2470-7155]             [2470-7155, 2470-7139]   
211646        173243           []                                 []   
211668        173258  [2470-508X]             [2470-4911, 2470-508X]   
211669        173259           []                                 []   
211670        173260  [2470-5098]  [2470-508X, 2470-5098, 2470-4903]   
211671        173261           []                                 []   
211674        173264           []                                 []   
211675        173264           []                                 []   
211683        173272           []               

In [116]:
e_only_data.to_pickle('e_only.pkl')
e_only_data.to_csv('e_only.txt',sep='\t',index=False)

In [118]:
p_and_e_data = df_pcad_btaa_portico[df_pcad_btaa_portico['matches_group_id'].isin(pe_groups)]
p_and_e_data

record_index     ISSN_bib  \
0                  0  [0000-0787]   
1                  1  [2150-4008]   
2                  2  [0000-0469]   
3                  3  [0000-0019]   
29                24  [0713-3936]   
30                25  [1929-7084]   
78                72  [1531-5169]   
79                72  [1531-5169]   
80                72  [1531-5169]   
81                72  [1531-5169]   
82                72  [1531-5169]   
83                72  [1531-5169]   
84                72  [1531-5169]   
85                73  [0148-9267]   
86                73  [0148-9267]   
164              151           []   
165              152  [0133-3720]   
166              153           []   
297              273  [0303-4569]   
298              274  [1439-0272]   
299              274  [1439-0272]   
300              274  [1439-0272]   
301              274  [1439-0272]   
302              274  [1439-0272]   
320              291           []   
321              292  [0009-4633]   
322              293  [1558-0407]   
342              313  [0031-5710]   
343              314  [0091-0260]   
344              315  [0033-3638]   
...              ...          ...   
211577        173183  [1573-7233]   
211578        173183  [1573-7233]   
211579        173183  [1573-7233]   
211602        173204  [0723-0869]   
211603        173205  [1878-0792]   
211604        173205  [1878-0792]   
211625        173223  [1537-1719]   
211626        173224  [0737-4038]   
211647        173244  [0029-4810]   
211648        173245  [1096-0961]   
211649        173245  [1096-0961]   
211650        173246  [0006-5242]   
211651        173247  [1432-0584]   
211652        173247  [1432-0584]   
211653        173247  [1432-0584]   
211654        173248           []   
211655        173249  [0939-5555]   
211656        173250  [1430-2772]   
211657        173250  [1430-2772]   
211658        173250  [1430-2772]   
211659        173250  [1430-2772]   
211660        173251  [1279-8509]   
211661        173251  [1279-8509]   
211662        173252  [1079-9796]   
211663        173253           []   
211664        173254  [0340-4684]   
211665        173255  [1269-3286]   
211666        173256  [0033-3026]   
211684        173273  [0131-6095]   
211685        173274           []   

                                        ISSN_cluster            MMS_ID  \
0                  [0000-0787, 0000-0469, 0000-0019]  9937257820001701   
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
2                  [0000-0787, 0000-0469, 0000-0019]  9913446020001701   
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
29                                       [0713-3936]  9953497050001701   
30                            [0713-3936, 1929-7084]  9975244382301701   
78                            [1531-5169, 0148-9267]  9968959840001701   
79                            [1531-5169, 0148-9267]  9968959840001701   
80                            [1531-5169, 0148-9267]  9968959840001701   
81                            [1531-5169, 0148-9267]  9968959840001701   
82                            [1531-5169, 0148-9267]  9968959840001701   
83                            [1531-5169, 0148-9267]  9968959840001701   
84                            [1531-5169, 0148-9267]  9968959840001701   
85                            [1531-5169, 0148-9267]  9946998200001701   
86                            [1531-5169, 0148-9267]  9946998200001701   
164                                               []  9974762623801701   
165                                      [0133-3720]  9957941200001701   
166                                      [0133-3720]  9926650440001701   
297                                      [0303-4569]  9931505200001701   
298                           [1439-0272, 0303-4569]  9967779320001701   
299                           [1439-0272, 0303-4569]  9967779320001701   
300                           [1439-0272, 0303-4569]  9967779320001701   
301        

In [119]:
p_and_e_data.to_pickle('p_and_e.pkl')
p_and_e_data.to_csv('p_and_e.txt',sep='\t',index=False)

In [121]:
df_pcad_btaa_portico.columns

Index(['record_index', 'ISSN_bib', 'ISSN_cluster', 'MMS_ID', 'OCN',
       'OCN_cluster', 'Title_bib', 'chron', 'descr', 'e_holdings', 'enum',
       'p_or_e', 'ISSN_group_id', 'OCN_group_id', 'both_groups',
       'matches_group_id', 'MMS ID', 'Item PID', 'Barcode', 'Enum_item',
       'Chron_item', 'Descr_item', 'Permanent Library', 'Permanent Location',
       'Electronic Collection Id', 'Public Name', 'MMS Id', 'Title_portfolio',
       'Begin Publication Date', 'End Publication Date', 'ISSN_portfolio',
       'Coverage Information Combined', 'Coverage Statement', 'Portfolio Id',
       'Lifecycle', 'Embargo Operator', 'Embargo Months', 'Embargo Years',
       'Status (Active)', 'PCAD?', 'ISSN_to_match', 'ISSN Number_BTAA-SPR',
       'Title 1 (Print)_BTAA-SPR', 'Publisher (Print)_BTAA-SPR',
       'Title 2 (Print)_BTAA-SPR', 'Publisher (Print).1_BTAA-SPR',
       'Title 3 (Print)_BTAA-SPR', 'Publisher (Print).2_BTAA-SPR',
       '(more bib records?)_BTAA-SPR', 'Match?_BTAA-SPR',
 

In [123]:
df_pcad_btaa_portico['PCAD?'].value_counts()

Yes      70523
Maybe    14211
Name: PCAD?, dtype: int64

In [132]:
pcad_test = p_and_e_data[p_and_e_data['PCAD?'].isin(['Yes','Maybe'])]
pcad_test

record_index     ISSN_bib  \
1                  1  [2150-4008]   
30                25  [1929-7084]   
78                72  [1531-5169]   
79                72  [1531-5169]   
80                72  [1531-5169]   
81                72  [1531-5169]   
82                72  [1531-5169]   
83                72  [1531-5169]   
84                72  [1531-5169]   
164              151           []   
298              274  [1439-0272]   
299              274  [1439-0272]   
300              274  [1439-0272]   
301              274  [1439-0272]   
302              274  [1439-0272]   
322              293  [1558-0407]   
342              313  [0031-5710]   
346              317  [1945-7421]   
347              317  [1945-7421]   
348              317  [1945-7421]   
349              317  [1945-7421]   
350              317  [1945-7421]   
415              377  [2059-464X]   
417              379  [1758-6038]   
418              379  [1758-6038]   
419              380  [1466-4119]   
420              380  [1466-4119]   
421              381  [2054-5584]   
422              381  [2054-5584]   
506              456  [2054-166X]   
...              ...          ...   
211409        173029  [1552-3578]   
211410        173029  [1552-3578]   
211411        173029  [1552-3578]   
211412        173029  [1552-3578]   
211499        173110  [1532-656X]   
211500        173110  [1532-656X]   
211501        173110  [1532-656X]   
211502        173110  [1532-656X]   
211503        173110  [1532-656X]   
211527        173133  [2470-3885]   
211528        173134  [0277-593X]   
211575        173181  [1532-2300]   
211577        173183  [1573-7233]   
211578        173183  [1573-7233]   
211579        173183  [1573-7233]   
211603        173205  [1878-0792]   
211604        173205  [1878-0792]   
211625        173223  [1537-1719]   
211648        173245  [1096-0961]   
211649        173245  [1096-0961]   
211651        173247  [1432-0584]   
211652        173247  [1432-0584]   
211653        173247  [1432-0584]   
211656        173250  [1430-2772]   
211657        173250  [1430-2772]   
211658        173250  [1430-2772]   
211659        173250  [1430-2772]   
211660        173251  [1279-8509]   
211661        173251  [1279-8509]   
211685        173274           []   

                                        ISSN_cluster            MMS_ID  \
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
30                            [0713-3936, 1929-7084]  9975244382301701   
78                            [1531-5169, 0148-9267]  9968959840001701   
79                            [1531-5169, 0148-9267]  9968959840001701   
80                            [1531-5169, 0148-9267]  9968959840001701   
81                            [1531-5169, 0148-9267]  9968959840001701   
82                            [1531-5169, 0148-9267]  9968959840001701   
83                            [1531-5169, 0148-9267]  9968959840001701   
84                            [1531-5169, 0148-9267]  9968959840001701   
164                                               []  9974762623801701   
298                           [1439-0272, 0303-4569]  9967779320001701   
299                           [1439-0272, 0303-4569]  9967779320001701   
300                           [1439-0272, 0303-4569]  9967779320001701   
301                           [1439-0272, 0303-4569]  9967779320001701   
302                           [1439-0272, 0303-4569]  9967779320001701   
322                           [0009-4633, 1558-0407]  9967176950001701   
342                           [0033-3638, 0031-5710]  9974832880401701   
346                [0091-0260, 1945-7421, 0885-6591]  9969175130001701   
347                [0091-0260, 1945-7421, 0885-6591]  9969175130001701   
348                [0091-0260, 1945-7421, 0885-6591]  9969175130001701   
349                [0091-0260, 1945-7421, 0885-6591]  9969175130001701   
350                [0091-0260, 1945-7421, 0885-6591]  9969175130001701   
415        

In [133]:
pe2_groups = list(pcad_test['matches_group_id'])
pe2_groups

[0,
 20,
 63,
 63,
 63,
 63,
 63,
 63,
 63,
 127,
 232,
 232,
 232,
 232,
 232,
 243,
 260,
 260,
 260,
 260,
 260,
 260,
 313,
 313,
 313,
 313,
 313,
 313,
 313,
 378,
 378,
 400,
 400,
 436,
 454,
 454,
 454,
 454,
 454,
 472,
 521,
 565,
 565,
 565,
 575,
 575,
 575,
 575,
 603,
 603,
 603,
 662,
 662,
 709,
 709,
 709,
 861,
 861,
 861,
 861,
 861,
 861,
 898,
 1093,
 1093,
 1109,
 1109,
 1109,
 1151,
 1152,
 1152,
 1200,
 1200,
 1200,
 1226,
 1226,
 1226,
 1226,
 1226,
 1248,
 1280,
 1280,
 1280,
 1280,
 1280,
 1280,
 1287,
 1301,
 1301,
 1301,
 1301,
 1374,
 1374,
 1374,
 1374,
 1374,
 1428,
 1431,
 1431,
 1442,
 1442,
 1459,
 1459,
 1459,
 1459,
 1459,
 1459,
 1494,
 1528,
 1551,
 1551,
 1562,
 1562,
 1562,
 1562,
 1562,
 1562,
 1562,
 1625,
 1625,
 1627,
 1627,
 1627,
 1652,
 1652,
 1652,
 1705,
 1705,
 1731,
 1731,
 1731,
 1731,
 1731,
 1731,
 1731,
 1731,
 1731,
 1731,
 1734,
 1734,
 1734,
 1734,
 1734,
 1762,
 1762,
 1762,
 1762,
 1762,
 1784,
 1784,
 1784,
 1784,
 1786,
 1

In [134]:
p_and_e_data_pcad = p_and_e_data[p_and_e_data['matches_group_id'].isin(pe2_groups)]
p_and_e_data_pcad

record_index     ISSN_bib  \
0                  0  [0000-0787]   
1                  1  [2150-4008]   
2                  2  [0000-0469]   
3                  3  [0000-0019]   
29                24  [0713-3936]   
30                25  [1929-7084]   
78                72  [1531-5169]   
79                72  [1531-5169]   
80                72  [1531-5169]   
81                72  [1531-5169]   
82                72  [1531-5169]   
83                72  [1531-5169]   
84                72  [1531-5169]   
85                73  [0148-9267]   
86                73  [0148-9267]   
164              151           []   
165              152  [0133-3720]   
166              153           []   
297              273  [0303-4569]   
298              274  [1439-0272]   
299              274  [1439-0272]   
300              274  [1439-0272]   
301              274  [1439-0272]   
302              274  [1439-0272]   
320              291           []   
321              292  [0009-4633]   
322              293  [1558-0407]   
342              313  [0031-5710]   
343              314  [0091-0260]   
344              315  [0033-3638]   
...              ...          ...   
211577        173183  [1573-7233]   
211578        173183  [1573-7233]   
211579        173183  [1573-7233]   
211602        173204  [0723-0869]   
211603        173205  [1878-0792]   
211604        173205  [1878-0792]   
211625        173223  [1537-1719]   
211626        173224  [0737-4038]   
211647        173244  [0029-4810]   
211648        173245  [1096-0961]   
211649        173245  [1096-0961]   
211650        173246  [0006-5242]   
211651        173247  [1432-0584]   
211652        173247  [1432-0584]   
211653        173247  [1432-0584]   
211654        173248           []   
211655        173249  [0939-5555]   
211656        173250  [1430-2772]   
211657        173250  [1430-2772]   
211658        173250  [1430-2772]   
211659        173250  [1430-2772]   
211660        173251  [1279-8509]   
211661        173251  [1279-8509]   
211662        173252  [1079-9796]   
211663        173253           []   
211664        173254  [0340-4684]   
211665        173255  [1269-3286]   
211666        173256  [0033-3026]   
211684        173273  [0131-6095]   
211685        173274           []   

                                        ISSN_cluster            MMS_ID  \
0                  [0000-0787, 0000-0469, 0000-0019]  9937257820001701   
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
2                  [0000-0787, 0000-0469, 0000-0019]  9913446020001701   
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
29                                       [0713-3936]  9953497050001701   
30                            [0713-3936, 1929-7084]  9975244382301701   
78                            [1531-5169, 0148-9267]  9968959840001701   
79                            [1531-5169, 0148-9267]  9968959840001701   
80                            [1531-5169, 0148-9267]  9968959840001701   
81                            [1531-5169, 0148-9267]  9968959840001701   
82                            [1531-5169, 0148-9267]  9968959840001701   
83                            [1531-5169, 0148-9267]  9968959840001701   
84                            [1531-5169, 0148-9267]  9968959840001701   
85                            [1531-5169, 0148-9267]  9946998200001701   
86                            [1531-5169, 0148-9267]  9946998200001701   
164                                               []  9974762623801701   
165                                      [0133-3720]  9957941200001701   
166                                      [0133-3720]  9926650440001701   
297                                      [0303-4569]  9931505200001701   
298                           [1439-0272, 0303-4569]  9967779320001701   
299                           [1439-0272, 0303-4569]  9967779320001701   
300                           [1439-0272, 0303-4569]  9967779320001701   
301        

In [125]:
pcad_groups = df_pcad_btaa_portico[df_pcad_btaa_portico['PCAD?'].isin(['Yes','Maybe'])]
pcad_groups

record_index     ISSN_bib  \
1                  1  [2150-4008]   
6                  6           []   
9                  9           []   
10                 9           []   
15                14  [2411-1406]   
16                15  [2055-5520]   
17                15  [2055-5520]   
18                15  [2055-5520]   
20                17           []   
21                17           []   
22                17           []   
30                25  [1929-7084]   
36                31  [2470-802X]   
37                32           []   
61                56           []   
72                67  [2405-8521]   
73                68  [2352-7110]   
74                68  [2352-7110]   
78                72  [1531-5169]   
79                72  [1531-5169]   
80                72  [1531-5169]   
81                72  [1531-5169]   
82                72  [1531-5169]   
83                72  [1531-5169]   
84                72  [1531-5169]   
95                82  [2470-959X]   
105               92  [0745-7219]   
110               97  [0737-5379]   
118              105           []   
133              120  [2451-8654]   
...              ...          ...   
211634        173231  [2470-6663]   
211642        173239  [2470-6981]   
211644        173241           []   
211645        173242  [2470-7155]   
211646        173243           []   
211648        173245  [1096-0961]   
211649        173245  [1096-0961]   
211651        173247  [1432-0584]   
211652        173247  [1432-0584]   
211653        173247  [1432-0584]   
211656        173250  [1430-2772]   
211657        173250  [1430-2772]   
211658        173250  [1430-2772]   
211659        173250  [1430-2772]   
211660        173251  [1279-8509]   
211661        173251  [1279-8509]   
211668        173258  [2470-508X]   
211669        173259           []   
211670        173260  [2470-5098]   
211671        173261           []   
211674        173264           []   
211675        173264           []   
211683        173272           []   
211685        173274           []   
211689        173278  [0893-7184]   
211692        173281           []   
211693        173282  [2470-7597]   
211695        173284  [2470-7708]   
211696        173285           []   
211698        173287           []   

                                        ISSN_cluster            MMS_ID  \
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
6                                                 []  9967355600001701   
9                                        [2080-8097]  9966896580001701   
10                                       [2080-8097]  9966896580001701   
15                            [2411-1406, 2072-6414]  9974071460801701   
16                                       [2055-5520]  9974080735401701   
17                                       [2055-5520]  9974080735401701   
18                                       [2055-5520]  9974080735401701   
20                                       [2059-5131]  9974744300301701   
21                                       [2059-5131]  9974744300301701   
22                                       [2059-5131]  9974744300301701   
30                            [0713-3936, 1929-7084]  9975244382301701   
36                            [2470-8011, 2470-802X]  9975423097101701   
37                                                []  9974757856101701   
61                                                []  9967063310001701   
72                                       [2405-8521]  9974001151001701   
73                                       [2352-7110]  9974001120701701   
74                                       [2352-7110]  9974001120701701   
78                            [1531-5169, 0148-9267]  9968959840001701   
79                            [1531-5169, 0148-9267]  9968959840001701   
80                            [1531-5169, 0148-9267]  9968959840001701   
81                            [1531-5169, 0148-9267]  9968959840001701   
82         

In [127]:
pcad_groups_PandE_holdings = list(set(pe_groups)&set(pcad_groups['matches_group_id']))
pcad_groups_PandE_holdings

[0,
 65538,
 65542,
 98315,
 65552,
 98321,
 65554,
 65555,
 20,
 32790,
 32792,
 32795,
 65564,
 65566,
 65567,
 32799,
 65571,
 65574,
 65575,
 65579,
 65580,
 65582,
 65584,
 32819,
 32821,
 32822,
 65593,
 98362,
 63,
 65603,
 98372,
 98376,
 32842,
 65610,
 98381,
 65615,
 65618,
 65620,
 98389,
 65622,
 32857,
 65625,
 65629,
 98397,
 65631,
 32864,
 65633,
 65640,
 65644,
 98412,
 32878,
 32879,
 32880,
 65646,
 32882,
 65650,
 65651,
 65653,
 98416,
 65656,
 65658,
 98428,
 98429,
 65662,
 32895,
 98431,
 127,
 65668,
 65674,
 98444,
 65677,
 65679,
 65680,
 32914,
 65682,
 65685,
 65687,
 32923,
 65692,
 65694,
 65698,
 65702,
 98478,
 32952,
 65721,
 98489,
 98491,
 98493,
 65736,
 32971,
 65739,
 65741,
 65742,
 65744,
 65745,
 65751,
 65755,
 98523,
 65763,
 65765,
 232,
 65773,
 65774,
 65776,
 243,
 65781,
 65784,
 65788,
 65791,
 33025,
 65794,
 65795,
 260,
 33034,
 33035,
 65804,
 98570,
 65806,
 65810,
 65813,
 65818,
 65826,
 98595,
 33061,
 98600,
 65833,
 98603,
 9

In [128]:
len(pcad_groups_PandE_holdings)

7889

In [129]:
pcad_groups2= df_pcad_btaa_portico[df_pcad_btaa_portico['matches_group_id'].isin(pcad_groups_PandE_holdings)]
pcad_groups2

record_index     ISSN_bib  \
0                  0  [0000-0787]   
1                  1  [2150-4008]   
2                  2  [0000-0469]   
3                  3  [0000-0019]   
29                24  [0713-3936]   
30                25  [1929-7084]   
78                72  [1531-5169]   
79                72  [1531-5169]   
80                72  [1531-5169]   
81                72  [1531-5169]   
82                72  [1531-5169]   
83                72  [1531-5169]   
84                72  [1531-5169]   
85                73  [0148-9267]   
86                73  [0148-9267]   
164              151           []   
165              152  [0133-3720]   
166              153           []   
297              273  [0303-4569]   
298              274  [1439-0272]   
299              274  [1439-0272]   
300              274  [1439-0272]   
301              274  [1439-0272]   
302              274  [1439-0272]   
320              291           []   
321              292  [0009-4633]   
322              293  [1558-0407]   
342              313  [0031-5710]   
343              314  [0091-0260]   
344              315  [0033-3638]   
...              ...          ...   
211577        173183  [1573-7233]   
211578        173183  [1573-7233]   
211579        173183  [1573-7233]   
211602        173204  [0723-0869]   
211603        173205  [1878-0792]   
211604        173205  [1878-0792]   
211625        173223  [1537-1719]   
211626        173224  [0737-4038]   
211647        173244  [0029-4810]   
211648        173245  [1096-0961]   
211649        173245  [1096-0961]   
211650        173246  [0006-5242]   
211651        173247  [1432-0584]   
211652        173247  [1432-0584]   
211653        173247  [1432-0584]   
211654        173248           []   
211655        173249  [0939-5555]   
211656        173250  [1430-2772]   
211657        173250  [1430-2772]   
211658        173250  [1430-2772]   
211659        173250  [1430-2772]   
211660        173251  [1279-8509]   
211661        173251  [1279-8509]   
211662        173252  [1079-9796]   
211663        173253           []   
211664        173254  [0340-4684]   
211665        173255  [1269-3286]   
211666        173256  [0033-3026]   
211684        173273  [0131-6095]   
211685        173274           []   

                                        ISSN_cluster            MMS_ID  \
0                  [0000-0787, 0000-0469, 0000-0019]  9937257820001701   
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
2                  [0000-0787, 0000-0469, 0000-0019]  9913446020001701   
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
29                                       [0713-3936]  9953497050001701   
30                            [0713-3936, 1929-7084]  9975244382301701   
78                            [1531-5169, 0148-9267]  9968959840001701   
79                            [1531-5169, 0148-9267]  9968959840001701   
80                            [1531-5169, 0148-9267]  9968959840001701   
81                            [1531-5169, 0148-9267]  9968959840001701   
82                            [1531-5169, 0148-9267]  9968959840001701   
83                            [1531-5169, 0148-9267]  9968959840001701   
84                            [1531-5169, 0148-9267]  9968959840001701   
85                            [1531-5169, 0148-9267]  9946998200001701   
86                            [1531-5169, 0148-9267]  9946998200001701   
164                                               []  9974762623801701   
165                                      [0133-3720]  9957941200001701   
166                                      [0133-3720]  9926650440001701   
297                                      [0303-4569]  9931505200001701   
298                           [1439-0272, 0303-4569]  9967779320001701   
299                           [1439-0272, 0303-4569]  9967779320001701   
300                           [1439-0272, 0303-4569]  9967779320001701   
301        

In [130]:
pcad_groups2.to_pickle('pcad_groups2.pkl')

In [136]:
df = pcad_groups2
df

record_index     ISSN_bib  \
0                  0  [0000-0787]   
1                  1  [2150-4008]   
2                  2  [0000-0469]   
3                  3  [0000-0019]   
29                24  [0713-3936]   
30                25  [1929-7084]   
78                72  [1531-5169]   
79                72  [1531-5169]   
80                72  [1531-5169]   
81                72  [1531-5169]   
82                72  [1531-5169]   
83                72  [1531-5169]   
84                72  [1531-5169]   
85                73  [0148-9267]   
86                73  [0148-9267]   
164              151           []   
165              152  [0133-3720]   
166              153           []   
297              273  [0303-4569]   
298              274  [1439-0272]   
299              274  [1439-0272]   
300              274  [1439-0272]   
301              274  [1439-0272]   
302              274  [1439-0272]   
320              291           []   
321              292  [0009-4633]   
322              293  [1558-0407]   
342              313  [0031-5710]   
343              314  [0091-0260]   
344              315  [0033-3638]   
...              ...          ...   
211577        173183  [1573-7233]   
211578        173183  [1573-7233]   
211579        173183  [1573-7233]   
211602        173204  [0723-0869]   
211603        173205  [1878-0792]   
211604        173205  [1878-0792]   
211625        173223  [1537-1719]   
211626        173224  [0737-4038]   
211647        173244  [0029-4810]   
211648        173245  [1096-0961]   
211649        173245  [1096-0961]   
211650        173246  [0006-5242]   
211651        173247  [1432-0584]   
211652        173247  [1432-0584]   
211653        173247  [1432-0584]   
211654        173248           []   
211655        173249  [0939-5555]   
211656        173250  [1430-2772]   
211657        173250  [1430-2772]   
211658        173250  [1430-2772]   
211659        173250  [1430-2772]   
211660        173251  [1279-8509]   
211661        173251  [1279-8509]   
211662        173252  [1079-9796]   
211663        173253           []   
211664        173254  [0340-4684]   
211665        173255  [1269-3286]   
211666        173256  [0033-3026]   
211684        173273  [0131-6095]   
211685        173274           []   

                                        ISSN_cluster            MMS_ID  \
0                  [0000-0787, 0000-0469, 0000-0019]  9937257820001701   
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
2                  [0000-0787, 0000-0469, 0000-0019]  9913446020001701   
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
29                                       [0713-3936]  9953497050001701   
30                            [0713-3936, 1929-7084]  9975244382301701   
78                            [1531-5169, 0148-9267]  9968959840001701   
79                            [1531-5169, 0148-9267]  9968959840001701   
80                            [1531-5169, 0148-9267]  9968959840001701   
81                            [1531-5169, 0148-9267]  9968959840001701   
82                            [1531-5169, 0148-9267]  9968959840001701   
83                            [1531-5169, 0148-9267]  9968959840001701   
84                            [1531-5169, 0148-9267]  9968959840001701   
85                            [1531-5169, 0148-9267]  9946998200001701   
86                            [1531-5169, 0148-9267]  9946998200001701   
164                                               []  9974762623801701   
165                                      [0133-3720]  9957941200001701   
166                                      [0133-3720]  9926650440001701   
297                                      [0303-4569]  9931505200001701   
298                           [1439-0272, 0303-4569]  9967779320001701   
299                           [1439-0272, 0303-4569]  9967779320001701   
300                           [1439-0272, 0303-4569]  9967779320001701   
301        

In [323]:
dates = df['chron']
dates.dropna(inplace=True)
dates

C:\Users\kjthomps\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\series.py:2993: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._update_inplace(result)


0                                                        []
2                                                        []
3         [1888, 1951, 1932, 1946, 1962, 1967, 1971, 200...
29        [2000, 1998-1999, 2001-2002, 2002, 1996-1997, ...
85        [2002, 1997, 2004, 2006, 2001, 1988, 1989, 200...
86        [2002, 1997, 2004, 2006, 2001, 1988, 1989, 200...
165       [2007, 1997, 2017, 2011, 2010, 2009, 2009, 198...
166                                                  [2008]
297       [1995, 1997, 2002, 2001, 1985, 2006, 2004, 198...
320                                               [1967-69]
321       [1975/1976-1976/1977, 1974/1975, 1980/1981, 19...
343       [1997, 2007, 2007, 2007, 2006, 2006, 2006, 198...
344       [1970, 1940, 1969, 1968, 1958-59, 1956-57, 195...
345                                   [1972-73, 1972, 1972]
416                  [1993-94, 1999-2000, 1997-98, 1995-96]
508       [1988, 1983/84, 2000, 1999, 1998, 1997, 1990, ...
539       [1953-1954, 1951-1953, 1979-19

In [324]:
len(dates)

40535

In [325]:
dates = dates[dates.apply(len) > 0]
dates

3         [1888, 1951, 1932, 1946, 1962, 1967, 1971, 200...
29        [2000, 1998-1999, 2001-2002, 2002, 1996-1997, ...
85        [2002, 1997, 2004, 2006, 2001, 1988, 1989, 200...
86        [2002, 1997, 2004, 2006, 2001, 1988, 1989, 200...
165       [2007, 1997, 2017, 2011, 2010, 2009, 2009, 198...
166                                                  [2008]
297       [1995, 1997, 2002, 2001, 1985, 2006, 2004, 198...
320                                               [1967-69]
321       [1975/1976-1976/1977, 1974/1975, 1980/1981, 19...
343       [1997, 2007, 2007, 2007, 2006, 2006, 2006, 198...
344       [1970, 1940, 1969, 1968, 1958-59, 1956-57, 195...
345                                   [1972-73, 1972, 1972]
416                  [1993-94, 1999-2000, 1997-98, 1995-96]
508       [1988, 1983/84, 2000, 1999, 1998, 1997, 1990, ...
539       [1953-1954, 1951-1953, 1979-1980, 1977-1978, 1...
582       [1980, 1980, 1983, 1982, 1984, 1983, 1984, 198...
583       [1984, 1976, 1965, 1969, 1968,

In [329]:
len(dates)

38295

In [331]:
fixed_dates = []

In [333]:
def date_fix (dlist):
    fixed_dates = []
    for date in dlist:
        #date = date.replace(' ','')
            
        date = str(date).strip()
        if date == '':
            print(date)
            print('Nothin?')
        #1973-89

        elif re.findall("^\d{4}-\d{2}$", date):
            #print(date + " range")
            year, partyear = re.split('-',date)
            century = year[:2]
            newyear = century + partyear
            rangeYear = int(newyear) + 1
            year_range = list(range(int(year), rangeYear))
            #print(year_range)
            fixed_dates.extend(year_range)
            #print(fixed_dates)

        elif re.findall("^\d{4}$", date):
            ##print(date + " four digits")
            fixed_dates.append(int(date))
            ##print(fixed_dates)

        elif re.findall("^\d{4}-\d{4}$",date):
            #print(date + " year-year")
            year1, year2 = re.split(r'[-]',date)
            #print(year1)
            #print(year2)
            year_range = list(range(int(year1),int(year2)+1))
            #print(year_range)
            fixed_dates.extend(year_range)
            #print(fixed_dates)

        elif re.findall("^\d{4}\/\d{4}$",date):
            #print(date + " year/year")
            year1, year2 = re.split(r'[/]',date)
            #print(year1)
            #print(year2)
            year_range = list(range(int(year1),int(year2)+1))
            #print(year_range)
            fixed_dates.extend(year_range)
            #print(fixed_dates)

        elif re.findall("^\d{4}\/\d{2}$",date):
            #print(date + " year/year")
            year, partyear = re.split(r'[/]',date)
            century = year[:2]
            newyear = century + partyear
            rangeYear = int(newyear) + 1
            year_range = list(range(int(year), rangeYear))
            #print(year_range)
            fixed_dates.extend(year_range)
            #print(fixed_dates)

        #1990/91-1991/92
        elif re.findall("^\d{4}\/\d{2}-\d{4}\/\d{2}$",date):
            #print(date)
            p = re.search("(?P<year1>^\d{4})(\/)(?P<yrpt2>\d{2})(-)(?P<year3>\d{4})(\/)(?P<yrpt4>\d{2}$)",date)
            #print(p)
            y1 = p.group('year1')
            c1 = y1[:2]
            y2 = c1 + p.group('yrpt2')
            range1 = list(range(int(y1),int(y2)+1))
            #print(range1)
            fixed_dates.extend(range1)

            y3 = p.group('year3')
            c2 = y3[:2]

            range3 = list(range(int(y2),int(y3)+1))
            #print(range3)
            fixed_dates.extend(range3)

            y4 = c2 + p.group('yrpt4')
            range2 = list(range(int(y3),int(y4)+1))
            #print(range2)
            fixed_dates.extend(range2)

            #print(fixed_dates)

        #2003/2004-2004/2005
        elif re.findall("^\d{4}\/\d{4}-\d{4}\/\d{4}$",date):
            #print(date + " year/year-year/year")
            date1, date2 = re.split('-',date)

            year1, year2 = re.split(r'[/]',date1)
            year_range1 = list(range(int(year1), int(year2)+1))
            #print(year_range1)
            fixed_dates.extend(year_range1)

            year3, year4 = re.split(r'[/]',date2)
            year_range2 = list(range(int(year2), int(year3)+1))
            #print(year_range2)
            fixed_dates.extend(year_range2)

            year_range3 = list(range(int(year3),int(year4)+1))
            #print(year_range3)
            fixed_dates.extend(year_range3)

            #print(fixed_dates)

        #2001-2001/2002
        elif re.findall("^\d{4}-\d{4}\/\d{4}$",date):
            #print(date + " year-year/year")
            date1, date2 = re.split('-',date)

            fixed_dates.append(int(date1))

            year1, year2 = re.split(r'[/]',date2)
            year_range = list(range(int(year1), int(year2)+1))
            #print(year_range)
            fixed_dates.extend(year_range)
            #print(fixed_dates)

        #1999/2000-2000
        elif re.findall("^\d{4}\/\d{4}-\d{4}$",date):
            #print(date + " year/year-year")
            date1, date2 = re.split('-',date)

            fixed_dates.append(int(date2))

            year1, year2 = re.split(r'[/]',date1)
            year_range = list(range(int(year1), int(year2)+1))
            #print(year_range)
            fixed_dates.extend(year_range)
            #print(fixed_dates)

        #1985-89/90
        elif re.findall("^\d{4}-\d{2}\/\d{2}$",date):
            #print(date + " year-yr/yr")
            y1,y2,y3 = re.split(r'[/-]',date)
            century = y1[:2]
            ny2 = century + y2
            ny3 = century + y3

            year_range1 = list(range(int(y1), int(ny2)+1))
            #print(year_range1)
            fixed_dates.extend(year_range1)

            year_range2 = list(range(int(ny2), int(ny3)+1))
            #print(year_range2)
            fixed_dates.extend(year_range2)

            #print(fixed_dates)        

        #1988/89-90
        elif re.findall("^\d{4}\/\d{2}-\d{2}$",date):
            #print(date + " year/yr-yr")
            year1, years = re.split(r'[/]',date)
            partyear1, partyear2 = re.split('-',years)
            century = year1[:2]
            newyear1 = century + partyear1
            newyear2 = century + partyear2

            rangeYear1 = int(newyear1) + 1
            year_range1 = list(range(int(year1), rangeYear1))
            #print(year_range1)
            fixed_dates.extend(year_range1)

            rangeYear2 = int(newyear2) + 1
            year_range2 = list(range(int(newyear1), rangeYear2))
            #print(year_range2)
            fixed_dates.extend(year_range2)

            #print(fixed_dates)    

        #2001/02-2004
        elif re.findall("^\d{4}\/\d{2}-\d{4}$",date):
            #print(date + " year/yr-year")
            years, year2 = re.split(r'[-]',date)
            year1, partyear =  re.split(r'[/]',years)
            century = year1[:2]
            newyear = century + partyear

            rangeYear1 = int(newyear) + 1
            year_range1 = list(range(int(year1), rangeYear1))
            #print(year_range1)
            fixed_dates.extend(year_range1)

            rangeYear2 = int(year2) + 1
            year_range2 = list(range(rangeYear1, rangeYear2))
            #print(year_range2)
            fixed_dates.extend(year_range2)
            #print(fixed_dates)            

        #1999/2000-2000/01
        elif re.findall("^\d{4}\/\d{4}-\d{4}\/\d{2}$",date):
            #print(date + " year/year-year/yr")
            ys1, ys2 = re.split(r'[-]',date)
            y1a, y1b  =  re.split(r'[/]',ys1)

            year_range1 = list(range(int(y1a), int(y1b)+1))
            #print(year_range1)
            fixed_dates.extend(year_range1)

            y2,py2 = re.split(r'[/]',ys2)
            ce2 = y2[:2]
            ny2 = ce2 + py2
            year_range2 = list(range(int(y2),int(ny2)+1))
            #print(year_range2)
            fixed_dates.extend(year_range2)
            #print(fixed_dates)  

        #1989-1990/91
        elif re.findall("^\d{4}-\d{4}\/\d{2}$",date):
            #print(date + " year-year/yr")
            y1, ys2 = re.split(r'[-]',date)
            y2a, y2b  =  re.split(r'[/]',ys2)

            year_range1 = list(range(int(y1), int(y2a)+1))
            #print(year_range1)
            fixed_dates.extend(year_range1)

            ce2 = y2a[:2]
            ny2 = ce2 + y2b
            year_range2 = list(range(int(y2a),int(ny2)+1))
            #print(year_range2)
            fixed_dates.extend(year_range2)
            #print(fixed_dates)  

        #1999,2001
        elif re.findall("^\d{4}\,\d{4}$",date):
            #print(date + " year,year")
            year1, year2 = re.split(r'[,]',date)
            year_range = [int(year1),int(year2)]
            #print(year_range)
            fixed_dates.extend(year_range)
            #print(fixed_dates)

        #200602006/2007
        elif re.findall("^\d{4}0\d{4}\/\d{4}$",date):
            p = re.search("(?P<year1>^\d{4})(?P<zero>0)(?P<range>\d{4}\/\d{4}$)",date)
            #print(p)
            y1 = p.group('year1')
            yset = p.group('range')
            year1,year2 = re.split(r'[/]',yset)
            yrange = list(range(int(y1),int(year1)+1))
            #print(yrange)
            fixed_dates.extend(yrange)
            yrange2 = list(range(int(year1),int(year2)+1))
            #print(yrange2)
            fixed_dates.extend(yrange2)

        #1960-68, 1978-2005
        elif re.findall("^\d{4}-\d{2},\s\d{4}-\d{4}$",date):
            #print(date)
            p = re.search("(?P<year1>^\d{4})(-)(?P<yrpt1>\d{2})(,\s)(?P<year3>\d{4})(-)(?P<year4>\d{4}$)",date)
            #p = re.search("(?P<year1>\d{4})(-)(?P<yrpt1>\d{2})(,\s)(?P<year3>\d{4})(-)",date)
            #print(p)
            y1 = p.group('year1')
            c1 = y1[:2]
            y2 = c1 + p.group('yrpt1')
            range1 = list(range(int(y1),int(y2)+1))
            #print(range1)
            fixed_dates.extend(range1)

            range2 = list(range(int(p.group('year3')),int(p.group('year4'))+1))
            #print(range2)
            fixed_dates.extend(range2)
            #print(fixed_dates)

        #1948-66,1970
        elif re.findall("^\d{4}-\d{2},\d{4}$",date):
            #print(date)
            p = re.search("(?P<year1>^\d{4})(-)(?P<yrpt1>\d{2})(,)(?P<year3>\d{4}$)",date)
            #print(p)
            y1 = p.group('year1')
            c1 = y1[:2]
            y2 = c1 + p.group('yrpt1')
            range1 = list(range(int(y1),int(y2)+1))
            #print(range1)
            fixed_dates.extend(range1)

            fixed_dates.append(int(p.group('year3')))
            #print(fixed_dates)

        #1988/89-89/90
        elif re.findall("^\d{4}\/\d{2}-\d{2}\/\d{2}$",date):
            #print(date)
            p = re.search("(?P<year1>^\d{4})(\/)(?P<yrpt2>\d{2})(-)(?P<yrpt3>\d{2})(\/)(?P<yrpt4>\d{2}$)",date)
            #print(p)
            y1 = p.group('year1')
            c1 = y1[:2]
            y2 = c1 + p.group('yrpt2')
            range1 = list(range(int(y1),int(y2)+1))
            #print(range1)
            fixed_dates.extend(range1)

            y3 = c1 + p.group('yrpt3')
            range2 = list(range(int(y2),int(y3)+1))
            #print(range2)
            fixed_dates.extend(range2)

            range3 = list(range(int(y3),int(c1 + p.group('yrpt4'))+1))
            #print(range3)
            fixed_dates.extend(range3)
            #print(fixed_dates)

        #1998/99-1999/2000
        elif re.findall("^\d{4}\/\d{2}-\d{4}\/\d{4}$",date):
            #print(date)
            p = re.search("(?P<year1>^\d{4})(\/)(?P<yrpt2>\d{2})(-)(?P<y3>\d{4})(\/)(?P<y4>\d{4}$)",date)
            #print(p)
            y1 = p.group('year1')
            c1 = y1[:2]
            y2 = c1 + p.group('yrpt2')
            range1 = list(range(int(y1),int(y2)+1))
            #print(range1)
            fixed_dates.extend(range1)

            y3 = p.group('y3')
            range2 = list(range(int(y2),int(y3)+1))
            #print(range2)
            fixed_dates.extend(range2)

            range3 = list(range(int(y3),int(p.group('y4'))+1))
            #print(range3)
            fixed_dates.extend(range3)
            #print(fixed_dates)

        #2015=2016
        elif re.findall("^\d{4}=\d{4}$",date):
            #print(date)
            p = re.search("(?P<year1>^\d{4})(\=)(?P<year2>\d{4}$)",date)
            #print(p)
            #print(type(p.group('year1')))
            #print(type(p.group('year2')))
            range1 = list(range(int(p.group('year1')),int(p.group('year2'))+1))
            #print(range1)
            fixed_dates.extend(range1)
            #print(fixed_dates)

        #200120/02-2003/2004
        elif re.findall("^\d{6}\/\d{2}-\d{4}\/\d{4}$",date):
            #print(date)
            yrs1,yrs2 = re.split(r'[-]',date)
            yrs1 = yrs1.replace("/","")
            year1 = yrs1[:4]
            year2 = yrs1[4:]
            #print(year1)
            #print(year2)

            year3,year4 = yrs2.split('/')
            #print(year3)
            #print(year4)

            range1 = list(range(int(year1),int(year2)+1))
            #print(range1)
            fixed_dates.extend(range1)

            range2 = list(range(int(year2),int(year3)+1))
            #print(range2)
            fixed_dates.extend(range2)

            range3 = list(range(int(year3),int(year4)+1))
            #print(range3)
            fixed_dates.extend(range3)

            #print(fixed_dates)

        #1-1
        elif re.findall("^\d{1}-\d{1}$",date):
            print(date)
            print(" probably not a date?")

        #1997/98- 1998
        elif re.findall("^\d{4}\/\d{2}-\s\d{4}$",date):
            #print(date)
            yrs,year3 = re.split(r'[-]',date)
            year3 = year3.strip()
            year1,year2 = re.split(r'[/]',yrs)
            c1 = year1[:2]
            year2 = c1 + year2

            #print(year1)
            #print(year2)
            #print(year3)

            range1 = list(range(int(year1),int(year2)+1))
            #print(range1)
            fixed_dates.extend(range1)

            range2 = list(range(int(year2),int(year3)+1))
            #print(range2)
            fixed_dates.extend(range2)

            #print(fixed_dates)

        #2001-10-12
        elif re.findall("^\d{4}-\d{2}-\d{2}$",date):
            #print(date + " year-mm-dd")
            year, mo, day = re.split('-',date)
            fixed_dates.append(int(year))

            #print(fixed_dates)

        #1976-19.78
        elif re.findall("^\d{4}-\d{2}\.\d{2}$",date):
            #print(date + " year-yy.yy")
            year1, year2 = re.split('-',date)
            #print(year1)
            year2 = year2.replace(".","")
            #print(year2)
            rangeyear = list(range(int(year1),int(year2)+1))
            fixed_dates.extend(rangeyear)

            #print(fixed_dates)

        else:
            print(date)
            print("UNKNOWN FORMAT")
            #fixed_dates.append(int(date))
            #print(fixed_dates)

    return list(sorted(set(fixed_dates)))

In [334]:
fixed_dates = dates.apply(date_fix)
fixed_dates

55
UNKNOWN FORMAT

Nothin?

Nothin?

Nothin?

Nothin?

Nothin?
1997 ANNUAL
UNKNOWN FORMAT
6
UNKNOWN FORMAT
1983/1984-11984/985
UNKNOWN FORMAT
1992.93
UNKNOWN FORMAT
2007- 2008
UNKNOWN FORMAT

Nothin?

Nothin?
1899-900
UNKNOWN FORMAT
1850-188
UNKNOWN FORMAT
60
UNKNOWN FORMAT
62
UNKNOWN FORMAT
61
UNKNOWN FORMAT
198901-06
UNKNOWN FORMAT
1992-958
UNKNOWN FORMAT

Nothin?
2006-070
UNKNOWN FORMAT
81
UNKNOWN FORMAT
80
UNKNOWN FORMAT
82
UNKNOWN FORMAT
1972197
UNKNOWN FORMAT
1974,1976-78
UNKNOWN FORMAT
19931994
UNKNOWN FORMAT
19668-69
UNKNOWN FORMAT
1999-200
UNKNOWN FORMAT
1999-200
UNKNOWN FORMAT
1999-200
UNKNOWN FORMAT
1999-200
UNKNOWN FORMAT
1999-200
UNKNOWN FORMAT
1976, 1979-80
UNKNOWN FORMAT
1994098
UNKNOWN FORMAT
198-1990
UNKNOWN FORMAT
195/1966
UNKNOWN FORMAT

Nothin?

Nothin?
1997/98 - 2000/01
UNKNOWN FORMAT
1879/1961-962/1970
UNKNOWN FORMAT

Nothin?
1942-143
UNKNOWN FORMAT
197201-06
UNKNOWN FORMAT
1983/984
UNKNOWN FORMAT
199907-10
UNKNOWN FORMAT
1961-68,1973-77
UNKNOWN FORMAT
1995199
UNK

3         [1873, 1874, 1876, 1880, 1881, 1882, 1883, 188...
29        [1991, 1992, 1993, 1994, 1995, 1996, 1997, 199...
85        [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...
86        [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...
165       [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...
166                                                  [2008]
297       [1974, 1975, 1976, 1977, 1978, 1979, 1980, 198...
320                                      [1967, 1968, 1969]
321       [1969, 1970, 1971, 1972, 1973, 1974, 1975, 197...
343       [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...
344       [1940, 1941, 1942, 1943, 1944, 1945, 1946, 194...
345                                            [1972, 1973]
416        [1993, 1994, 1995, 1996, 1997, 1998, 1999, 2000]
508       [1983, 1984, 1985, 1986, 1987, 1988, 1989, 199...
539       [1929, 1930, 1931, 1932, 1933, 1934, 1935, 193...
582       [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...
583       [1945, 1950, 1951, 1952, 1953,

In [335]:
type(fixed_dates)

pandas.core.series.Series

In [336]:
fixed_dates

3         [1873, 1874, 1876, 1880, 1881, 1882, 1883, 188...
29        [1991, 1992, 1993, 1994, 1995, 1996, 1997, 199...
85        [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...
86        [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...
165       [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...
166                                                  [2008]
297       [1974, 1975, 1976, 1977, 1978, 1979, 1980, 198...
320                                      [1967, 1968, 1969]
321       [1969, 1970, 1971, 1972, 1973, 1974, 1975, 197...
343       [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...
344       [1940, 1941, 1942, 1943, 1944, 1945, 1946, 194...
345                                            [1972, 1973]
416        [1993, 1994, 1995, 1996, 1997, 1998, 1999, 2000]
508       [1983, 1984, 1985, 1986, 1987, 1988, 1989, 199...
539       [1929, 1930, 1931, 1932, 1933, 1934, 1935, 193...
582       [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...
583       [1945, 1950, 1951, 1952, 1953,

In [347]:
def ranges(ints):
    #print(ints)
    ints = sorted(set(ints))
    if ints == []:
        print('empty list')
        yield ''
    else:
        range_start = previous_number = ints[0]
        for number in ints[1:]:
            #print(number)
            #print(type(number))
            #print(previous_number)
            #print(type(previous_number))
            if number == (previous_number + 1):
                previous_number = number
            else:
                yield range_start, previous_number
                range_start = previous_number = number
        yield range_start, previous_number

In [348]:
date_ranges = fixed_dates.apply(ranges).apply(list)
date_ranges

empty list
empty list
empty list


3         [(1873, 1874), (1876, 1876), (1880, 1910), (19...
29                                           [(1991, 2002)]
85                                           [(1977, 2017)]
86                                           [(1977, 2017)]
165                                          [(1973, 2017)]
166                                          [(2008, 2008)]
297                                          [(1974, 2007)]
320                                          [(1967, 1969)]
321                                          [(1969, 2015)]
343                                          [(1973, 2007)]
344                                          [(1940, 1972)]
345                                          [(1972, 1973)]
416                                          [(1993, 2000)]
508                            [(1983, 1990), (1992, 2006)]
539                            [(1929, 1999), (2003, 2013)]
582                                          [(1977, 1985)]
583                            [(1945, 1

In [350]:
dates_df = pd.DataFrame(fixed_dates)
dates_df

chron
3       [1873, 1874, 1876, 1880, 1881, 1882, 1883, 188...
29      [1991, 1992, 1993, 1994, 1995, 1996, 1997, 199...
85      [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...
86      [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...
165     [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...
166                                                [2008]
297     [1974, 1975, 1976, 1977, 1978, 1979, 1980, 198...
320                                    [1967, 1968, 1969]
321     [1969, 1970, 1971, 1972, 1973, 1974, 1975, 197...
343     [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...
344     [1940, 1941, 1942, 1943, 1944, 1945, 1946, 194...
345                                          [1972, 1973]
416      [1993, 1994, 1995, 1996, 1997, 1998, 1999, 2000]
508     [1983, 1984, 1985, 1986, 1987, 1988, 1989, 199...
539     [1929, 1930, 1931, 1932, 1933, 1934, 1935, 193...
582     [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...
583     [1945, 1950, 1951, 1952, 1953, 1954, 1955, 195...
584                  [2000, 2001, 2002, 2003, 2004, 2005]
585                                          [1992, 1993]
587     [1987, 1988, 1989, 1990, 1991, 1992, 1993, 199...
588                                    [1985, 1986, 1987]
589            [1995, 1996, 1997, 1998, 1999, 2000, 2001]
616     [1989, 1990, 1991, 1992, 1993, 1994, 1995, 199...
656     [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...
658     [1949, 1950, 1951, 1952, 1953, 1954, 1955, 195...
716     [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...
779                              [1856, 1857, 1858, 1859]
782     [1840, 1841, 1843, 1844, 1845, 1846, 1847, 184...
797     [1988, 1989, 1990, 1991, 1992, 1993, 1994, 199...
839                                    [2013, 2014, 2015]
...                                                   ...
211322                           [1973, 1975, 1976, 1977]
211324  [1994, 1995, 1996, 1997, 1998, 1999, 2000, 200...
211336                                             [1983]
211337                                 [1984, 1985, 1986]
211338                                 [1980, 1981, 1982]
211339                     [1989, 1990, 1991, 1992, 1993]
211340  [1995, 1996, 1997, 1998, 1999, 2000, 2001, 200...
211367  [1970, 1971, 1972, 1973, 1974, 1975, 1976, 197...
211373  [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...
211400  [1985, 1986, 1987, 1988, 1989, 1990, 1991, 199...
211401  [1985, 1986, 1987, 1988, 1989, 1990, 1991, 199...
211402                                 [2005, 2006, 2007]
211413  [1993, 1994, 1995, 1996, 1997, 1998, 1999, 200...
211414   [1966, 1967, 1968, 1969, 1970, 1971, 1972, 1973]
211498  [1987, 1988, 1989, 1990, 1991, 1992, 1993, 199...
211529                                       [1982, 1986]
211574  [1983, 1984, 1985, 1986, 1987, 1988, 1989, 199...
211576                                 [1982, 1983, 1984]
211602  [1983, 1984, 1985, 1986, 1987, 1988, 1989, 199...
211626  [1983, 1984, 1985, 1986, 1987, 1988, 1990, 199...
211647  [1961, 1962, 1963, 1964, 1965, 1966, 1967, 196...
211650  [1955, 1956, 1957, 1958, 1959, 1960, 1961, 196...
211654  [1978, 1979, 1980, 1981, 1982, 1983, 1984, 198...
211655  [1991, 1992, 1993, 1994, 1995, 1996, 1997, 199...
211662  [1995, 1996, 1997, 1998, 1999, 2000, 2001, 200...
211663                                       [1976, 1977]
211664  [1975, 1976, 1977, 1978, 1979, 1980, 1981, 198...
211665                     [1996, 1997, 1998, 1999, 2000]
211666  [1921, 1922, 1923, 1924, 1925, 1926, 1927, 192...
211684                                       [2002, 2003]

[38295 rows x 1 columns]

In [351]:
ranges_df = pd.DataFrame(date_ranges)
ranges_df

chron
3       [(1873, 1874), (1876, 1876), (1880, 1910), (19...
29                                         [(1991, 2002)]
85                                         [(1977, 2017)]
86                                         [(1977, 2017)]
165                                        [(1973, 2017)]
166                                        [(2008, 2008)]
297                                        [(1974, 2007)]
320                                        [(1967, 1969)]
321                                        [(1969, 2015)]
343                                        [(1973, 2007)]
344                                        [(1940, 1972)]
345                                        [(1972, 1973)]
416                                        [(1993, 2000)]
508                          [(1983, 1990), (1992, 2006)]
539                          [(1929, 1999), (2003, 2013)]
582                                        [(1977, 1985)]
583                          [(1945, 1945), (1950, 1985)]
584                                        [(2000, 2005)]
585                                        [(1992, 1993)]
587                                        [(1987, 2016)]
588                                        [(1985, 1987)]
589                                        [(1995, 2001)]
616                                        [(1989, 2006)]
656                                        [(1973, 2014)]
658                          [(1949, 1958), (1963, 1973)]
716                                        [(1973, 2018)]
779                                        [(1856, 1859)]
782                          [(1840, 1841), (1843, 1853)]
797                                        [(1988, 2003)]
839                                        [(2013, 2015)]
...                                                   ...
211322                       [(1973, 1973), (1975, 1977)]
211324                                     [(1994, 2015)]
211336                                     [(1983, 1983)]
211337                                     [(1984, 1986)]
211338                                     [(1980, 1982)]
211339                                     [(1989, 1993)]
211340                                     [(1995, 2012)]
211367                                     [(1970, 2007)]
211373                       [(1973, 1991), (1993, 2011)]
211400                       [(1985, 1995), (1999, 2004)]
211401                       [(1985, 1995), (1999, 2004)]
211402                                     [(2005, 2007)]
211413                                     [(1993, 2008)]
211414                                     [(1966, 1973)]
211498                                     [(1987, 2006)]
211529                       [(1982, 1982), (1986, 1986)]
211574                                     [(1983, 2008)]
211576                                     [(1982, 1984)]
211602         [(1983, 2003), (2005, 2005), (2007, 2007)]
211626                       [(1983, 1988), (1990, 2018)]
211647                                     [(1961, 1975)]
211650                                     [(1955, 1990)]
211654                                     [(1978, 1995)]
211655                                     [(1991, 2008)]
211662                                     [(1995, 2008)]
211663                                     [(1976, 1977)]
211664                                     [(1975, 1994)]
211665                                     [(1996, 2000)]
211666                                     [(1921, 1973)]
211684                                     [(2002, 2003)]

[38295 rows x 1 columns]

In [352]:
combo_ranges = pd.merge(dates_df,ranges_df,how='outer',right_index=True,left_index=True,suffixes=['_as_list','_ranges_calc'])
combo_ranges

chron_as_list  \
3       [1873, 1874, 1876, 1880, 1881, 1882, 1883, 188...   
29      [1991, 1992, 1993, 1994, 1995, 1996, 1997, 199...   
85      [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...   
86      [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...   
165     [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...   
166                                                [2008]   
297     [1974, 1975, 1976, 1977, 1978, 1979, 1980, 198...   
320                                    [1967, 1968, 1969]   
321     [1969, 1970, 1971, 1972, 1973, 1974, 1975, 197...   
343     [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...   
344     [1940, 1941, 1942, 1943, 1944, 1945, 1946, 194...   
345                                          [1972, 1973]   
416      [1993, 1994, 1995, 1996, 1997, 1998, 1999, 2000]   
508     [1983, 1984, 1985, 1986, 1987, 1988, 1989, 199...   
539     [1929, 1930, 1931, 1932, 1933, 1934, 1935, 193...   
582     [1977, 1978, 1979, 1980, 1981, 1982, 1983, 198...   
583     [1945, 1950, 1951, 1952, 1953, 1954, 1955, 195...   
584                  [2000, 2001, 2002, 2003, 2004, 2005]   
585                                          [1992, 1993]   
587     [1987, 1988, 1989, 1990, 1991, 1992, 1993, 199...   
588                                    [1985, 1986, 1987]   
589            [1995, 1996, 1997, 1998, 1999, 2000, 2001]   
616     [1989, 1990, 1991, 1992, 1993, 1994, 1995, 199...   
656     [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...   
658     [1949, 1950, 1951, 1952, 1953, 1954, 1955, 195...   
716     [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...   
779                              [1856, 1857, 1858, 1859]   
782     [1840, 1841, 1843, 1844, 1845, 1846, 1847, 184...   
797     [1988, 1989, 1990, 1991, 1992, 1993, 1994, 199...   
839                                    [2013, 2014, 2015]   
...                                                   ...   
211322                           [1973, 1975, 1976, 1977]   
211324  [1994, 1995, 1996, 1997, 1998, 1999, 2000, 200...   
211336                                             [1983]   
211337                                 [1984, 1985, 1986]   
211338                                 [1980, 1981, 1982]   
211339                     [1989, 1990, 1991, 1992, 1993]   
211340  [1995, 1996, 1997, 1998, 1999, 2000, 2001, 200...   
211367  [1970, 1971, 1972, 1973, 1974, 1975, 1976, 197...   
211373  [1973, 1974, 1975, 1976, 1977, 1978, 1979, 198...   
211400  [1985, 1986, 1987, 1988, 1989, 1990, 1991, 199...   
211401  [1985, 1986, 1987, 1988, 1989, 1990, 1991, 199...   
211402                                 [2005, 2006, 2007]   
211413  [1993, 1994, 1995, 1996, 1997, 1998, 1999, 200...   
211414   [1966, 1967, 1968, 1969, 1970, 1971, 1972, 1973]   
211498  [1987, 1988, 1989, 1990, 1991, 1992, 1993, 199...   
211529                                       [1982, 1986]   
211574  [1983, 1984, 1985, 1986, 1987, 1988, 1989, 199...   
211576                                 [1982, 1983, 1984]   
211602  [1983, 1984, 1985, 1986, 1987, 1988, 1989, 199...   
211626  [1983, 1984, 1985, 1986, 1987, 1988, 1990, 199...   
211647  [1961, 1962, 1963, 1964, 1965, 1966, 1967, 196...   
211650  [1955, 1956, 1957, 1958, 1959, 1960, 1961, 196...   
211654  [1978, 1979, 1980, 1981, 1982, 1983, 1984, 198...   
211655  [1991, 1992, 1993, 1994, 1995, 1996, 1997, 199...   
211662  [1995, 1996, 1997, 1998, 1999, 2000, 2001, 200...   
211663                                       [1976, 1977]   
211664  [1975, 1976, 1977, 1978, 1979, 1980, 1981, 198...   
211665                     [1996, 1997, 1998, 1999, 2000]   
211666  [1921, 1922, 1923, 1924, 1925, 1926, 1927, 192...   
211684                                       [2002, 2003]   

                                        chron_ranges_calc  
3       [(1873, 1874), (1876, 1876), (1880, 1910), (19...  
29                                         [(1991, 2002)]  
85                                         [(1977, 2017)]  
86                   

In [353]:
df_with_ranges = pd.merge(df,combo_ranges,how='left',right_index=True,left_index=True)
df_with_ranges

record_index     ISSN_bib  \
0                  0  [0000-0787]   
1                  1  [2150-4008]   
2                  2  [0000-0469]   
3                  3  [0000-0019]   
29                24  [0713-3936]   
30                25  [1929-7084]   
78                72  [1531-5169]   
79                72  [1531-5169]   
80                72  [1531-5169]   
81                72  [1531-5169]   
82                72  [1531-5169]   
83                72  [1531-5169]   
84                72  [1531-5169]   
85                73  [0148-9267]   
86                73  [0148-9267]   
164              151           []   
165              152  [0133-3720]   
166              153           []   
297              273  [0303-4569]   
298              274  [1439-0272]   
299              274  [1439-0272]   
300              274  [1439-0272]   
301              274  [1439-0272]   
302              274  [1439-0272]   
320              291           []   
321              292  [0009-4633]   
322              293  [1558-0407]   
342              313  [0031-5710]   
343              314  [0091-0260]   
344              315  [0033-3638]   
...              ...          ...   
211577        173183  [1573-7233]   
211578        173183  [1573-7233]   
211579        173183  [1573-7233]   
211602        173204  [0723-0869]   
211603        173205  [1878-0792]   
211604        173205  [1878-0792]   
211625        173223  [1537-1719]   
211626        173224  [0737-4038]   
211647        173244  [0029-4810]   
211648        173245  [1096-0961]   
211649        173245  [1096-0961]   
211650        173246  [0006-5242]   
211651        173247  [1432-0584]   
211652        173247  [1432-0584]   
211653        173247  [1432-0584]   
211654        173248           []   
211655        173249  [0939-5555]   
211656        173250  [1430-2772]   
211657        173250  [1430-2772]   
211658        173250  [1430-2772]   
211659        173250  [1430-2772]   
211660        173251  [1279-8509]   
211661        173251  [1279-8509]   
211662        173252  [1079-9796]   
211663        173253           []   
211664        173254  [0340-4684]   
211665        173255  [1269-3286]   
211666        173256  [0033-3026]   
211684        173273  [0131-6095]   
211685        173274           []   

                                        ISSN_cluster            MMS_ID  \
0                  [0000-0787, 0000-0469, 0000-0019]  9937257820001701   
1                  [2150-4008, 0094-257X, 0000-0019]  9967008940001701   
2                  [0000-0787, 0000-0469, 0000-0019]  9913446020001701   
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
29                                       [0713-3936]  9953497050001701   
30                            [0713-3936, 1929-7084]  9975244382301701   
78                            [1531-5169, 0148-9267]  9968959840001701   
79                            [1531-5169, 0148-9267]  9968959840001701   
80                            [1531-5169, 0148-9267]  9968959840001701   
81                            [1531-5169, 0148-9267]  9968959840001701   
82                            [1531-5169, 0148-9267]  9968959840001701   
83                            [1531-5169, 0148-9267]  9968959840001701   
84                            [1531-5169, 0148-9267]  9968959840001701   
85                            [1531-5169, 0148-9267]  9946998200001701   
86                            [1531-5169, 0148-9267]  9946998200001701   
164                                               []  9974762623801701   
165                                      [0133-3720]  9957941200001701   
166                                      [0133-3720]  9926650440001701   
297                                      [0303-4569]  9931505200001701   
298                           [1439-0272, 0303-4569]  9967779320001701   
299                           [1439-0272, 0303-4569]  9967779320001701   
300                           [1439-0272, 0303-4569]  9967779320001701   
301        

In [354]:
df_with_ranges.to_pickle('df_with_date_ranges-20180702.pkl')
df_with_ranges.to_csv('df_with_date_ranges-20180702.txt', sep='\t')

In [355]:
df_with_ranges.columns

Index(['record_index', 'ISSN_bib', 'ISSN_cluster', 'MMS_ID', 'OCN',
       'OCN_cluster', 'Title_bib', 'chron', 'descr', 'e_holdings', 'enum',
       'p_or_e', 'ISSN_group_id', 'OCN_group_id', 'both_groups',
       'matches_group_id', 'MMS ID', 'Item PID', 'Barcode', 'Enum_item',
       'Chron_item', 'Descr_item', 'Permanent Library', 'Permanent Location',
       'Electronic Collection Id', 'Public Name', 'MMS Id', 'Title_portfolio',
       'Begin Publication Date', 'End Publication Date', 'ISSN_portfolio',
       'Coverage Information Combined', 'Coverage Statement', 'Portfolio Id',
       'Lifecycle', 'Embargo Operator', 'Embargo Months', 'Embargo Years',
       'Status (Active)', 'PCAD?', 'ISSN_to_match', 'ISSN Number_BTAA-SPR',
       'Title 1 (Print)_BTAA-SPR', 'Publisher (Print)_BTAA-SPR',
       'Title 2 (Print)_BTAA-SPR', 'Publisher (Print).1_BTAA-SPR',
       'Title 3 (Print)_BTAA-SPR', 'Publisher (Print).2_BTAA-SPR',
       '(more bib records?)_BTAA-SPR', 'Match?_BTAA-SPR',
 

In [361]:
has_preservation = df_with_ranges[(df_with_ranges['Earliest Year Preserved_PORTICO'].notnull()) | df_with_ranges['SPR Holdings_BTAA-SPR'].notnull()]
has_preservation

record_index     ISSN_bib  \
3                  3  [0000-0019]   
29                24  [0713-3936]   
85                73  [0148-9267]   
86                73  [0148-9267]   
165              152  [0133-3720]   
297              273  [0303-4569]   
321              292  [0009-4633]   
343              314  [0091-0260]   
416              378  [1063-0279]   
508              457  [0737-8831]   
539              487  [0007-7712]   
540              488  [0007-7712]   
541              488  [0007-7712]   
616              554  [0263-6484]   
716              641  [0091-7370]   
797              718  [0268-005X]   
839              758  [2321-0230]   
840              758  [2321-0230]   
985              897  [0030-0071]   
1278            1184  [0013-5984]   
1564            1458  [0264-1615]   
1594            1486  [0003-4436]   
1657            1545  [0262-8104]   
1661            1549  [0094-7776]   
1788            1657  [0161-8628]   
1790            1659  [0161-8628]   
1839            1703  [1356-336X]   
1876            1740  [0094-3312]   
1971            1826  [0141-0423]   
1972            1826  [0141-0423]   
...              ...          ...   
210922        172605  [0003-987X]   
210943        172624  [0108-7673]   
210944        172625  [0365-110X]   
210981        172654  [0250-832X]   
211023        172690  [0035-1571]   
211089        172751  [0074-7696]   
211151        172804  [0737-0008]   
211180        172833  [0737-0016]   
211190        172841  [0044-2992]   
211263        172911  [0737-1209]   
211288        172931  [0942-9352]   
211315        172957  [0362-1340]   
211316        172957  [0362-1340]   
211317        172957  [0362-1340]   
211321        172961  [1523-2867]   
211340        172980  [1082-6742]   
211367        173006  [0040-5809]   
211373        173009  [0091-5521]   
211400        173023  [0884-0040]   
211401        173023  [0884-0040]   
211402        173024  [1551-6970]   
211413        173030  [1069-3971]   
211498        173109  [0891-5245]   
211574        173180  [0737-3937]   
211576        173182  [0167-7659]   
211602        173204  [0723-0869]   
211626        173224  [0737-4038]   
211655        173249  [0939-5555]   
211662        173252  [1079-9796]   
211684        173273  [0131-6095]   

                                        ISSN_cluster            MMS_ID  \
3       [0000-0469, 2150-4008, 0094-257X, 0000-0019]  9934112930001701   
29                                       [0713-3936]  9953497050001701   
85                            [1531-5169, 0148-9267]  9946998200001701   
86                            [1531-5169, 0148-9267]  9946998200001701   
165                                      [0133-3720]  9957941200001701   
297                                      [0303-4569]  9931505200001701   
321                                      [0009-4633]  9941025140001701   
343                                      [0091-0260]  9954506180001701   
416                                      [1063-0279]  9929194750001701   
508                                      [0737-8831]  9913435680001701   
539                                      [0007-7712]  9946099960001701   
540                                      [0007-7712]  9969467070001701   
541                                      [0007-7712]  9969467070001701   
616                           [1099-0844, 0263-6484]  9923819210001701   
716                           [0095-8905, 0091-7370]  9914421780001701   
797                                      [0268-005X]  9923318270001701   
839                           [2321-7472, 2321-0230]  9975302097601701   
840                           [2321-7472, 2321-0230]  9975302097601701   
985                                      [0030-0071]  9918440590001701   
1278                                     [0013-5984]  9928272270001701   
1564                          [0140-2773, 0264-1615]  9957941990001701   
1594                          [1281-7082, 0003-4436]  9933285490001701   
1657       

In [362]:
has_preservation['Permanent Library'].unique()

array([nan, 'ZMLAC', 'TWILS', 'TSCI', 'TMAGR', 'TAND', 'TCOS', 'MBRIG',
       'TZDS', 'TBIOM', 'DUMD', 'TVET', 'TARCH', 'TMATH', 'TBWAN', 'TNRL',
       'TLAKE', 'TJOUR'], dtype=object)

In [363]:
has_preservation['Permanent Location'].unique()

array([nan, 'OWL', 'PER', 'PERC', 'MSSLT', 'STF', 'SN1', 'CARN', 'NONX',
       'MPL', 'GEN', 'UMDN', 'CBIM', 'UMDPD', 'UMD', 'AMEJ', 'GOVU',
       'CBI', 'MANN', 'UMDBK', 'UMDRC', 'REF', 'SWHG', 'CLS', 'CLRP'],
      dtype=object)

In [372]:
has_pres_TSCI_TZDS = has_preservation[has_preservation['Permanent Library'].isin(['TSCI','TZDS'])]
has_pres_TSCI_TZDS

record_index     ISSN_bib                       ISSN_cluster  \
16383          14108  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16384          14109  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16385          14110  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16386          14111  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16387          14112  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16388          14113  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16389          14114  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16390          14115  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16391          14116  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16392          14117  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16393          14118  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16394          14119  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16395          14120  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16396          14121  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16397          14122  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16398          14123  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16399          14124  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16400          14125  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16401          14126  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16402          14127  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16403          14128  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16404          14129  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16405          14130  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16406          14131  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16407          14132  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16408          14133  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16409          14134  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16410          14135  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16411          14136  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16412          14137  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
...              ...          ...                                ...   
195715        159241  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195716        159242  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195717        159243  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195718        159244  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195719        159245  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195720        159246  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195726        159248  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195727        159249  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195728        159250  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195729        159251  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195730        159252  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195731        159253  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195732        159254  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195733        159255  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195734        159256  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195735        159257  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195736        159258  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195737        159259  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195738        159260  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195739        159261  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195740        159262  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195741        159263  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195742        159264  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195743        159265  [1434-6060]  [1434-6079, 1

In [373]:
set_for_walter_basement = has_pres_TSCI_TZDS[((has_pres_TSCI_TZDS['Permanent Library'] == 'TSCI')& 
                                              (has_pres_TSCI_TZDS['Permanent Location'] == 'PER')) | 
                                             (has_pres_TSCI_TZDS['Permanent Library'] == 'TZDS')]
set_for_walter_basement

record_index     ISSN_bib                       ISSN_cluster  \
16383          14108  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16384          14109  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16385          14110  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16386          14111  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16387          14112  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16388          14113  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16389          14114  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16390          14115  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16391          14116  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16392          14117  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16393          14118  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16394          14119  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16395          14120  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16396          14121  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16397          14122  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16398          14123  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16399          14124  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16400          14125  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16401          14126  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16402          14127  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16403          14128  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16404          14129  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16405          14130  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16406          14131  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16407          14132  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16408          14133  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16409          14134  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16410          14135  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16411          14136  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16412          14137  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
...              ...          ...                                ...   
195715        159241  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195716        159242  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195717        159243  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195718        159244  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195719        159245  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195720        159246  [0178-7683]  [0178-7683, 0340-2193, 1155-4312]   
195726        159248  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195727        159249  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195728        159250  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195729        159251  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195730        159252  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195731        159253  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195732        159254  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195733        159255  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195734        159256  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195735        159257  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195736        159258  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195737        159259  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195738        159260  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195739        159261  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195740        159262  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195741        159263  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195742        159264  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195743        159265  [1434-6060]  [1434-6079, 1

In [375]:
set_for_walter_basement.columns

Index(['record_index', 'ISSN_bib', 'ISSN_cluster', 'MMS_ID', 'OCN',
       'OCN_cluster', 'Title_bib', 'chron', 'descr', 'e_holdings', 'enum',
       'p_or_e', 'ISSN_group_id', 'OCN_group_id', 'both_groups',
       'matches_group_id', 'MMS ID', 'Item PID', 'Barcode', 'Enum_item',
       'Chron_item', 'Descr_item', 'Permanent Library', 'Permanent Location',
       'Electronic Collection Id', 'Public Name', 'MMS Id', 'Title_portfolio',
       'Begin Publication Date', 'End Publication Date', 'ISSN_portfolio',
       'Coverage Information Combined', 'Coverage Statement', 'Portfolio Id',
       'Lifecycle', 'Embargo Operator', 'Embargo Months', 'Embargo Years',
       'Status (Active)', 'PCAD?', 'ISSN_to_match', 'ISSN Number_BTAA-SPR',
       'Title 1 (Print)_BTAA-SPR', 'Publisher (Print)_BTAA-SPR',
       'Title 2 (Print)_BTAA-SPR', 'Publisher (Print).1_BTAA-SPR',
       'Title 3 (Print)_BTAA-SPR', 'Publisher (Print).2_BTAA-SPR',
       '(more bib records?)_BTAA-SPR', 'Match?_BTAA-SPR',
 

In [378]:
walter_groups = set_for_walter_basement['matches_group_id'].unique().tolist()
walter_groups

[11058,
 23860,
 26444,
 28512,
 30472,
 30757,
 33593,
 41516,
 43527,
 43752,
 45605,
 46661,
 50639,
 54323,
 55588,
 57461,
 61186,
 64832,
 66069,
 68844,
 70193,
 71110,
 71367,
 78203,
 81767,
 82687,
 86124,
 86615,
 86779,
 93879,
 100603]

In [379]:
walter_groups_df = df[df['matches_group_id'].isin(walter_groups)]
walter_groups_df

record_index     ISSN_bib                       ISSN_cluster  \
16382          14107  [1521-0634]  [2331-4168, 1521-0634, 1040-7782]   
16383          14108  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16384          14109  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16385          14110  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16386          14111  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16387          14112  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16388          14113  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16389          14114  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16390          14115  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16391          14116  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16392          14117  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16393          14118  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16394          14119  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16395          14120  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16396          14121  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16397          14122  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16398          14123  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16399          14124  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16400          14125  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16401          14126  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16402          14127  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16403          14128  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16404          14129  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16405          14130  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16406          14131  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16407          14132  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16408          14133  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16409          14134  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16410          14135  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
16411          14136  [1040-7790]  [1040-7790, 0149-5720, 1521-0626]   
...              ...          ...                                ...   
195725        159247  [1434-6036]  [1434-6028, 1434-6036, 1286-4862]   
195726        159248  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195727        159249  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195728        159250  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195729        159251  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195730        159252  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195731        159253  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195732        159254  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195733        159255  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195734        159256  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195735        159257  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195736        159258  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195737        159259  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195738        159260  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195739        159261  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195740        159262  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195741        159263  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195742        159264  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195743        159265  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195744        159266  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195745        159267  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195746        159268  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195747        159269  [1434-6060]  [1434-6079, 1155-4312, 1434-6060]   
195748        159270  [1434-6060]  [1434-6079, 1

In [380]:
walter_groups_df.to_pickle('walter_groups-20180702.pkl')
walter_groups_df.to_csv('walter_groups-20180702.txt', sep='\t')